## Importazione librerie

In [1]:
import string
import sys
import io 
import os
import nltk
import pandas as pd
import numpy as np
import os
from collections import Counter
from gensim.models import Word2Vec
from cade.cade import CADE
import treetaggerwrapper

C:\ProgramData\Anaconda3\lib\site-packages\treetaggerwrapper.py:739: FutureWarning: Possible nested set at position 8
  punct2find_re = re.compile("([^ ])([[" + ALONEMARKS + "])",
C:\ProgramData\Anaconda3\lib\site-packages\treetaggerwrapper.py:2043: FutureWarning: Possible nested set at position 152
  DnsHostMatch_re = re.compile("(" + DnsHost_expression + ")",
C:\ProgramData\Anaconda3\lib\site-packages\treetaggerwrapper.py:2067: FutureWarning: Possible nested set at position 409
  UrlMatch_re = re.compile(UrlMatch_expression, re.VERBOSE | re.IGNORECASE)
C:\ProgramData\Anaconda3\lib\site-packages\treetaggerwrapper.py:2079: FutureWarning: Possible nested set at position 192
  EmailMatch_re = re.compile(EmailMatch_expression, re.VERBOSE | re.IGNORECASE)


### Definizione path

In [2]:
path_letterario_w2v = "C:/Users/cafe6/Università degli Studi di Milano-Bicocca/g.carbone8@campus.unimib.it - data/Models/fasi_letterarie/frasi_NON_lemmatizzate_bigrammi/w2v"

path_letterario_cade = "C:/Users/cafe6/Università degli Studi di Milano-Bicocca/g.carbone8@campus.unimib.it - data/Models/fasi_letterarie/frasi_NON_lemmatizzate_bigrammi/CADE"

path_autori_w2v = "C:/Users/cafe6/Università degli Studi di Milano-Bicocca/g.carbone8@campus.unimib.it - data/Models/autori/frasi_NON_lemmatizzate_bigrammi/w2v"

path_autori_cade = "C:/Users/cafe6/Università degli Studi di Milano-Bicocca/g.carbone8@campus.unimib.it - data/Models/autori/frasi_NON_lemmatizzate_bigrammi/CADE"

### Definizione funzioni

In [3]:
# Funzione per calcolare la frequenza dei topos nei modelli

def topos_frequencies(words: list, n_mod: int, text: str):
    
    embeddings = []
    for k in range(n_mod):
        model = Word2Vec.load(text + '_' + str(k) + '.model') #adattare nome
        embeddings.append(model) #ottengo una lista contenente gli n modelli per il testo desiderato
    
    topos_freq = dict()
    
    for k in range(n_mod):
        for word in words:
            if word not in topos_freq.keys():
                topos_freq[word] = embeddings[k].wv.get_vecattr(word, "count")
            else:
                topos_freq[word] += embeddings[k].wv.get_vecattr(word, "count")
    
    return topos_freq

In [4]:
# Funzione che estrae le n parole più simili ad una parola target, calcolando la similarità media per un dato numero di modelli

def similar_words_per_topos(word, n_mod, n_words, text):
        #parola target, numero di modelli, numero di parole simili da estrarre, corpus da analizzare
    text_2 = text
    text = text.lower()
    
    #ottengo gli n modelli del testo considerato
    embeddings = []
    for k in range(n_mod):
        model = Word2Vec.load(text + '_' + str(k) + '.model') #adattare nome
        embeddings.append(model) #ottengo una lista contenente gli n modelli per il testo desiderato
        
    #modello per modello, ottengo la lista delle m parole (n_words) più simili al target
    words = []
    for k in range(n_mod):
        for tupla in embeddings[k].wv.most_similar(word)[:n_words]: #ottengo una lista di tuple (parola, similarità)
            words.append(tupla[0]) #appendo solamente la parola, senza considerare il valore di similarità rispetto al target
        
    #creo un dizionario che presenta le parole uniche contenute nella lista "words", e le rispettive frequenze assolute
    c = Counter(words)
    word_frequencies = dict(c)
    
    #creo un dizionario che contiene la lista di parole uniche in "words" e calcola la similarità media di ciascuna di esse
    init = [0] * len(np.unique(words))
    word_similarities = dict(zip(np.unique(words), init))

    for k in range(n_mod):
        for tupla in embeddings[k].wv.most_similar(word)[:n_words]:
            word_similarities[tupla[0]] += tupla[1]
    for word in np.unique(words):
        word_similarities[word] = word_similarities[word] / word_frequencies[word]

    #trasformo il dizionario con le frequenze assolute e quello con le similarità medie in dataframe, e li unisco
    df_1 = pd.DataFrame(list(word_frequencies.items()), columns=['Words','Abs.frequency'])
    df_2 = pd.DataFrame(list(word_similarities.items()), columns=['Words','Med.similarity'])
  
    #calcolo anche la similarità normalizzata, nel caso dovesse servie
    normalized_similarity = (df_2['Med.similarity']-df_2['Med.similarity'].min())/(df_2['Med.similarity'].max() - df_2['Med.similarity'].min()) 
    df = pd.merge(df_1, df_2, on = 'Words')
    df['Med.similarity(norm.)'] = normalized_similarity

    #aggiungo la colonna col nome del testo considerato
    df['Text'] = [text_2] * len(df)
    
    return df

In [5]:
# Funzioni per estrarre, per una parola target, le parole più simili appartenenti a una specifica categoria grammaticale (nomi,
# aggettivi, ...)

def find_similar(word: str, n_similar: int, n_mod:int, pos_tag_prefix: str, models: list) -> list:
    #parola da analizzare, numero di parole simili volute, numero modelli, prefisso POS desiderato, lista dei modelli
    most_similar = dict()
    
    #ottengo la lista delle n parole simili alla parola target filtrando per il POS tag desiderato
    for k in range(n_mod):
        similar = models[k].wv.most_similar(word, topn=(5*n_similar)) #moltiplico per avere un campione più ampio
        similar_filtered = list(filter(lambda similar: check_pos_tag(similar[0], pos_tag_prefix), similar))

    #combino le parole ottenute dai vari modelli
    for (string, similarity) in similar_filtered:
        if string not in most_similar.keys():
            most_similar[string] = similarity
        else:
            most_similar[string] = max(most_similar[string], similarity)

    #ordino le parole in base alla similarità e seleziono solo il numero desiderato
    similar_filtered_sorted = sorted(most_similar.items(), key=lambda item: item[1], reverse=True)[:n_similar]
    similar_final = [w for (w, sim) in similar_filtered_sorted]
    
    return similar_final

In [6]:
# Funzione utile in quella precedente, che definisce il "part-of-speech" tag
tagger = treetaggerwrapper.TreeTagger(TAGLANG='it')

def check_pos_tag(word: str, tag_prefix: str) -> bool:
    tag = tagger.tag_text(word)
    part_of_speech = treetaggerwrapper.make_tags(tag)
    return part_of_speech[0].pos.startswith(tag_prefix)

In [7]:
# Declinazione della funzione generale per trovare i sinonimi

def find_synonyms(word: str, n_synonyms: int, n_mod: int, models: list) -> list:
    return find_similar(word, n_synonyms, n_mod, 'NOM', models) #controllare che il tag sia giusto

# Declinazione della funzione generale per trovare gli aggettivi descrittivi

def find_describing_adjectives(words: list, n_adjectives: int, n_mod: int, models: list) -> None:
    #in questo caso passo come argomento la lista contenente i sinonimi
    for word in words:
        print(find_similar(word, n_adjectives, n_mod, 'ADJ', models))

In [32]:
# Funzione per comparare una parola fra embedding diversi

def compare_word_btw_embeddings(word_to_study, n_mod, text1, text2):
    #parola da studiare, numero di embedding creati per corpus, testo preso come riferimento (da cui estraggo il vettore della
    #parola target), testo da cui estraggo le parole simili
    
    #prendo il numero totale di embedding dei due testi considerati
    embeddings1 = []
    for it in range(n_mod):
        model = Word2Vec.load(text1 + '_' + str(it) + '.model') #sistemare il nome se necessario
        embeddings1.append(model)
        
    embeddings2 = []
    for it in range(n_mod):
        model = Word2Vec.load(text2 + '_' + str(it) + '.model')
        embeddings2.append(model)

    #ottengo la lista delle parole più simili alla target per ciascun modello
    words = []
    for k in range(n_mod):
        word_vector = embeddings1[k].wv[word_to_study]
        for tupla in embeddings2[k].wv.most_similar(positive=[word_vector])[:10]: #modificare a piacere il numero
            words.append(tupla[0])
    
    #creo dizionario con parole uniche e relativa frequenza assoluta
    c = Counter(words)
    word_frequencies = dict(c)
    
    #creo dizionario con parole uniche calcolando la similarità media
    init = [0] * len(np.unique(words))
    word_similarities = dict(zip(np.unique(words), init))
    
    for k in range(n_mod):
        word_vector = embeddings1[k].wv[word_to_study]
        for tupla in embeddings2[k].wv.most_similar(positive=[word_vector])[:10]:
            word_similarities[tupla[0]] += tupla[1]
    
    for word in np.unique(words):
        word_similarities[word] = word_similarities[word] / word_frequencies[word]
  
    #genero il dataframe finale
    df = pd.DataFrame(list(word_similarities.items()), columns=['Words','Med.similarity'])
    df = df.sort_values(by=['Med.similarity'], ascending=False)
    df = df.head(n=10)
    
    return df

# ANALISI WORD2VEC

## ANALISI PER FASE LETTERARIA

In [9]:
os.chdir(path_letterario_w2v)
lista_periodi_letterari = ['1_duecento_poetica_e_prosa Medievo', '2_dolce_stil_novo', '3_petrarchismo', 
                           '4_boccaccio_e_umanesimo', '5_manierismo_e_barocco', '6_classicismo_arcadia', 
                           '7_illuminismo_neoclassicismo', '8_romanticismo', '9_verismo', '10_decadentismo', 
                           '11_avanguardie_primo_novecento', '12_neorealismo']

### TOPOS: PASTORE

In [10]:
for periodo in lista_periodi_letterari:
    try:
        print("###" + periodo + "###")
        df_periodo = similar_words_per_topos("pastore", 5, 10, periodo)
        print(df_periodo[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + periodo)

###1_duecento_poetica_e_prosa Medievo###
La chiave non esiste nel modello1_duecento_poetica_e_prosa Medievo
###2_dolce_stil_novo###
La chiave non esiste nel modello2_dolce_stil_novo
###3_petrarchismo###
La chiave non esiste nel modello3_petrarchismo
###4_boccaccio_e_umanesimo###
           Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0     elfigluolo              5        0.806757               0.244444
1          ovile              4        0.803879               0.178272
2        heliseo              2        0.796115               0.105780
3      domenicho              5        0.792372               0.454916
4          paris              1        0.800022               0.523871
5      conspecto              1        0.799406               0.461820
6      sacerdote              2        0.797732               0.304249
7     consecrato              1        0.797198               0.753389
8            eva              4        0.802448               0.494121
9   elmino

             Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0        mandriano              5        0.694221               0.384583
1        pescatore              5        0.677394               0.079711
2        contadino              5        0.667689               0.492063
3       melchiorre              5        0.671619               0.051512
4           zuanne              5        0.678526               0.557552
5       cacciatore              1        0.663761               0.211489
6   vecchiopastore              5        0.652815               0.050594
7          basilio              2        0.639034               1.000000
8           basile              2        0.657316               0.623096
9            servo              1        0.639063               0.008604
10         nuorese              1        0.649099               0.247559
11           predu              2        0.638299               0.135760
12       pancraziu              1        0.642395  

### Altre parole correlate

In [11]:
for periodo in lista_periodi_letterari:
    try:
        print("###" + periodo + "###")
        df_periodo = similar_words_per_topos("pastori", 5, 10, periodo)
        print(df_periodo[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + periodo)

###1_duecento_poetica_e_prosa Medievo###
La chiave non esiste nel modello1_duecento_poetica_e_prosa Medievo
###2_dolce_stil_novo###
La chiave non esiste nel modello2_dolce_stil_novo
###3_petrarchismo###
La chiave non esiste nel modello3_petrarchismo
###4_boccaccio_e_umanesimo###
             Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0            balli              3        0.818722               0.450810
1           greggi              5        0.837263               0.375738
2          volanti              1        0.829197               0.455057
3          cantano              5        0.821078               0.000000
4        altissimi              5        0.820952               0.612259
5           fructi              3        0.814365               0.317466
6        splendide              2        0.819697               0.229038
7           teatri              1        0.814002               0.009089
8            porci              3        0.819851              

         Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0    lavoranti              2        0.733488               0.911037
1      paesani              4        0.725683               0.344627
2      agnelli              5        0.730976               0.380157
3       gregge              5        0.725974               0.239415
4         tori              3        0.716112               0.800504
5     capretti              5        0.727074               0.000000
6        porci              5        0.734117               0.524844
7        ovili              3        0.722004               0.769356
8      banditi              2        0.712234               0.594671
9      nuoresi              1        0.706910               0.982183
10  mendicanti              2        0.727666               0.797855
11       lepri              1        0.726981               0.817262
12   guardiani              4        0.719807               0.229359
13   giovenche              1     

### TOPOS: AMORE

In [12]:
for periodo in lista_periodi_letterari:
    try:
        print("###" + periodo + "###")
        df_periodo = similar_words_per_topos("amore", 5, 10, periodo)
        print(df_periodo[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + periodo)

###1_duecento_poetica_e_prosa Medievo###
       Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0      servo              5        0.946097               0.448241
1       solo              5        0.935064               0.626854
2      amare              5        0.933991               0.000000
3      sente              5        0.921397               0.331082
4      matto              5        0.936987               0.238349
5    cortese              5        0.924395               0.358444
6      perde              4        0.924240               0.284246
7    potenza              3        0.919240               0.230184
8      laude              1        0.921122               0.312181
9        ama              3        0.928196               0.719222
10    dolore              2        0.922876               0.326290
11    cresce              1        0.925283               0.172160
12     crede              3        0.921387               0.238671
13  malvagio         

        Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0      verace              5        0.828206               0.909620
1       finto              1        0.815702               0.897856
2     affetto              4        0.825517               0.425543
3       nasca              3        0.814596               0.592645
4      geloso              2        0.810955               0.649747
5       cieca              2        0.816089               0.122169
6      stolta              5        0.819230               0.000000
7       error              2        0.811006               0.421733
8       farti              3        0.817783               0.590784
9      indole              2        0.814655               0.649579
10        ama              2        0.825168               0.579618
11    rimorso              2        0.804708               0.420045
12      anima              1        0.811119               0.014536
13     presta              1        0.809473    

### Altre parole correlate

In [13]:
for periodo in lista_periodi_letterari:
    try:
        print("###" + periodo + "###")
        df_periodo = similar_words_per_topos("amor", 5, 10, periodo)
        print(df_periodo[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + periodo)

###1_duecento_poetica_e_prosa Medievo###
      Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0      gioi              5        0.993857               0.708710
1     merzé              5        0.994574               0.471168
2     senza              5        0.990563               0.374791
3       meo              5        0.990041               0.336904
4   madonna              3        0.990759               0.536081
5       sol              2        0.989458               0.000000
6        en              2        0.988572               0.203222
7     lasso              1        0.988563               0.309554
8      noia              4        0.989023               0.231394
9     gioia              2        0.989274               0.904882
10      for              1        0.988785               0.296362
11   pregio              2        0.989682               0.202043
12     core              4        0.989579               0.493483
13    dolce              1        0

        Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0      duolmi              5        0.899653               0.403335
1    chieggio              2        0.888293               1.000000
2       rendi              2        0.886866               0.275352
3   lasciarti              5        0.894406               0.238514
4       eppur              1        0.884863               0.000000
5     abborre              5        0.892599               0.763919
6       speri              2        0.887124               0.024042
7      dovevi              1        0.882690               0.673338
8         mel              1        0.882281               0.107253
9      deggia              1        0.882061               0.610213
10       temo              3        0.896651               0.552510
11    incarco              2        0.896496               0.472495
12  scongiuro              1        0.892743               0.008403
13      bramo              3        0.889255    

            Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0         perdoni              5        0.856423               0.309786
1          domine              5        0.820732               0.184377
2        benedica              5        0.840078               0.791971
3            gesú              5        0.823384               0.665157
4          carità              5        0.830115               0.378034
5       liberanos              1        0.807713               0.545736
6          davide              3        0.807556               0.579487
7       perdonami              5        0.804314               0.128800
8         perdona              1        0.777855               0.380024
9          lavorà              2        0.787975               0.286806
10  angelocustode              3        0.792341               0.095122
11     panebianco              1        0.785329               0.000000
12          saulo              1        0.783628               0

In [14]:
for periodo in lista_periodi_letterari:
    try:
        print("###" + periodo + "###")
        df_periodo = similar_words_per_topos("innamorato", 5, 10, periodo)
        print(df_periodo[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + periodo)

###1_duecento_poetica_e_prosa Medievo###
La chiave non esiste nel modello1_duecento_poetica_e_prosa Medievo
###2_dolce_stil_novo###
La chiave non esiste nel modello2_dolce_stil_novo
###3_petrarchismo###
La chiave non esiste nel modello3_petrarchismo
###4_boccaccio_e_umanesimo###
          Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0         adone              5        0.843208               0.334556
1     inamorato              5        0.839064               1.000000
2       siccheo              5        0.828807               0.380023
3          amai              2        0.819103               0.472386
4      servente              5        0.828671               0.409449
5      parlante              2        0.814535               0.488154
6       accorta              2        0.816046               0.496633
7      pulcella              2        0.808899               0.323836
8     vedendola              2        0.816509               0.194670
9    vergognosa     

              Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0        innamorata              5        0.671559               0.227398
1           riamata              5        0.662399               0.658416
2           ingenuo              5        0.662750               0.517103
3        entusiasta              2        0.644061               0.242926
4      perdutamente              5        0.640521               0.445714
5      intelligente              1        0.650401               0.442233
6             adora              3        0.638369               0.359896
7            amasse              5        0.650814               0.278437
8          ammirato              2        0.639036               0.280575
9      giovanissimo              1        0.642637               0.326768
10        fiducioso              1        0.640561               0.794942
11           geloso              4        0.640653               0.000000
12     riconoscente              1    

### TOPOS: CHIESA

In [15]:
for periodo in lista_periodi_letterari:
    try:
        print("###" + periodo + "###")
        df_periodo = similar_words_per_topos("chiesa", 5, 10, periodo)
        print(df_periodo[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + periodo)

###1_duecento_poetica_e_prosa Medievo###
          Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0          pure              2        0.989605               0.552570
1          oggi              3        0.989770               0.904383
2    altragente              3        0.991673               0.620664
3      fannogli              3        0.987771               0.436544
4        ardono              2        0.987969               0.403675
5      dimorano              1        0.985743               0.455195
6       trebuto              3        0.988181               0.155407
7        dicovi              4        0.988117               0.484266
8        istare              1        0.984513               0.411502
9         sonvi              4        0.990010               0.881843
10        tende              1        0.992430               0.000000
11      intorno              1        0.991495               0.528593
12         olio              1        0.991017   

            Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0       monastero              5        0.680683               0.154433
1          chiese              5        0.647360               0.545915
2        cappella              5        0.637265               0.651497
3          ergere              5        0.607868               0.233165
4   metropolitano              4        0.601285               0.107126
5          cristo              3        0.595310               0.187894
6      santamaria              5        0.603122               0.141648
7         diocesi              4        0.603033               0.238463
8         monache              3        0.594374               0.169619
9           duomo              5        0.598611               0.097340
10      patriarca              3        0.589227               1.000000
11      benedetto              1        0.599833               0.043502
12       convento              1        0.607361               0

### Altre parole correlate

In [16]:
for periodo in lista_periodi_letterari:
    try:
        print("###" + periodo + "###")
        df_periodo = similar_words_per_topos("papa", 5, 10, periodo)
        print(df_periodo[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + periodo)

###1_duecento_poetica_e_prosa Medievo###
             Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0           colore              1        0.992724               0.428563
1      duefrategli              5        0.992983               0.990329
2        cavalcare              2        0.990820               0.437417
3             olio              1        0.990971               1.000000
4          comandò              2        0.990344               0.395687
5       alessandro              1        0.989730               0.555382
6             acri              3        0.989660               0.769305
7             osti              1        0.989519               0.217091
8             andò              2        0.990665               0.575028
9        riverenza              1        0.988995               0.650181
10            alau              4        0.994110               0.738238
11          domini              3        0.991660               0.815414
12        

           Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0      pontefice              5        0.619750               0.000000
1     successore              3        0.561001               0.289622
2    gregoriovii              3        0.554491               0.304159
3      cardinali              5        0.559615               0.234122
4      scomunicò              5        0.549660               0.140299
5      patriarca              5        0.546430               0.200125
6       concilio              2        0.546975               0.033628
7   giovannixxii              3        0.537945               0.229081
8       antipapa              2        0.535098               0.052023
9         papale              2        0.538016               0.166243
10      clemente              4        0.560846               0.034464
11       vescovi              2        0.567224               0.133857
12  innocenzoiii              1        0.539502               0.106961
13   c

In [17]:
for periodo in lista_periodi_letterari:
    try:
        print("###" + periodo + "###")
        df_periodo = similar_words_per_topos("prete", 5, 10, periodo)
        print(df_periodo[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + periodo)

###1_duecento_poetica_e_prosa Medievo###
La chiave non esiste nel modello1_duecento_poetica_e_prosa Medievo
###2_dolce_stil_novo###
La chiave non esiste nel modello2_dolce_stil_novo
###3_petrarchismo###
La chiave non esiste nel modello3_petrarchismo
###4_boccaccio_e_umanesimo###
             Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0               ni              5        0.787783               0.530453
1           notaro              5        0.800323               0.315008
2   bastianocoiaio              5        0.802281               0.000000
3             mulo              5        0.795777               1.000000
4            costì              2        0.781857               0.138989
5          manderò              2        0.786835               0.544800
6          pierino              5        0.788536               0.491909
7        instantia              2        0.787240               0.322199
8      cancelliero              3        0.783983              

          Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0    cappellano              5        0.748154               0.026383
1        momolo              3        0.715956               0.173902
2       compare              2        0.718519               0.202896
3     heribrand              4        0.724420               0.233666
4          orso              5        0.724445               0.203720
5        paolon              2        0.717892               1.000000
6       puttini              1        0.718395               0.237107
7      caporale              1        0.717222               0.325037
8       bottajo              1        0.717190               0.131636
9   viaggiatore              3        0.720426               0.274121
10   giovinotto              1        0.726039               0.347324
11    servitore              1        0.722824               0.430696
12     maràbito              1        0.718936               0.032045
13      burbero     

In [18]:
for periodo in lista_periodi_letterari:
    try:
        print("###" + periodo + "###")
        df_periodo = similar_words_per_topos("frate", 5, 10, periodo)
        print(df_periodo[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + periodo)

###1_duecento_poetica_e_prosa Medievo###
        Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0    possente              3        0.989234               0.661396
1    prodezza              1        0.987706               0.585965
2      corona              2        0.987022               0.779170
3      vedete              4        0.987503               0.461275
4      dritto              5        0.988514               0.341779
5     apresso              3        0.987881               0.283846
6        fate              3        0.987514               0.642341
7         fra              3        0.990491               0.591933
8        tien              1        0.985647               0.551448
9          du              4        0.988318               0.385458
10     leanza              4        0.989787               1.000000
11         lu              3        0.988656               0.195605
12    laudato              1        0.989482               0.548729
13     

La chiave non esiste nel modello6_classicismo_arcadia
###7_illuminismo_neoclassicismo###
             Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0     plenipotente              5        0.874748               0.168436
1              fue              2        0.854391               0.374164
2             avia              1        0.847691               0.003343
3             isso              1        0.845774               0.353080
4            peché              2        0.845349               0.006226
5         nocierto              5        0.843995               0.151763
6          senator              4        0.853297               0.321528
7           morone              2        0.843153               0.343048
8           messer              5        0.862188               0.342781
9            prete              4        0.852956               0.513268
10         diacono              2        0.847272               0.117643
11        ambrogio              3  

In [19]:
for periodo in lista_periodi_letterari:
    try:
        print("###" + periodo + "###")
        df_periodo = similar_words_per_topos("dio", 5, 10, periodo)
        print(df_periodo[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + periodo)

###1_duecento_poetica_e_prosa Medievo###
        Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0      grazia              5        0.923889               0.138208
1    speranza              5        0.904497               0.121799
2    sapienza              5        0.871445               0.406782
3      tenuto              5        0.869047               0.223794
4      cristo              5        0.882226               0.026303
5   peccatore              1        0.871597               1.000000
6      dunque              1        0.869374               0.000000
7       opera              3        0.863228               0.136284
8       santa              1        0.866918               0.100647
9   volontade              1        0.866610               0.184431
10   prossimo              1        0.887367               0.255442
11    peccati              3        0.866609               0.076610
12     poveri              1        0.877668               0.341885
13     

         Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0        onore              4        0.679890               0.100323
1        sacro              5        0.678502               1.000000
2        unico              4        0.674056               0.337630
3     giudizio              4        0.655827               0.466220
4       cristo              4        0.654548               0.619441
5     creatore              5        0.681409               0.186116
6        falli              2        0.656229               0.399745
7          ira              1        0.654957               0.379070
8    riverenza              2        0.650292               0.369161
9   obbedienza              1        0.652737               0.356872
10       iddio              4        0.655328               0.347705
11     custode              1        0.665976               0.292965
12     sincero              1        0.649696               0.962552
13     zelante              1     

In [20]:
for periodo in lista_periodi_letterari:
    try:
        print("###" + periodo + "###")
        df_periodo = similar_words_per_topos("cristo", 5, 10, periodo)
        print(df_periodo[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + periodo)

###1_duecento_poetica_e_prosa Medievo###
         Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0        beati              5        0.962287               0.345382
1     vangelio              5        0.961501               0.552657
2     superbia              3        0.953098               0.146588
3       poveri              5        0.960530               1.000000
4   favellando              4        0.953123               0.622488
5    scrittura              5        0.960019               0.000000
6      profeta              5        0.956740               0.544180
7     apostoli              1        0.951428               0.244853
8        iddio              5        0.951222               0.541033
9        anime              1        0.946396               0.293167
10     peccati              4        0.951146               0.927614
11       paolo              3        0.943956               0.771506
12      gloria              1        0.938012               0.

La chiave non esiste nel modello6_classicismo_arcadia
###7_illuminismo_neoclassicismo###
              Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0   romanopontefice              5        0.787120               0.608735
1         arciprete              4        0.766000               0.417713
2   ponteficeromano              1        0.769966               0.000000
3             nicea              2        0.769813               0.515464
4           martire              2        0.761978               0.238672
5       pubblicasse              2        0.762387               0.205661
6         appostoli              4        0.761739               0.270904
7      predicazione              1        0.763599               0.211187
8         ortatoria              1        0.761723               0.537584
9          dichiarò              1        0.761694               0.452457
10   sommopontefice              2        0.761247               0.416672
11       conservata    

                Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0             vescovo              5        0.772224               0.177790
1                gesù              5        0.713489               0.075514
2          doncamillo              5        0.681281               0.000000
3               giuda              5        0.675740               0.318650
4              bacchi              5        0.662480               0.114314
5        spiritosanto              2        0.662709               0.559950
6             michele              1        0.651547               0.277132
7         severamente              1        0.648973               0.095879
8   risposesorridendo              5        0.645823               0.133959
9          donmariano              3        0.654008               0.287731
10         monsignore              2        0.656630               0.038799
11       rabbisolomon              4        0.653288               0.108920
12          

### TOPOS: FELICITA'

In [21]:
for periodo in lista_periodi_letterari:
    try:
        print("###" + periodo + "###")
        df_periodo = similar_words_per_topos("felicità", 5, 10, periodo)
        print(df_periodo[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + periodo)

###1_duecento_poetica_e_prosa Medievo###
La chiave non esiste nel modello1_duecento_poetica_e_prosa Medievo
###2_dolce_stil_novo###
La chiave non esiste nel modello2_dolce_stil_novo
###3_petrarchismo###
La chiave non esiste nel modello3_petrarchismo
###4_boccaccio_e_umanesimo###
              Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0        infelicità              5        0.790204               0.240036
1           miseria              5        0.738061               0.151502
2      tranquillità              5        0.740254               0.032316
3             summa              4        0.735550               0.177168
4            sanità              5        0.721822               0.312956
5           povertà              3        0.725080               0.039559
6   famigliaalberta              1        0.716754               0.173308
7          virtuosa              3        0.712840               0.327902
8           assidua              2        0.714817    

             Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0        innocenza              5        0.718015               0.473007
1         rinunzia              4        0.703090               0.451820
2          fidente              5        0.714326               0.043149
3        sovrumana              4        0.697965               0.526567
4          suprema              4        0.690263               0.663757
5        illusione              1        0.681273               0.911919
6            oblio              1        0.678874               0.122886
7    creaturaumana              5        0.703930               0.313014
8       infelicità              2        0.683294               0.383056
9      aspirazione              3        0.695052               0.171131
10     incoscienza              1        0.692172               0.346795
11        pienezza              1        0.690700               1.000000
12       impotenza              2        0.689238  

### Altre parole correlate

In [22]:
for periodo in lista_periodi_letterari:
    try:
        print("###" + periodo + "###")
        df_periodo = similar_words_per_topos("gioia", 5, 10, periodo)
        print(df_periodo[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + periodo)

###1_duecento_poetica_e_prosa Medievo###
      Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0   madonna              5        0.989990               0.654818
1        ca              4        0.987494               0.569957
2      loco              5        0.989956               0.696734
3      gioi              5        0.989669               0.976232
4     senza              4        0.986531               0.000000
5      noia              5        0.987663               0.387829
6       cor              1        0.988230               0.944764
7      amor              5        0.987987               0.994245
8       meo              2        0.987579               1.000000
9        en              2        0.986438               0.584532
10     core              4        0.989852               0.184765
11    merzé              4        0.985260               0.599054
12    dolce              3        0.984188               0.403883
13  sovente              1        0

        Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0        gelo              5        0.965190               0.389913
1        vene              5        0.962510               0.541223
2       provò              5        0.960397               0.457536
3       gioco              3        0.955924               0.650859
4    nascosto              4        0.958743               0.871281
5       desta              4        0.958409               0.487172
6      divide              4        0.962690               0.470609
7   traditore              1        0.956294               1.000000
8        alma              1        0.956280               0.522867
9      catena              1        0.954655               0.502345
10     ignoto              3        0.955525               0.668046
11   palpitar              3        0.954866               0.362396
12    palpita              3        0.952807               0.468420
13      gelar              2        0.954909    

           Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0       felicità              5        0.798506               0.377398
1       vergogna              5        0.783767               0.000000
2     malinconia              5        0.778734               0.636239
3      sconforto              4        0.778666               0.364576
4      delusione              4        0.772250               0.226826
5       angoscia              3        0.772780               0.451578
6       dolcezza              5        0.796523               0.952028
7   disperazione              3        0.775845               1.000000
8        rimorso              5        0.764232               0.309611
9        miseria              1        0.762898               0.521504
10     disperata              2        0.766558               0.138239
11   umiliazione              1        0.777338               0.170520
12        ardore              1        0.783475               0.519847
13    

### TOPOS: PATRIA/ITALIA

In [23]:
for periodo in lista_periodi_letterari:
    try:
        print("###" + periodo + "###")
        df_periodo = similar_words_per_topos("patria", 5, 10, periodo)
        print(df_periodo[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + periodo)

###1_duecento_poetica_e_prosa Medievo###
La chiave non esiste nel modello1_duecento_poetica_e_prosa Medievo
###2_dolce_stil_novo###
         Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0        poeti              3        0.998649               0.476205
1   igualmente              3        0.998249               1.000000
2     chiamati              3        0.998460               0.715647
3       truova              2        0.998220               0.825573
4     chiamato              4        0.998565               0.453532
5         modi              3        0.998655               0.764918
6       ovidio              4        0.998369               0.767036
7         savi              1        0.998176               0.274511
8        fuoco              1        0.998099               0.338545
9         vere              1        0.998094               0.786408
10     invidia              2        0.998617               0.536938
11  giovinezza              1        0.9

           Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0         grecia              5        0.708655               0.938693
1       alfredde              5        0.706761               0.580588
2    conversione              3        0.698390               0.230989
3         musset              5        0.692690               0.345253
4         tirolo              1        0.701158               0.535221
5     cancellato              5        0.688427               0.054022
6          asilo              1        0.695698               0.275614
7     redenzione              4        0.690806               0.667743
8        posteri              1        0.692973               0.691815
9     queiluoghi              2        0.693734               1.000000
10       ispagna              3        0.694798               0.551458
11        esilio              3        0.699134               0.430963
12        orrori              1        0.695678               0.483221
13    

In [24]:
for periodo in lista_periodi_letterari:
    try:
        print("###" + periodo + "###")
        df_periodo = similar_words_per_topos("italia", 5, 10, periodo)
        print(df_periodo[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + periodo)

###1_duecento_poetica_e_prosa Medievo###
La chiave non esiste nel modello1_duecento_poetica_e_prosa Medievo
###2_dolce_stil_novo###
          Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0        regina              4        0.998824               0.624592
1         tolta              1        0.998912               0.487377
2       rivolsi              1        0.998831               0.206712
3        misera              2        0.998865               0.175973
4           dèi              2        0.998903               0.763291
5      signoria              1        0.998762               0.260989
6          esta              2        0.998801               0.896495
7       costume              2        0.998764               0.390852
8         figli              1        0.998737               0.196614
9   gentildonna              1        0.998721               0.607366
10     faccendo              1        0.999061               0.000000
11       difesa             

             Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0          narsete              5        0.686644               0.570636
1         germania              5        0.675387               0.265825
2        belisario              5        0.681813               0.888707
3         pannonia              5        0.684394               0.249640
4             goti              5        0.674541               0.565732
5           ottone              5        0.673455               0.740681
6   costantinopoli              2        0.654071               0.721206
7       vestrogoti              3        0.652549               0.178111
8           spagne              2        0.649771               1.000000
9          ravenna              2        0.658786               0.696170
10    delongobardi              2        0.667792               0.948176
11         alboino              2        0.668005               0.358267
12         augusto              2        0.654774  

### Altre parole correlate

In [25]:
for periodo in lista_periodi_letterari:
    try:
        print("###" + periodo + "###")
        df_periodo = similar_words_per_topos("stato", 5, 10, periodo)
        print(df_periodo[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + periodo)

###1_duecento_poetica_e_prosa Medievo###
        Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0       grave              5        0.977860               0.041683
1      stesso              5        0.963869               0.589087
2       penso              1        0.967525               0.583714
3       matto              1        0.967178               0.000000
4       certo              5        0.967583               0.445537
5       gioco              1        0.963993               1.000000
6    villania              1        0.963916               0.191015
7       perde              1        0.963403               0.303717
8    saccente              1        0.961493               0.051533
9      penare              2        0.961985               0.572885
10      vista              1        0.960107               0.013100
11  sembiante              1        0.958456               0.176315
12      mette              1        0.957260               0.490758
13     

             Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0         prospero              5        0.764731               0.172564
1          notizie              5        0.737144               0.205340
2         tuttavia              5        0.744828               0.172758
3         presente              5        0.714895               0.210885
4           salute              5        0.744770               0.226745
5           ottimo              5        0.692877               0.115433
6         lasciato              4        0.683111               0.738644
7     irregolarità              4        0.681437               0.319261
8            volte              1        0.688089               0.527860
9        curiosità              1        0.680852               1.000000
10       informato              4        0.677413               0.158080
11        migliore              3        0.671362               0.810892
12           trova              1        0.659178  

           Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0   signorperelà              5        0.942247               0.000000
1     matrimonio              5        0.944686               0.293681
2         dunque              1        0.945989               0.506440
3         marito              3        0.937487               0.205834
4           oggi              5        0.940053               0.871589
5         voluto              1        0.938619               0.713705
6         saputo              1        0.933769               0.270440
7         invece              1        0.933637               1.000000
8         essere              1        0.933503               0.321452
9         doveva              1        0.932564               0.328711
10          dato              4        0.943627               0.537952
11     possibile              4        0.941933               0.929166
12      soltanto              2        0.937939               0.668216
13    

In [26]:
for periodo in lista_periodi_letterari:
    try:
        print("###" + periodo + "###")
        df_periodo = similar_words_per_topos("impero", 5, 10, periodo)
        print(df_periodo[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + periodo)

###1_duecento_poetica_e_prosa Medievo###
La chiave non esiste nel modello1_duecento_poetica_e_prosa Medievo
###2_dolce_stil_novo###
La chiave non esiste nel modello2_dolce_stil_novo
###3_petrarchismo###
La chiave non esiste nel modello3_petrarchismo
###4_boccaccio_e_umanesimo###
           Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0        merzede              3        0.923847               0.000000
1        indutto              4        0.923083               0.577202
2       contenda              1        0.922817               0.767322
3            ave              3        0.920797               0.654775
4         peccar              2        0.920946               0.636850
5          vanti              3        0.920867               0.503920
6           odia              3        0.916156               0.904394
7          fruir              3        0.918824               1.000000
8       chiamerò              1        0.918875               0.692459
9         

                   Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0             differente              1        0.876618               0.042775
1         formaartistica              4        0.863854               0.331789
2              femminino              1        0.871063               0.000000
3              riproduce              5        0.871191               0.523356
4               estetico              3        0.865341               0.401253
5               sviluppa              1        0.865772               0.536216
6              conflitto              2        0.863729               0.488764
7        formaletteraria              3        0.861862               0.899660
8              modernità              3        0.867398               0.402824
9            costituisce              2        0.867292               0.654938
10              organico              1        0.865207               0.337320
11         ogniindividuo              1        0.864

In [27]:
for periodo in lista_periodi_letterari:
    try:
        print("###" + periodo + "###")
        df_periodo = similar_words_per_topos("nazione", 5, 10, periodo)
        print(df_periodo[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + periodo)

###1_duecento_poetica_e_prosa Medievo###
La chiave non esiste nel modello1_duecento_poetica_e_prosa Medievo
###2_dolce_stil_novo###
La chiave non esiste nel modello2_dolce_stil_novo
###3_petrarchismo###
La chiave non esiste nel modello3_petrarchismo
###4_boccaccio_e_umanesimo###
               Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0         esercitato              5        0.747179               1.000000
1       tantapotenza              5        0.732304               0.155222
2       nomefranzese              2        0.728461               0.372154
3      moltevittorie              3        0.729043               0.485280
4           deturchi              2        0.725583               0.271574
5          celebrato              2        0.728629               0.431439
6            plebeio              3        0.731814               0.179666
7   degnitàimperiale              4        0.727391               0.259947
8           prìncipi              2        0.

                Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0              nazion              5        0.626101               0.058315
1       nazioneintera              5        0.627803               0.000000
2          incivilire              3        0.590209               0.088068
3       politicamente              5        0.602854               0.386132
4           nazionale              5        0.595712               0.146179
5      conquistatrice              4        0.598753               0.167025
6           feudalitá              2        0.596989               0.348865
7             nobiltá              5        0.595193               0.205594
8         linguacolta              1        0.590670               0.215337
9         cristianità              1        0.587398               0.159910
10  civiltàuniversale              2        0.584648               0.281439
11        mondocivile              3        0.593799               0.230368
12     civil

In [28]:
for periodo in lista_periodi_letterari:
    try:
        print("###" + periodo + "###")
        df_periodo = similar_words_per_topos("bandiera", 5, 10, periodo)
        print(df_periodo[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + periodo)

###1_duecento_poetica_e_prosa Medievo###
La chiave non esiste nel modello1_duecento_poetica_e_prosa Medievo
###2_dolce_stil_novo###
La chiave non esiste nel modello2_dolce_stil_novo
###3_petrarchismo###
            Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0           rotta              5        0.991580               0.925504
1        campagna              3        0.989454               0.823134
2       spronando              5        0.990834               0.323431
3           ariva              4        0.990872               0.595934
4          abatte              4        0.991282               0.468615
5         schiere              2        0.990004               0.598728
6            urta              2        0.988484               0.030381
7         discese              1        0.989293               0.428236
8        mordante              3        0.988957               0.834794
9        bandiere              3        0.988873               0.395154
10   

               Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0             trofeo              5        0.775698               0.337306
1   santissimocristo              2        0.758263               0.194124
2             cometa              4        0.764265               0.042755
3              cervo              3        0.753541               0.366487
4             apollo              2        0.752521               0.673098
5          guerriero              2        0.765422               0.588751
6         sanmichele              3        0.748228               0.249013
7        larghissimo              3        0.748651               0.135241
8             blocco              2        0.747513               0.471762
9            vertice              1        0.750194               0.206353
10         rivestito              1        0.768724               0.706182
11              cono              3        0.761315               0.226664
12            eretto     

### TOPOS: GUERRA

In [29]:
for periodo in lista_periodi_letterari:
    try:
        print("###" + periodo + "###")
        df_periodo = similar_words_per_topos("guerra", 5, 10, periodo)
        print(df_periodo[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + periodo)

###1_duecento_poetica_e_prosa Medievo###
        Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0      venuta              4        0.971151               0.705470
1     apresso              5        0.968975               0.398005
2      affare              4        0.965888               0.878207
3         fra              3        0.959601               0.126664
4       basso              1        0.955545               0.693536
5        fuor              1        0.955013               0.000000
6   messaggio              4        0.959273               0.306714
7       parea              2        0.957525               0.353664
8          du              1        0.953281               0.096888
9    possente              3        0.956884               0.554424
10      infra              3        0.961061               0.435367
11      monta              2        0.961328               0.448559
12     matera              1        0.965881               0.705077
13    l

       Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0      venti              5        0.912436               0.026991
1    spoglie              5        0.906849               0.136678
2      vento              4        0.907417               0.000000
3      sfere              4        0.903243               0.429307
4    perigli              3        0.903299               0.543753
5        fur              4        0.903249               0.639475
6     trofei              1        0.916361               0.485919
7        vie              2        0.905916               0.215205
8      regni              3        0.904357               0.364741
9   procelle              2        0.900443               0.545504
10    grecia              4        0.906000               0.446134
11     lacci              3        0.901587               0.582324
12      nevi              1        0.893807               0.543554
13      fumo              2        0.899960               0.84

          Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0     futurista              5        0.943617               0.232986
1       società              5        0.919818               0.274069
2       libertà              5        0.929393               0.301476
3   rivoluzione              5        0.919936               0.000000
4         razza              4        0.910726               0.345922
5         paese              3        0.916533               1.000000
6          cioè              2        0.914045               0.227628
7         amore              3        0.911145               0.664003
8        poichè              2        0.909376               0.210655
9          oggi              1        0.912105               0.107456
10        senso              1        0.912682               0.255642
11      nazioni              3        0.910200               0.360246
12    futuristi              2        0.910919               0.191182
13       numero     

### TOPOS: FIGURA FEMMINILE

In [30]:
for periodo in lista_periodi_letterari:
    try:
        print("###" + periodo + "###")
        df_periodo = similar_words_per_topos("donna", 5, 10, periodo)
        print(df_periodo[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + periodo)

###1_duecento_poetica_e_prosa Medievo###
      Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0     gioia              3        0.980356               0.535651
1        en              1        0.981063               0.373657
2       meo              4        0.979531               0.217427
3      loco              2        0.979035               0.442879
4   madonna              5        0.979037               0.000000
5       par              5        0.978623               1.000000
6      gioi              1        0.978433               0.475085
7      amor              3        0.978696               0.483948
8        ca              5        0.977870               0.861272
9      ched              4        0.977074               0.602184
10      tal              3        0.978340               0.602453
11      cor              3        0.978223               0.699475
12    senza              2        0.976218               0.895548
13      ver              3        0

         Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0         dama              5        0.565626               0.026848
1      femmina              5        0.584152               0.359753
2    fanciulla              5        0.575713               0.784792
3       orfana              2        0.558044               0.637139
4      ragazza              4        0.563784               0.545512
5       pudica              4        0.558164               0.834713
6       strega              4        0.553657               1.000000
7        sposo              3        0.558744               0.291379
8        elina              1        0.560948               0.470652
9      nutrice              2        0.541333               0.161309
10      costei              4        0.573165               0.488629
11      moglie              2        0.557126               0.490973
12  contessina              3        0.551464               0.601057
13       suora              1     

In [31]:
for periodo in lista_periodi_letterari:
    try:
        print("###" + periodo + "###")
        df_periodo = similar_words_per_topos("madre", 5, 10, periodo)
        print(df_periodo[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + periodo)

###1_duecento_poetica_e_prosa Medievo###
           Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0          adamo              5        0.954619               0.769439
1       apostoli              5        0.961064               1.000000
2           dopo              5        0.952885               0.217002
3            eva              5        0.945992               0.707431
4     gesùcristo              5        0.941839               0.460871
5   spiritosanto              4        0.942256               0.200100
6     favellando              3        0.938702               0.312283
7    onnipotente              1        0.933108               0.155297
8     jesùcristo              4        0.937450               0.357780
9      peccatori              4        0.940246               0.000000
10           job              4        0.943110               0.255332
11        ventre              3        0.936315               0.327230
12     volontade              1     

          Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0        figlia              5        0.905385               0.201235
1        persia              4        0.870908               0.000000
2       augusta              4        0.875249               0.482918
3         amata              2        0.858832               0.132417
4        licida              5        0.863107               0.143929
5            ii              4        0.869789               0.303949
6         sposo              4        0.858360               1.000000
7          real              2        0.866762               0.177636
8       germano              1        0.849212               0.042622
9       genitor              2        0.849588               0.127770
10      istante              1        0.859751               0.036172
11   pastorella              1        0.858484               0.389245
12  principessa              2        0.854611               0.244776
13        creta     

        Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0       nonna              5        0.646064               0.221045
1       terni              5        0.594884               0.037331
2       paola              5        0.620264               0.119413
3       mamma              5        0.607836               0.000000
4    natalina              5        0.602364               0.260210
5         zia              5        0.604338               0.049944
6      figlia              5        0.592538               0.109998
7    casorati              1        0.582351               0.471641
8        mary              1        0.579084               0.339469
9     miranda              1        0.576681               0.074266
10    sorella              4        0.598826               0.041052
11  mariarosa              1        0.598273               0.396011
12      balbo              1        0.589704               1.000000
13      serva              1        0.581552    

In [32]:
for periodo in lista_periodi_letterari:
    try:
        print("###" + periodo + "###")
        df_periodo = similar_words_per_topos("femmina", 5, 10, periodo)
        print(df_periodo[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + periodo)

###1_duecento_poetica_e_prosa Medievo###
           Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0       creatura              5        0.961320               0.077585
1        soffera              5        0.950343               0.582647
2       apostolo              5        0.939322               0.208704
3         toglie              5        0.929185               0.336164
4          viene              2        0.919311               1.000000
5   dicesalamone              5        0.931485               0.121861
6        angioli              2        0.912700               0.433967
7         ventre              1        0.909160               0.297738
8          colla              5        0.926330               0.333889
9         poveri              1        0.908611               0.348917
10       diventa              4        0.926210               0.297613
11        imperò              2        0.927002               0.134977
12      disiderj              3     

              Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0            femina              5        0.760032               0.374301
1        stracciona              5        0.736278               0.323235
2     buonafamiglia              3        0.727198               0.123790
3       figliaunica              3        0.722692               0.000000
4    mariamaddalena              3        0.730081               0.327909
5        figlioccia              2        0.719815               0.659550
6        marianoina              3        0.727380               0.190984
7             matta              1        0.717970               1.000000
8        castellana              1        0.717522               0.230346
9           puledra              1        0.717457               0.171052
10     duefigliuole              2        0.720782               0.122175
11          maschio              4        0.726325               0.132457
12          zingara              1    

In [33]:
for periodo in lista_periodi_letterari:
    try:
        print("###" + periodo + "###")
        df_periodo = similar_words_per_topos("sposa", 5, 10, periodo)
        print(df_periodo[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + periodo)

###1_duecento_poetica_e_prosa Medievo###
            Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0          grazie              2        0.992806               0.495006
1             dae              3        0.992396               0.592431
2   apparecchiato              4        0.991983               0.419183
3         accidia              3        0.991447               0.855239
4          merito              1        0.991735               0.000000
5           sposo              3        0.993619               0.621740
6        disidero              2        0.990900               0.591849
7        passione              3        0.992133               0.667691
8      dolcissimo              5        0.994224               0.571041
9           tieni              1        0.990324               0.395606
10   consolazione              2        0.992144               1.000000
11          dalli              3        0.991865               0.742162
12           muta      

      Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0     sposo              5        0.969445               0.282325
1    licori              5        0.954115               0.000000
2     vanne              5        0.951109               0.046361
3   germano              5        0.943032               0.075431
4     corri              5        0.942900               0.346729
5      enea              5        0.938451               0.362735
6     barce              4        0.942233               0.255925
7     sofia              3        0.940449               0.054540
8     vieni              5        0.941817               0.365897
9     alceo              1        0.939550               0.140304
10  augusto              1        0.930932               0.631984
11   prence              2        0.941109               0.319751
12    iarba              1        0.933635               0.303898
13   figlia              1        0.930062               1.000000
14  ascolt

         Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0        elena              5        0.849483               0.244758
1          zia              5        0.843967               0.373009
2       cugina              5        0.847673               0.959228
3   margherita              5        0.836921               0.496373
4   governante              2        0.838706               1.000000
5     duchessa              5        0.827130               0.313076
6       regina              5        0.824685               0.757185
7       figlia              3        0.818995               0.716961
8      cognata              1        0.815963               0.325219
9         olga              3        0.827041               0.119411
10       sposo              2        0.831285               0.012530
11      nubile              3        0.819742               0.329910
12    consorte              2        0.821655               0.494362
13      monaca              1     

### TOPOS: NOTTE/SERA

In [34]:
for periodo in lista_periodi_letterari:
    try:
        print("###" + periodo + "###")
        df_periodo = similar_words_per_topos("notte", 5, 10, periodo)
        print(df_periodo[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + periodo)

###1_duecento_poetica_e_prosa Medievo###
       Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0     sicché              2        0.974070               0.279257
1       olio              3        0.975920               0.248313
2      morta              4        0.975023               0.885664
3      ferro              4        0.979513               0.329388
4    vivanda              4        0.976423               0.409489
5    credere              4        0.973696               0.371203
6      caldo              3        0.972972               0.707564
7     chiesa              1        0.974358               0.658013
8     poteva              2        0.977380               0.203837
9       mese              2        0.977411               0.784714
10     tanti              2        0.977001               0.000000
11  sollazzo              2        0.973158               0.586054
12      alto              2        0.972105               0.447976
13   andasse         

         Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0      soletto              5        0.809112               0.396995
1        barca              5        0.796728               0.735097
2       trombe              5        0.785508               0.132952
3           lì              4        0.787940               0.213174
4       stento              5        0.779298               0.559574
5       fretta              4        0.778367               0.342362
6        furia              4        0.783162               0.444929
7       grotta              4        0.774429               0.258128
8        palme              4        0.771151               0.199868
9      cocchio              1        0.772328               0.547132
10  tempestosa              1        0.762362               0.187993
11        sera              2        0.771089               0.186670
12       bosco              2        0.768577               1.000000
13     discese              2     

In [35]:
for periodo in lista_periodi_letterari:
    try:
        print("###" + periodo + "###")
        df_periodo = similar_words_per_topos("sera", 5, 10, periodo)
        print(df_periodo[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + periodo)

###1_duecento_poetica_e_prosa Medievo###
           Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0       talvolta              4        0.994714               0.509037
1           nero              3        0.993490               0.613248
2          manda              3        0.993927               0.227110
3          panno              2        0.994294               0.009307
4           alta              3        0.993812               0.506499
5           armi              2        0.993329               0.233386
6        andasse              3        0.992066               0.000000
7         lasciò              1        0.991855               0.191950
8         andava              1        0.991081               1.000000
9       volevano              2        0.992150               0.350902
10         collo              1        0.995561               0.508497
11       làentro              2        0.993258               0.180454
12          mese              2     

              Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0           silesia              5        0.959186               0.464348
1           mattina              5        0.954301               0.299891
2              mese              1        0.956041               0.315689
3         settimana              2        0.952383               0.362901
4            laudon              4        0.954067               0.703102
5            dimani              4        0.953476               0.706369
6         vicinanze              5        0.956786               0.299834
7           general              1        0.952584               0.660502
8          tavolino              2        0.952820               0.736769
9         terminato              1        0.951174               0.383355
10         corriere              1        0.953412               0.290361
11            festa              2        0.945571               0.418573
12           lunedì              3    

### Altre parole correlate:

In [36]:
for periodo in lista_periodi_letterari:
    try:
        print("###" + periodo + "###")
        df_periodo = similar_words_per_topos("tenebre", 5, 10, periodo)
        print(df_periodo[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + periodo)

###1_duecento_poetica_e_prosa Medievo###
La chiave non esiste nel modello1_duecento_poetica_e_prosa Medievo
###2_dolce_stil_novo###
La chiave non esiste nel modello2_dolce_stil_novo
###3_petrarchismo###
         Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0       gratia              3        0.997924               0.511210
1        fuggo              5        0.997853               0.701877
2        grido              1        0.997888               1.000000
3        pasce              1        0.997887               0.431103
4        quali              2        0.997687               0.342621
5      stagion              2        0.997989               0.356286
6        sorda              2        0.997522               0.649971
7     occhimei              3        0.997589               0.695444
8      alberga              3        0.997934               0.672072
9       uomini              1        0.997471               0.302653
10        sòle              2        0

         Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0   crepuscolo              5        0.749782               0.005611
1        ombre              5        0.729168               0.241388
2        lampi              4        0.704676               0.236654
3       luridi              3        0.696751               0.292182
4       nebbie              3        0.705781               0.224285
5     notturna              5        0.711575               0.090400
6      susurro              4        0.715778               1.000000
7       baleno              4        0.702122               0.031340
8      faville              1        0.702640               0.244952
9         bujo              1        0.701350               0.277558
10      nuvola              1        0.705231               0.150626
11      ardori              1        0.702418               0.303812
12    chiarore              1        0.692990               0.295254
13  alternando              1     

In [37]:
for periodo in lista_periodi_letterari:
    try:
        print("###" + periodo + "###")
        df_periodo = similar_words_per_topos("ombra", 5, 10, periodo)
        print(df_periodo[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + periodo)

###1_duecento_poetica_e_prosa Medievo###
La chiave non esiste nel modello1_duecento_poetica_e_prosa Medievo
###2_dolce_stil_novo###
       Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0      mercé              1        0.997403               0.668132
1       posa              1        0.997400               0.164947
2   speranza              2        0.997243               0.847454
3       dole              1        0.997124               0.173143
4    nessuna              2        0.997371               0.451990
5       cara              1        0.997043               0.230433
6       sete              3        0.997141               0.815263
7       arte              1        0.997032               0.005393
8       velo              1        0.996951               0.803924
9     fretta              4        0.997479               0.483777
10     lieta              2        0.997903               0.597953
11       puo              2        0.997368               0.1578

         Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0      rimirar              4        0.942134               0.723643
1       stassi              3        0.941396               0.870346
2        orror              3        0.940701               0.770176
3         muta              1        0.943946               0.928809
4         alma              1        0.942223               0.724958
5     splendor              2        0.935077               1.000000
6      beltade              4        0.943276               0.017849
7        tosco              4        0.939041               0.492573
8      auretta              1        0.940418               0.564773
9        errar              3        0.936719               0.636922
10     securtà              2        0.944395               0.510931
11     alberga              2        0.939580               0.966013
12    mormorar              2        0.935749               0.321823
13       porgi              1     

          Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0        sagoma              5        0.749840               0.641854
1       tenebra              1        0.743103               0.465176
2         alone              4        0.736703               0.429940
3    illuminato              5        0.737739               0.192918
4       spariva              3        0.724254               0.695000
5      filtrava              2        0.720236               0.000000
6      striscia              3        0.731217               0.670090
7          rupe              2        0.731359               0.387258
8      riflesso              5        0.740181               0.191283
9       schermo              1        0.722535               0.826514
10     bagliore              1        0.730223               0.736660
11       smorta              3        0.727141               0.839460
12      sgombro              3        0.725703               0.496165
13     illumina     

### TOPOS: FORTUNA

In [38]:
for periodo in lista_periodi_letterari:
    try:
        print("###" + periodo + "###")
        df_periodo = similar_words_per_topos("fortuna", 5, 10, periodo)
        print(df_periodo[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + periodo)

###1_duecento_poetica_e_prosa Medievo###
         Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0       gentil              3        0.997725               0.769684
1       amanti              2        0.996955               0.266918
2       tuttor              1        0.996207               0.354565
3        laido              3        0.996196               0.520369
4        mando              2        0.996305               0.975532
5   dispiacere              2        0.996121               0.761217
6       poiché              5        0.996568               0.119234
7        pensi              1        0.995748               0.537650
8      gentile              2        0.995080               1.000000
9         deve              3        0.995567               0.208923
10        move              3        0.995856               0.000000
11      stella              1        0.995186               0.221071
12         han              1        0.995121               0.

           Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0         sicuri              5        0.847931               0.673940
1        massime              5        0.831487               0.151280
2    ragionevoli              1        0.836809               0.025000
3     venerabili              5        0.830834               0.649708
4         giusti              2        0.833886               0.668291
5           rari              2        0.840683               0.503697
6         povere              1        0.833034               0.496814
7      distingue              5        0.830149               0.288132
8          utili              1        0.831861               0.700850
9         esempi              2        0.822736               0.672251
10  lodevolmente              1        0.838024               0.723326
11      soggetti              1        0.832705               0.281969
12         varia              2        0.821243               0.569719
13    

            Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0        carriera              5        0.697600               0.295336
1       rifiutata              4        0.682956               0.999931
2      negoziante              4        0.690309               0.000000
3         donnina              3        0.691443               0.025082
4     reputazione              5        0.683665               0.822569
5     qualcheanno              1        0.697603               0.485632
6     sicurissimo              3        0.679359               0.962764
7         ginetta              4        0.679074               0.540494
8     sentitodire              1        0.688888               0.466287
9          tutore              2        0.678654               0.241362
10       prestare              1        0.685422               0.789917
11     potràesser              3        0.678803               0.458491
12        eredità              2        0.679745               0

### TOPOS: NOIA

In [39]:
for periodo in lista_periodi_letterari:
    try:
        print("###" + periodo + "###")
        df_periodo = similar_words_per_topos("noia", 5, 10, periodo)
        print(df_periodo[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + periodo)

###1_duecento_poetica_e_prosa Medievo###
       Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0      senza              3        0.996218               0.655327
1        vil              2        0.995292               0.519304
2      dolor              5        0.995730               0.638932
3     savere              4        0.996137               0.218506
4        ahi              2        0.995097               0.761833
5      aggio              2        0.995414               0.790834
6      nente              2        0.995095               0.832713
7       amar              1        0.995376               0.380277
8      dolze              2        0.995828               0.175265
9       fera              1        0.994773               0.582300
10     dolce              3        0.995663               0.394729
11      sete              2        0.995304               0.531162
12     merto              4        0.995297               0.156532
13     magno         

           Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0        sedurmi              2        0.978527               0.746175
1       ritrarre              5        0.978015               0.297991
2        risenta              3        0.978859               0.554447
3     tolleranza              2        0.977355               0.160707
4      soverchio              1        0.976216               0.692454
5    dissimulare              3        0.976940               0.494813
6         troppa              1        0.975435               0.789526
7       sollievo              1        0.975026               0.480787
8         fisico              1        0.974126               0.673869
9    buonaequità              4        0.976545               0.459992
10        rarità              4        0.977932               0.106425
11     discapito              1        0.974254               0.036652
12     liberarmi              2        0.973990               0.465874
13    

              Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0            attori              3        0.998421               0.406551
1            docile              1        0.998267               0.118942
2            rivela              1        0.998236               0.554913
3          ritratti              1        0.998198               0.552715
4            facili              1        0.998187               0.536461
5            lucido              1        0.998161               0.621832
6        spettacoli              2        0.998441               0.727953
7           livello              1        0.998111               0.147547
8           compito              1        0.998095               0.182748
9       apparizione              1        0.998072               0.178820
10            crema              2        0.998420               0.636950
11          carcere              1        0.998476               0.551393
12             nodo              1    

### TOPOS: TEMPORALE/PIOGGIA

In [40]:
for periodo in lista_periodi_letterari:
    try:
        print("###" + periodo + "###")
        df_periodo = similar_words_per_topos("temporale", 5, 10, periodo)
        print(df_periodo[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + periodo)

###1_duecento_poetica_e_prosa Medievo###
La chiave non esiste nel modello1_duecento_poetica_e_prosa Medievo
###2_dolce_stil_novo###
La chiave non esiste nel modello2_dolce_stil_novo
###3_petrarchismo###
La chiave non esiste nel modello3_petrarchismo
###4_boccaccio_e_umanesimo###
                 Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0           spirituale              5        0.889075               0.199324
1           bencommune              2        0.825537               0.221406
2    alcunoparticulare              5        0.817338               0.141365
3        tantaautoritá              5        0.824548               0.190108
4           esterminio              2        0.814254               0.310397
5           diventasse              2        0.813316               0.317859
6          augumentare              1        0.814454               0.211679
7          esaltazione              2        0.810008               0.135978
8             mancassi     

             Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0   settimanasanta              5        0.805143               0.389469
1      carneficina              1        0.795200               0.426412
2          celebrò              1        0.794380               0.827056
3        pescarese              2        0.794121               0.206671
4        celebrata              1        0.789497               0.651568
5            troia              1        0.787443               0.659517
6       pestilenza              3        0.785235               0.464201
7         rovereto              1        0.785221               0.631429
8         luminare              1        0.783748               0.246095
9        ventilare              1        0.783547               0.477260
10           bruci              2        0.794968               0.409233
11         fiumano              2        0.789878               0.190109
12      novegiorni              3        0.788803  

In [41]:
for periodo in lista_periodi_letterari:
    try:
        print("###" + periodo + "###")
        df_periodo = similar_words_per_topos("pioggia", 5, 10, periodo)
        print(df_periodo[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + periodo)

###1_duecento_poetica_e_prosa Medievo###
La chiave non esiste nel modello1_duecento_poetica_e_prosa Medievo
###2_dolce_stil_novo###
      Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0      anni              1        0.998940               1.000000
1     trovo              1        0.998840               0.518434
2        mo              1        0.998792               0.584490
3       sen              2        0.998702               0.413806
4      sale              1        0.998765               0.673532
5      udir              1        0.998724               0.717874
6     selva              1        0.998680               0.821002
7    gridar              1        0.998655               0.436130
8      fore              1        0.998620               0.726977
9      temo              2        0.998459               0.600966
10     rota              2        0.998701               0.756725
11    serra              2        0.998644               0.387999
12    lett

         Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0        bosco              5        0.933980               0.399187
1        verno              3        0.937972               0.656525
2        tuono              4        0.937945               0.142362
3        punta              3        0.937484               0.670003
4       rapido              1        0.933138               0.922468
5     torrente              1        0.930537               0.649288
6       soffio              3        0.928418               0.472748
7         onda              3        0.931248               0.871668
8      soletto              3        0.933783               0.282278
9         nube              1        0.928557               0.096230
10       dorso              1        0.937071               0.790948
11        fumo              4        0.936480               0.528692
12     deserto              2        0.934136               0.189885
13        neve              1     

### TOPOS: GIOVINEZZA

In [42]:
for periodo in lista_periodi_letterari:
    try:
        print("###" + periodo + "###")
        df_periodo = similar_words_per_topos("giovinezza", 5, 10, periodo)
        print(df_periodo[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + periodo)

###1_duecento_poetica_e_prosa Medievo###
La chiave non esiste nel modello1_duecento_poetica_e_prosa Medievo
###2_dolce_stil_novo###
            Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0       cittadini              1        0.998628               0.484735
1           greco              2        0.998451               0.375397
2        seguendo              1        0.998338               0.462700
3            polo              2        0.998469               0.797593
4          romani              1        0.998170               0.744944
5          cinque              1        0.998125               0.530225
6           falsa              1        0.998123               1.000000
7            pari              1        0.998089               0.649674
8           palla              1        0.998028               0.564265
9     similemente              1        0.998019               0.360856
10          poeti              2        0.998610               0.534403
11  

           Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0       virilità              5        0.797426               0.538565
1     vecchiezza              5        0.780924               0.439526
2     giovanezza              5        0.774859               0.320653
3       infanzia              5        0.761711               0.021415
4      vecchiaja              4        0.761067               0.349900
5       gioconda              2        0.757334               0.242662
6         matura              5        0.766710               0.634063
7       gioconde              3        0.750721               0.420869
8        adorata              5        0.768969               0.501934
9    spensierata              4        0.765814               0.331579
10       ambasce              1        0.762861               0.000000
11        obblia              1        0.756204               0.487401
12      dolcezze              3        0.755530               0.410427
13  fa

In [43]:
for periodo in lista_periodi_letterari:
    try:
        print("###" + periodo + "###")
        df_periodo = similar_words_per_topos("giovane", 5, 10, periodo)
        print(df_periodo[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + periodo)

###1_duecento_poetica_e_prosa Medievo###
           Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0       lasciare              5        0.995353               0.211064
1       immagine              5        0.994517               0.418957
2        vincere              1        0.993811               0.330691
3        diritta              1        0.993772               0.205531
4        provare              1        0.993307               0.421184
5        perdere              3        0.992274               0.486639
6         averai              3        0.992903               0.305518
7         lodare              1        0.992570               0.370866
8        ricorda              1        0.992339               0.502672
9           llui              3        0.992735               0.170987
10        andate              4        0.993349               0.650186
11       vecchio              2        0.993654               0.815661
12         porre              1     

              Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0        metastasio              5        0.876116               0.635168
1        successore              4        0.864516               0.770427
2            mattei              4        0.864141               0.142434
3        dottissimo              4        0.870312               0.242797
4    signorgiuseppe              4        0.860787               0.828743
5             luzan              1        0.856026               0.747028
6           potenza              3        0.867207               0.712705
7           codesto              1        0.854660               0.283787
8              majo              1        0.854420               0.235583
9       maresciallo              2        0.861149               0.437589
10          vecchio              4        0.879882               0.527430
11              zio              2        0.868692               0.886950
12        ritornato              2    

           Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0       mezzaetà              5        0.682329               0.275361
1        robusto              5        0.695836               0.516892
2     giovanotto              5        0.667107               0.334193
3        anziana              5        0.666942               0.000000
4        maestra              3        0.650176               0.340768
5   intelligente              5        0.654692               0.081407
6          calvo              2        0.656015               0.519650
7      altomagro              1        0.652497               0.221664
8        ragazzo              3        0.647391               0.312068
9       tirolese              2        0.643599               0.236568
10       educato              4        0.656409               0.774165
11  giovanissimo              2        0.640897               0.189992
12  servizievole              4        0.650575               1.000000
13    

### TOPOS: BACIO

In [44]:
for periodo in lista_periodi_letterari:
    try:
        print("###" + periodo + "###")
        df_periodo = similar_words_per_topos("bacio", 5, 10, periodo)
        print(df_periodo[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + periodo)

###1_duecento_poetica_e_prosa Medievo###
La chiave non esiste nel modello1_duecento_poetica_e_prosa Medievo
###2_dolce_stil_novo###
La chiave non esiste nel modello2_dolce_stil_novo
###3_petrarchismo###
La chiave non esiste nel modello3_petrarchismo
###4_boccaccio_e_umanesimo###
           Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0         eccomi              5        0.936249               0.500829
1      prenderai              4        0.934293               0.403678
2    vaicercando              3        0.934396               0.525903
3        alceste              1        0.929491               0.736744
4         trarrò              2        0.927343               0.000000
5      peronella              2        0.928240               0.907621
6        celarsi              4        0.927878               0.614818
7       supplica              1        0.922086               0.559784
8           otta              1        0.921579               0.615229
9         

           Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0      abbraccio              5        0.695514               1.000000
1        carezza              5        0.626425               0.073457
2        baciare              5        0.635515               0.086268
3        guancia              5        0.594377               0.542269
4        baciato              2        0.574395               0.000000
5          baciò              2        0.567813               0.003505
6       baciasse              2        0.564893               0.075990
7           baci              5        0.574063               0.025774
8       baciarla              4        0.564434               0.472922
9          desti              4        0.580429               0.014333
10        baciai              4        0.575742               0.122028
11        ciocca              1        0.566313               0.228435
12       lagrima              1        0.568391               0.030189
13    

### TOPOS: LUNA

In [45]:
for periodo in lista_periodi_letterari:
    try:
        print("###" + periodo + "###")
        df_periodo = similar_words_per_topos("luna", 5, 10, periodo)
        print(df_periodo[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + periodo)

###1_duecento_poetica_e_prosa Medievo###
             Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0          montare              2        0.994183               0.440924
1          tornano              2        0.991333               0.000000
2          animali              4        0.991249               0.166433
3          mercato              1        0.991388               0.611485
4       celestiale              2        0.991252               0.260373
5             alti              2        0.989961               0.403418
6         profondo              3        0.989798               0.014777
7       potrebbono              2        0.990619               0.611864
8         serpente              2        0.989020               0.419031
9            amara              1        0.987889               0.269124
10           prese              1        0.989733               0.232872
11          romore              1        0.988291               0.220330
12        

       Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0    pioggia              5        0.864691               0.306253
1     nebbia              5        0.871611               0.172582
2       nube              4        0.859171               0.377831
3      verde              5        0.868931               0.000000
4     stelle              5        0.855371               0.479626
5       lago              3        0.862801               0.437379
6        giù              4        0.853179               0.258900
7     piante              2        0.847020               0.731096
8      tuono              1        0.846795               1.000000
9    cerchio              1        0.844503               0.076603
10    raggio              4        0.859679               0.620291
11   azzurro              2        0.848883               0.249398
12     punta              2        0.842978               0.788772
13    guarda              2        0.847331               0.12

### TOPOS: SILENZIO

In [46]:
for periodo in lista_periodi_letterari:
    try:
        print("###" + periodo + "###")
        df_periodo = similar_words_per_topos("silenzio", 5, 10, periodo)
        print(df_periodo[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + periodo)

###1_duecento_poetica_e_prosa Medievo###
La chiave non esiste nel modello1_duecento_poetica_e_prosa Medievo
###2_dolce_stil_novo###
La chiave non esiste nel modello2_dolce_stil_novo
###3_petrarchismo###
La chiave non esiste nel modello3_petrarchismo
###4_boccaccio_e_umanesimo###
             Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0       grandeagio              5        0.826410               0.124988
1       fortarrigo              2        0.835030               0.511547
2        guerriera              2        0.831629               0.736168
3   fortepiangendo              4        0.824121               0.178229
4   lungadimoranza              1        0.830384               0.818670
5        veggendol              1        0.828519               0.562352
6           tofano              3        0.830539               0.370334
7         ciutazza              4        0.828758               0.306792
8          postosi              1        0.825360              

            Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0      dispettoso              5        0.621654               0.848928
1           sordo              4        0.616405               0.697358
2   dolorosamente              2        0.615846               0.542733
3    raccapriccio              3        0.609008               0.540679
4      sbalordito              2        0.607233               0.211645
5        inquieto              2        0.609842               1.000000
6         tremore              1        0.605503               0.430252
7          taceva              5        0.614821               0.313095
8      turbamento              3        0.610033               0.518938
9      interrotto              1        0.597233               0.804571
10        scoppio              2        0.615018               0.382295
11       mormorio              1        0.627443               0.472601
12       ribrezzo              2        0.619954               0

### TOPOS: AMICIZIA

In [47]:
for periodo in lista_periodi_letterari:
    try:
        print("###" + periodo + "###")
        df_periodo = similar_words_per_topos("amicizia", 5, 10, periodo)
        print(df_periodo[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + periodo)

###1_duecento_poetica_e_prosa Medievo###
La chiave non esiste nel modello1_duecento_poetica_e_prosa Medievo
###2_dolce_stil_novo###
La chiave non esiste nel modello2_dolce_stil_novo
###3_petrarchismo###
La chiave non esiste nel modello3_petrarchismo
###4_boccaccio_e_umanesimo###
            Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0       parentado              5        0.727240               0.147943
1     benivolenza              5        0.766520               1.000000
2     coniunzione              5        0.711893               0.002438
3    espettazione              4        0.701311               0.030203
4      inimicizia              5        0.741052               0.324108
5   altripríncipi              1        0.697655               0.000000
6     simulazione              4        0.704731               0.241754
7    congiunzione              4        0.688139               0.193179
8    confederarsi              3        0.685895               0.684889


             Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0       iniziativa              5        0.712539               0.674555
1     disinteresse              4        0.708558               0.399200
2            stima              3        0.724302               0.691955
3       generosità              5        0.722031               0.417640
4        reverenza              2        0.705814               0.629662
5        beniamino              1        0.711206               0.226144
6      venerazione              1        0.708297               0.413347
7          prodiga              2        0.707870               0.946579
8        legittima              1        0.706682               0.063901
9         versione              1        0.703147               0.270168
10   sottomissione              3        0.705383               0.224597
11       affezione              3        0.710467               0.723292
12       reciproco              4        0.703935  

In [48]:
for periodo in lista_periodi_letterari:
    try:
        print("###" + periodo + "###")
        df_periodo = similar_words_per_topos("amico", 5, 10, periodo)
        print(df_periodo[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + periodo)

###1_duecento_poetica_e_prosa Medievo###
        Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0      doglia              5        0.984328               0.465708
1      segnor              2        0.980937               0.613735
2       ormai              2        0.978807               0.555471
3         ave              1        0.979699               0.625432
4        pria              4        0.979504               0.471687
5      portar              4        0.979172               1.000000
6       lauda              4        0.979549               0.759251
7    villania              2        0.977369               0.247334
8     laudare              1        0.978105               0.547627
9      figlio              1        0.977807               0.459192
10     stesso              2        0.979419               0.448348
11        ven              3        0.980523               0.281668
12     peggio              1        0.976040               0.607584
13     

            Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0         gemello              5        0.798212               0.191352
1            caro              5        0.782797               0.384603
2       servitore              5        0.794462               0.632580
3          antico              5        0.772947               0.126393
4           amato              5        0.755895               0.775824
5          presto              1        0.749195               0.000000
6      donsaverio              3        0.738242               0.127897
7       addiocaro              5        0.742606               0.183081
8         buzzano              5        0.738139               1.000000
9    padremaestro              4        0.743845               0.209370
10  signorrovatti              2        0.743945               0.054950
11        perdona              2        0.733226               0.287178
12          erede              1        0.742037               0

           Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0         cugino              5        0.735187               0.641933
1         turati              5        0.709599               0.836824
2     conoscente              5        0.727758               0.299323
3     assistente              5        0.728596               0.816100
4     psichiatra              4        0.715525               1.000000
5           bisi              2        0.706883               0.512785
6       desonnaz              5        0.715506               0.303792
7        roberto              1        0.705639               0.492517
8        rasetti              5        0.723693               0.000000
9           gino              1        0.694792               0.311946
10         adele              4        0.720723               0.513262
11        walter              1        0.711473               0.715455
12    farmacista              1        0.707064               0.268514
13    

### TOPOS: SOLITUDINE

In [49]:
for periodo in lista_periodi_letterari:
    try:
        print("###" + periodo + "###")
        df_periodo = similar_words_per_topos("solitudine", 5, 10, periodo)
        print(df_periodo[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + periodo)

###1_duecento_poetica_e_prosa Medievo###
La chiave non esiste nel modello1_duecento_poetica_e_prosa Medievo
###2_dolce_stil_novo###
La chiave non esiste nel modello2_dolce_stil_novo
###3_petrarchismo###
La chiave non esiste nel modello3_petrarchismo
###4_boccaccio_e_umanesimo###
            Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0       domestica              5        0.787864               0.426016
1        sfrenata              3        0.778412               0.018237
2         desidia              2        0.779259               0.608239
3        oppressa              5        0.770604               0.904174
4         insania              2        0.774733               0.046931
5         inerzia              5        0.779984               0.000000
6   infelicissima              2        0.772048               0.720180
7       giovinile              1        0.761572               0.633181
8         agiugni              2        0.773960               0.360278


             Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0      distrazione              4        0.666551               0.362066
1       agitazione              2        0.663629               0.467275
2       malinconia              5        0.669182               0.117589
3        monotonia              4        0.667728               0.000000
4       disinganno              1        0.667371               0.256816
5     scontentezza              4        0.660272               0.074469
6   spensieratezza              4        0.658389               0.606617
7          molesta              1        0.655979               0.576077
8      buonasalute              1        0.654238               0.470846
9        vecchiaja              1        0.651101               0.609838
10        languire              4        0.665387               0.532734
11          quiete              3        0.677935               0.674050
12        infanzia              2        0.663725  

In [50]:
for periodo in lista_periodi_letterari:
    try:
        print("###" + periodo + "###")
        df_periodo = similar_words_per_topos("solitario", 5, 10, periodo)
        print(df_periodo[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + periodo)

###1_duecento_poetica_e_prosa Medievo###
La chiave non esiste nel modello1_duecento_poetica_e_prosa Medievo
###2_dolce_stil_novo###
La chiave non esiste nel modello2_dolce_stil_novo
###3_petrarchismo###
La chiave non esiste nel modello3_petrarchismo
###4_boccaccio_e_umanesimo###
           Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0         rimoto              5        0.874388               0.638660
1        solingo              4        0.851441               0.462132
2           erto              4        0.848837               0.740465
3        baratro              5        0.845541               0.030377
4      navicella              3        0.840255               0.027917
5       ritrovai              2        0.830087               0.277923
6      salvatica              2        0.834480               0.523588
7           buia              1        0.822386               0.227695
8      salvatico              4        0.847080               0.363556
9        s

           Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0          vasto              4        0.793464               0.395802
1        isolato              5        0.790192               0.310925
2       maestoso              4        0.771939               0.286068
3       chiostro              3        0.779254               0.577447
4         remoto              2        0.766707               0.148963
5        errante              5        0.782321               0.211668
6        pensile              3        0.759836               0.668643
7       ricovero              2        0.762807               0.360493
8       edificio              3        0.764845               0.902701
9   antichissimo              3        0.773146               0.359904
10       etrusco              3        0.771958               0.000000
11         antro              2        0.770292               0.075277
12          ermo              3        0.766954               0.204321
13    

### TOPOS: INFINITO

In [51]:
for periodo in lista_periodi_letterari:
    try:
        print("###" + periodo + "###")
        df_periodo = similar_words_per_topos("infinito", 5, 10, periodo)
        print(df_periodo[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + periodo)

###1_duecento_poetica_e_prosa Medievo###
La chiave non esiste nel modello1_duecento_poetica_e_prosa Medievo
###2_dolce_stil_novo###
La chiave non esiste nel modello2_dolce_stil_novo
###3_petrarchismo###
La chiave non esiste nel modello3_petrarchismo
###4_boccaccio_e_umanesimo###
               Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0          portaseco              5        0.788867               0.526081
1   quantitàcontinua              5        0.794084               0.000000
2             motore              5        0.785343               0.497266
3        accidentale              2        0.776028               0.408311
4            risulta              4        0.772608               0.241478
5              vacuo              1        0.760739               0.452885
6             eccede              2        0.773081               0.448721
7             excede              1        0.758092               0.055304
8         piramidale              5        0.

                Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0              innato              4        0.720847               0.239928
1            corporeo              3        0.715648               1.000000
2            infinita              5        0.724088               0.705076
3          concepisce              4        0.726095               0.663578
4         immortalità              2        0.706548               0.201646
5          sensazione              3        0.712479               0.403035
6         indebolisce              4        0.709706               0.206937
7           immanente              5        0.721794               0.878593
8          indefinito              3        0.701371               0.559163
9           riempiere              1        0.694550               0.448146
10       puòconcepire              3        0.715218               0.537310
11           infinità              1        0.710654               0.301984
12          

## ANALISI PER AUTORE

In [69]:
os.chdir(path_autori_w2v)

In [70]:
lista_autori_w2v = ['Alessandro Manzoni', 'Dante Alighieri', 'Dino Buzzati', 'Francesco Petrarca', 'Gabriele D\'Annunzio', 
                    'Giacomo Leopardi', 'Giovanni Boccaccio', 'Giuseppe Parini', 'Italo Calvino', 'Italo Svevo', 
                    'Ludovico Ariosto', 'Luigi Pirandello', 'Pier Paolo Pasolini', 'Primo Levi', 'Torquato Tasso', 
                    'Ugo Foscolo', 'Umberto Eco', 'Vittorio Alfieri']

### TOPOS: PASTORE

In [71]:
for autore in lista_autori_w2v:
    try:
        print("###" + autore + "###")
        df_autore = similar_words_per_topos("pastore", 5, 10, autore)
        print(df_autore[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + autore)

###Alessandro Manzoni###
             Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0       confessore              4        0.943543               0.354103
1        chiudendo              5        0.949003               0.201969
2          pensoso              5        0.945663               0.657948
3           tasche              4        0.942890               0.243490
4         cipiglio              2        0.945992               1.000000
5        risposero              1        0.948454               0.831283
6          pistola              4        0.948440               0.629503
7          dipinto              2        0.943402               0.694047
8   ringraziamento              1        0.942900               0.000000
9        aspettati              1        0.942898               0.686156
10           ritta              3        0.939819               0.638941
11         pietosa              4        0.946606               0.299352
12         artigli        

          Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0       bartolo              5        0.959846               0.124269
1        tirate              1        0.961314               0.840536
2        posate              5        0.957365               0.859728
3       pallino              1        0.956433               0.085680
4       manacce              1        0.955152               0.197294
5        tromba              4        0.954441               0.951308
6     calicchio              1        0.952896               0.000000
7      portando              2        0.954441               0.012268
8        sporco              2        0.952524               0.083006
9     eccoliqua              1        0.952220               0.027410
10       tirano              1        0.960291               0.330709
11   carminella              2        0.960866               0.586285
12   cappellone              4        0.953924               0.469862
13     riparava     

### Altre parole correlate

In [72]:
for autore in lista_autori_w2v:
    try:
        print("###" + autore + "###")
        df_autore = similar_words_per_topos("pastori", 5, 10, autore)
        print(df_autore[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + autore)

###Alessandro Manzoni###
La chiave non esiste nel modelloAlessandro Manzoni
###Dante Alighieri###
La chiave non esiste nel modelloDante Alighieri
###Dino Buzzati###
La chiave non esiste nel modelloDino Buzzati
###Francesco Petrarca###
La chiave non esiste nel modelloFrancesco Petrarca
###Gabriele D'Annunzio###
       Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0     greggi              4        0.975084               0.636889
1       albe              3        0.969594               0.339235
2       file              2        0.969640               0.946875
3      ardui              5        0.974281               0.712922
4      prati              4        0.971723               0.175418
5    platani              3        0.967530               0.207769
6       novi              4        0.966472               0.587047
7    coralli              2        0.968841               0.703579
8       seni              1        0.971551               0.214925
9     atleti      

La chiave non esiste nel modelloVittorio Alfieri


### TOPOS: AMORE

In [73]:
for autore in lista_autori_w2v:
    try:
        print("###" + autore + "###")
        df_autore = similar_words_per_topos("amore", 5, 10, autore)
        print(df_autore[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + autore)

###Alessandro Manzoni###
            Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0           cuori              4        0.914224               0.147236
1            zelo              5        0.922459               0.000000
2            lode              4        0.903207               0.326949
3     riputazione              4        0.906646               0.408177
4           rende              5        0.920890               0.030429
5          merita              4        0.907747               0.337541
6        continui              3        0.902344               0.728802
7            pura              3        0.901932               0.378802
8        orgoglio              1        0.900214               0.365993
9       mostrarsi              1        0.898809               0.515498
10     dimostrata              3        0.903596               0.274905
11        operosa              1        0.908556               0.221133
12     sacrificio              1       

          Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0        amando              5        0.727591               0.269324
1          amor              5        0.717277               1.000000
2         amato              5        0.704384               0.604558
3   sanzadubbio              5        0.708649               0.467411
4    innamorato              5        0.706263               0.824246
5            te              1        0.685996               0.385854
6           ami              4        0.696335               0.305516
7     sollecito              1        0.673571               0.425669
8       cotanto              2        0.682268               0.362131
9        parere              1        0.668904               0.227723
10         tale              1        0.696471               0.355618
11       fedele              1        0.682075               0.224429
12      benigna              2        0.686834               0.657957
13         dono     

            Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0         aspetto              2        0.972845               0.461077
1        trattava              1        0.974372               0.275403
2      certamente              2        0.974963               0.622671
3       desiderio              5        0.979268               0.681166
4        tristram              4        0.977660               0.044876
5          potuto              4        0.971922               0.033946
6           resto              2        0.968248               0.515862
7       benissimo              4        0.970411               0.951057
8      psicologia              1        0.966800               0.190565
9      immaginare              4        0.974175               0.710601
10  semplicemente              1        0.972921               0.562541
11          ricco              1        0.969915               0.575947
12       fenomeno              1        0.969298               1

         Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0     sollievo              5        0.980340               0.062032
1      immenso              5        0.973830               0.196473
2    oltraggio              2        0.969658               0.134582
3   maraviglia              2        0.968996               0.204064
4     potresti              2        0.970973               0.106894
5       morire              5        0.972545               0.307084
6     malgrado              3        0.972343               0.469266
7      cangiar              2        0.968839               0.362356
8      lusinga              3        0.970845               0.494471
9      offende              1        0.969085               0.112562
10       dirmi              3        0.973505               0.262677
11        cara              2        0.971417               0.379008
12      voglia              3        0.971157               0.119070
13      amarti              2     

### Altre parole correlate

In [74]:
for autore in lista_autori_w2v:
    try:
        print("###" + autore + "###")
        df_autore = similar_words_per_topos("amor", 5, 10, autore)
        print(df_autore[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + autore)

###Alessandro Manzoni###
                Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0   verginesantissima              5        0.884225               0.518024
1            benedica              4        0.862951               0.000000
2               iddio              4        0.862813               0.251186
3         ringraziato              5        0.869107               0.026263
4    lasciatemiandare              5        0.862317               0.514904
5                nono              5        0.859506               0.503673
6        risposelucia              5        0.854939               0.265229
7                 nol              4        0.851792               0.439987
8               dolor              1        0.841245               0.657494
9          disselucia              5        0.851173               0.336521
10         zittozitto              4        0.861620               0.237775
11             sclamò              2        0.850581           

La chiave non esiste nel modelloItalo Calvino
###Italo Svevo###
La chiave non esiste nel modelloItalo Svevo
###Ludovico Ariosto###
         Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0       amante              3        0.932473               0.478294
1   quantunque              4        0.929617               0.098054
2        beltà              5        0.937039               0.705548
3        degna              5        0.935887               0.683829
4     vergogna              2        0.930909               0.488959
5         odio              3        0.941308               0.587214
6        desir              3        0.934916               0.648187
7        pietà              5        0.931628               0.000000
8     bellezza              3        0.924832               0.599885
9         duro              3        0.927657               0.280861
10        core              3        0.932687               1.000000
11      sdegno              1        0.93

In [75]:
for autore in lista_autori_w2v:
    try:
        print("###" + autore + "###")
        df_autore = similar_words_per_topos("innamorato", 5, 10, autore)
        print(df_autore[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + autore)

###Alessandro Manzoni###
                Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0           ritenendo              3        0.973533               0.573588
1            mandarlo              5        0.971602               0.399083
2          stabilirsi              2        0.970501               0.486303
3           ricevendo              1        0.970026               0.596469
4           domicilio              1        0.968971               0.469248
5             vivendo              1        0.968713               0.882757
6      marchesematteo              1        0.967849               0.395843
7         domandarono              1        0.967318               0.534814
8            torniamo              4        0.966877               0.257372
9             avverto              3        0.967356               0.174725
10          principia              1        0.974507               0.615828
11           inquieta              1        0.969935           

          Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0       pensavo              2        0.999087               0.579862
1         vinto              1        0.999007               0.476616
2         verrà              2        0.999050               0.534117
3       termine              2        0.999005               0.673396
4        finqui              2        0.998998               0.696652
5      sospetto              4        0.999057               0.000000
6       compito              1        0.998960               0.047278
7       capisci              1        0.998949               0.367237
8      dobbiamo              2        0.999014               0.609762
9        povero              2        0.999034               0.591362
10   raccontato              1        0.999039               1.000000
11      conosco              1        0.999034               0.856121
12     ripetere              2        0.999081               0.279453
13        ancor     

La chiave non esiste nel modelloUmberto Eco
###Vittorio Alfieri###
La chiave non esiste nel modelloVittorio Alfieri


### TOPOS: CHIESA

In [76]:
for autore in lista_autori_w2v:
    try:
        print("###" + autore + "###")
        df_autore = similar_words_per_topos("chiesa", 5, 10, autore)
        print(df_autore[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + autore)

###Alessandro Manzoni###
           Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0       convento              5        0.866229               0.314269
1         avanti              3        0.834172               0.107707
2       funzioni              3        0.833880               0.336741
3        spuntar              5        0.831550               0.246943
4       cappella              5        0.829832               0.151344
5        lettiga              2        0.826264               0.071366
6    pescarenico              5        0.829653               0.000000
7       portarsi              1        0.827602               0.131324
8      piazzetta              5        0.824114               1.000000
9         chiusa              4        0.824244               0.330697
10    cappuccini              1        0.825212               0.350961
11      carrozza              3        0.821346               0.173125
12         cerca              1        0.817897     

            Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0           arabi              5        0.961862               1.000000
1         oriente              5        0.955286               0.276767
2         stabilì              5        0.957024               0.035178
3         rapsodi              1        0.950778               0.033972
4   vediperticari              3        0.946774               0.156721
5         recente              4        0.952540               0.585839
6          gallie              5        0.949042               0.312133
7   nominatamente              1        0.945314               0.196181
8            ciro              1        0.943858               0.112090
9      primitempi              1        0.943225               0.647185
10        presero              2        0.952909               0.008172
11        vestigi              2        0.948249               0.359388
12        colonie              3        0.946146               0

               Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0        quartierino              5        0.809581               0.096305
1              bagni              1        0.802968               0.667475
2            uscendo              2        0.789084               0.153029
3         pomeriggio              2        0.789327               0.511659
4            abitava              5        0.809238               0.517999
5           carrozza              4        0.792226               0.261883
6           concerìa              1        0.793692               0.099611
7            accorsa              4        0.802702               1.000000
8         mezzanotte              4        0.788718               0.296828
9            villino              2        0.793743               0.171154
10           palazzo              4        0.794733               0.178232
11          tempesta              1        0.787360               0.501311
12           cortile     

### Altre parole correlate

In [77]:
for autore in lista_autori_w2v:
    try:
        print("###" + autore + "###")
        df_autore = similar_words_per_topos("papa", 5, 10, autore)
        print(df_autore[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + autore)

###Alessandro Manzoni###
               Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0           nominato              5        0.911708               0.474709
1            padilla              5        0.898802               0.356082
2             scrive              4        0.878286               0.000000
3             spagna              3        0.874065               0.315333
4          tipografo              3        0.881003               1.000000
5             senato              5        0.901651               0.750305
6           baruello              4        0.884558               0.183269
7         stampatori              3        0.871937               0.059113
8                sig              2        0.874028               0.439089
9             eletto              5        0.876320               0.353376
10         residente              3        0.882717               0.175789
11  cardinalfederigo              2        0.878426               0.805415


            Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0         milocca              5        0.918093               0.549058
1           ladri              1        0.906745               0.683617
2    nuovacolonia              4        0.905556               0.305083
3       costanova              4        0.911930               0.517554
4        ordinato              1        0.902396               0.353629
5      pubblicato              1        0.901346               0.748367
6     cinquecento              1        0.901072               0.616980
7        vignetta              3        0.902161               0.776767
8         ventura              3        0.907019               0.000000
9      combattere              2        0.902261               0.453749
10       miracoli              4        0.911261               0.536701
11      cristiani              1        0.908712               1.000000
12       esercito              2        0.912625               0

In [78]:
for autore in lista_autori_w2v:
    try:
        print("###" + autore + "###")
        df_autore = similar_words_per_topos("prete", 5, 10, autore)
        print(df_autore[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + autore)

###Alessandro Manzoni###
           Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0           tiro              5        0.930004               0.173411
1        pulpito              5        0.929520               0.632304
2   maravigliato              5        0.922315               0.158156
3        scherzo              1        0.926961               0.296364
4    garzoncello              1        0.926027               0.607521
5     parendogli              1        0.922866               0.464229
6         scorta              1        0.922439               0.328729
7      aspettato              4        0.923934               0.018612
8      riceverla              4        0.919551               0.361047
9     promettere              1        0.920873               0.599448
10     parlargli              1        0.929415               0.000000
11        fidato              2        0.918423               0.298491
12      cercherò              1        0.913803     

           Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0         gianni              5        0.944837               0.300339
1          zeppa              3        0.905699               0.395594
2    buonafemina              4        0.910647               0.469523
3      belcolore              5        0.905882               0.220504
4        montoro              5        0.904631               0.000000
5       paganino              2        0.898537               0.288768
6        andasse              4        0.899743               0.429610
7       ruggieri              2        0.901785               0.422013
8         monaco              5        0.910944               0.365343
9          egano              5        0.907585               1.000000
10      dissegli              3        0.908075               0.165058
11  comparpietro              1        0.898997               0.474126
12       melisso              2        0.891024               0.376176
13    

In [79]:
for autore in lista_autori_w2v:
    try:
        print("###" + autore + "###")
        df_autore = similar_words_per_topos("frate", 5, 10, autore)
        print(df_autore[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + autore)

###Alessandro Manzoni###
            Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0    conteattilio              5        0.889096               0.338156
1            tono              5        0.899292               0.372776
2      volevadire              5        0.887716               0.240154
3           tuono              5        0.889085               0.655486
4      cappellano              4        0.876804               0.148160
5        altavoce              4        0.880729               0.000000
6       sottovoce              2        0.880663               0.097628
7     guardandolo              4        0.877316               0.257469
8   accompagnando              3        0.879704               0.475428
9         dottore              3        0.874081               0.370555
10        monatto              1        0.883767               1.000000
11     voltandosi              4        0.871551               0.655109
12  fracristoforo              2       

La chiave non esiste nel modelloLuigi Pirandello
###Pier Paolo Pasolini###
La chiave non esiste nel modelloPier Paolo Pasolini
###Primo Levi###
La chiave non esiste nel modelloPrimo Levi
###Torquato Tasso###
La chiave non esiste nel modelloTorquato Tasso
###Ugo Foscolo###
La chiave non esiste nel modelloUgo Foscolo
###Umberto Eco###
             Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0              fra              2        0.995283               0.308760
1          peccato              3        0.994764               0.164394
2        colpevole              1        0.994809               0.336550
3            abati              2        0.994507               0.678922
4          lettore              1        0.994550               0.445418
5           enigmi              1        0.994397               0.202695
6           comune              1        0.994272               0.131725
7           sapete              1        0.994245               0.168760
8       

In [80]:
for autore in lista_autori_w2v:
    try:
        print("###" + autore + "###")
        df_autore = similar_words_per_topos("dio", 5, 10, autore)
        print(df_autore[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + autore)

###Alessandro Manzoni###
           Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0   misericordia              5        0.732437               0.785554
1       benedica              5        0.716413               0.026495
2          iddio              5        0.713453               0.000000
3          timor              5        0.679833               0.093190
4         grazia              5        0.683318               0.140965
5        perdono              5        0.665118               0.342625
6            dia              3        0.664681               0.745935
7        perdoni              5        0.669158               0.109483
8          cielo              2        0.657717               1.000000
9        madonna              5        0.665898               0.153118
10      benedice              1        0.659697               0.099048
11       signore              3        0.680573               0.305893
12        gloria              1        0.668250     

           Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0           idio              5        0.697610               0.215072
1        diavolo              5        0.676377               0.112986
2      rimettere              5        0.643093               0.005382
3         grazia              3        0.633265               0.126301
4          beato              4        0.606928               0.102384
5   misericordia              4        0.618363               0.170251
6       ninferno              4        0.600823               0.816211
7      peccatore              1        0.583251               0.205310
8       commessa              1        0.582703               0.172115
9          servo              1        0.582081               0.443039
10         croce              2        0.601750               1.000000
11    cognoscere              1        0.595135               0.078997
12        creato              3        0.596673               0.314045
13    

         Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0       scampi              5        0.683117               0.549309
1        marco              5        0.675044               0.749080
2        santo              5        0.656128               0.848432
3      castigo              5        0.669127               0.086512
4     benedica              5        0.659956               0.076017
5         amor              5        0.641516               0.546826
6       grazia              5        0.641287               0.912540
7          com              4        0.598798               0.151886
8      peccato              4        0.604833               0.056946
9   santissimo              3        0.590813               0.000000
10       privo              3        0.596069               0.707611
11      cristo              1        0.597830               1.000000
###Pier Paolo Pasolini###
          Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0     d

In [81]:
for autore in lista_autori_w2v:
    try:
        print("###" + autore + "###")
        df_autore = similar_words_per_topos("cristo", 5, 10, autore)
        print(df_autore[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + autore)

###Alessandro Manzoni###
La chiave non esiste nel modelloAlessandro Manzoni
###Dante Alighieri###
         Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0      martiro              1        0.998026               0.716326
1    coscïenza              3        0.998062               0.699655
2       parean              1        0.997954               0.365893
3        avria              1        0.997780               0.912162
4        viste              1        0.997751               0.093273
5      ricorda              1        0.997739               0.873543
6         fame              1        0.997735               0.242105
7        festa              1        0.997689               0.000000
8         rena              2        0.998027               0.352159
9        viver              1        0.997596               0.671930
10       turba              2        0.997498               0.643508
11       giace              1        0.997570               0.928430
12   

La chiave non esiste nel modelloItalo Calvino
###Italo Svevo###
La chiave non esiste nel modelloItalo Svevo
###Ludovico Ariosto###
           Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0     matrimonio              2        0.990287               0.522245
1         ultima              1        0.990952               0.573801
2   ragionamento              2        0.990176               0.799580
3           vere              1        0.990739               0.505196
4           dirà              2        0.989797               0.801143
5           fòra              2        0.991515               0.459348
6         tenuto              1        0.990218               1.000000
7          prove              2        0.990143               0.242304
8          merti              2        0.991533               0.968939
9           note              2        0.990587               0.655454
10         guidi              2        0.992676               0.790452
11         prega 

           Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0       apostoli              5        0.983412               1.000000
1           nome              5        0.962362               0.255233
2           vita              5        0.966644               0.044182
3         poveri              3        0.963247               0.189802
4        scienza              3        0.961667               0.081984
5           tale              2        0.964312               0.035220
6           pure              2        0.960509               0.126232
7      benedetto              1        0.964109               0.175077
8         creato              1        0.962413               0.000000
9      francesco              1        0.962031               0.176018
10       vescovo              3        0.961243               0.297026
11         figli              3        0.960765               0.046470
12  misericordia              1        0.962056               0.187854
13    

### TOPOS: FELICITA'

In [82]:
for autore in lista_autori_w2v:
    try:
        print("###" + autore + "###")
        df_autore = similar_words_per_topos("felicità", 5, 10, autore)
        print(df_autore[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + autore)

###Alessandro Manzoni###
             Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0        innocenza              1        0.948552               0.176478
1       dimostrata              5        0.949162               0.577730
2         perfetta              3        0.945778               0.158462
3         incarico              4        0.940761               0.375708
4      trasmettere              5        0.942157               0.422513
5           eterna              4        0.939430               0.411146
6        affezione              2        0.943533               0.525748
7        vivissima              3        0.943924               0.985698
8          osodire              1        0.933337               0.874189
9          esprima              1        0.932563               0.474422
10         confido              4        0.940370               0.000000
11        durevole              1        0.941571               0.361657
12        meritato        

           Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0     difficoltà              4        0.999225               0.446521
1      coscienza              1        0.999174               0.685820
2         morale              1        0.999160               0.753894
3          studi              1        0.999150               0.585497
4       risalire              1        0.999145               0.622361
5         propri              3        0.999184               0.644514
6      contrasto              2        0.999167               0.576670
7        ricerca              4        0.999134               0.921599
8         futuro              1        0.999122               0.474386
9        vissuto              1        0.999117               0.856006
10          fuga              2        0.999214               0.324334
11        sparse              2        0.999219               0.435099
12   conseguenze              3        0.999185               0.815161
13    

             Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0           specie              3        0.991699               0.402643
1        scrittori              4        0.991328               0.072891
2          depoeti              3        0.992092               0.789457
3          fingere              1        0.991854               0.347396
4         tragedie              1        0.991838               0.333618
5   dicearistotele              3        0.991520               0.319615
6        giudicata              5        0.991925               0.772179
7           musica              1        0.991627               0.577285
8      definizione              2        0.990892               0.556247
9        considera              4        0.992138               1.000000
10         epopeia              1        0.992696               0.149311
11      quantunque              2        0.992252               0.682453
12        trattate              2        0.991813  

### Altre parole correlate

In [83]:
for autore in lista_autori_w2v:
    try:
        print("###" + autore + "###")
        df_autore = similar_words_per_topos("gioia", 5, 10, autore)
        print(df_autore[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + autore)

###Alessandro Manzoni###
            Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0           gioja              5        0.878241               0.628252
1   rassegnazione              5        0.867233               1.000000
2           dolce              5        0.888120               0.205519
3         provata              3        0.860410               0.786545
4           pietà              5        0.849930               0.153476
5            dono              1        0.851351               0.007671
6            cure              5        0.870915               0.168794
7          gloria              3        0.848943               0.174803
8            vivo              2        0.848313               0.401250
9           soave              3        0.848798               0.000000
10         sangue              2        0.868505               0.548673
11        pensier              1        0.849652               0.576174
12        superbo              2       

         Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0        gioco              5        0.894044               0.792069
1   allegrezza              5        0.886071               0.786088
2       sicura              3        0.874155               0.275850
3      virtute              5        0.883636               0.870002
4      biltate              5        0.885841               0.138493
5       disire              5        0.889059               0.353969
6       sentir              1        0.864808               0.000000
7      martire              3        0.864632               1.000000
8        desio              5        0.866276               0.232998
9        ognor              5        0.871772               0.419186
10       talor              4        0.876323               0.237580
11         fin              2        0.869271               0.481335
12      focoso              1        0.855698               0.537863
13      ferita              1     

              Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0              pene              3        0.991507               0.327181
1       decisamente              1        0.991080               0.129880
2             cosmo              2        0.990615               0.326695
3            virile              5        0.992388               0.822411
4             ansia              1        0.989339               0.398446
5       gratitudine              2        0.990389               1.000000
6          angoscia              3        0.990618               0.618458
7         timidezza              3        0.992002               0.367762
8          felicità              2        0.990993               0.384966
9        solitudine              2        0.989850               0.943568
10            preda              3        0.993165               0.291938
11          terrore              1        0.993798               0.646831
12          normale              1    

### TOPOS: PATRIA/ITALIA

In [84]:
for autore in lista_autori_w2v:
    try:
        print("###" + autore + "###")
        df_autore = similar_words_per_topos("patria", 5, 10, autore)
        print(df_autore[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + autore)

###Alessandro Manzoni###
               Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0               lice              4        0.893640               0.398080
1          celebrità              1        0.891413               0.503627
2         condannato              1        0.886078               0.816578
3               fama              1        0.884408               0.706226
4           scriveva              3        0.882557               0.591634
5            posteri              1        0.880889               0.786537
6               nato              1        0.879166               0.610805
7            ridotto              2        0.879757               0.446726
8              fonte              2        0.879131               0.455292
9             godeva              2        0.880705               0.158208
10             vanto              1        0.896169               0.336036
11             unito              1        0.887953               0.546389


              Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0        continuare              1        0.998585               0.783276
1           nessuna              1        0.998562               0.833119
2            saputo              4        0.998613               0.655666
3           giocare              1        0.998428               0.561303
4   incomprensibili              2        0.998448               0.900578
5             pietà              2        0.998467               0.814711
6         puòessere              1        0.998254               1.000000
7          entrambi              3        0.998497               0.561983
8            potevo              1        0.998227               0.709927
9         principio              1        0.998157               0.647585
10      apprensione              4        0.998569               0.650002
11        costruire              3        0.998683               0.930370
12            dover              1    

        Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0       erede              5        0.955509               0.314620
1       laude              5        0.939042               0.358212
2       regio              5        0.938683               0.346384
3         don              3        0.936447               1.000000
4      moglie              5        0.936734               0.212096
5     imperio              4        0.938809               0.427368
6    promesse              2        0.931582               0.201041
7     sorella              3        0.934366               0.435370
8   acquistar              4        0.935521               0.187056
9       nozze              1        0.929712               0.356229
10      reina              4        0.934913               0.115428
11       dato              1        0.936792               0.000000
12   ingiusto              2        0.932208               0.052773
13    signore              1        0.928904    

In [85]:
for autore in lista_autori_w2v:
    try:
        print("###" + autore + "###")
        df_autore = similar_words_per_topos("italia", 5, 10, autore)
        print(df_autore[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + autore)

###Alessandro Manzoni###
          Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0    carlomagno              5        0.887985               0.321863
1       francia              5        0.877467               1.000000
2   dominazione              5        0.874354               0.170642
3       barbari              3        0.859750               0.257667
4     conquista              5        0.866361               0.480639
5        romano              5        0.865800               0.000000
6      italiana              4        0.854682               0.672623
7        romani              3        0.849871               0.747378
8          papi              4        0.849773               0.145071
9     defranchi              3        0.846349               0.200134
10     giannone              2        0.852389               0.370581
11   longobardo              2        0.861778               0.082246
12         sede              1        0.853457               0.08

La chiave non esiste nel modelloItalo Calvino
###Italo Svevo###
La chiave non esiste nel modelloItalo Svevo
###Ludovico Ariosto###
         Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0     bretagna              3        0.992475               0.177023
1     steccato              5        0.990835               0.541759
2        sorto              2        0.989695               1.000000
3        fiumi              1        0.990521               0.414123
4         arli              2        0.989593               0.331366
5       vedean              1        0.989844               0.380412
6        gigli              1        0.989805               0.007696
7   padiglione              1        0.989426               0.484691
8        entro              1        0.989234               0.066332
9     spelonca              1        0.989204               0.776925
10  ritrovarsi              2        0.987938               0.689411
11     cittade              1        0.98

          Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0   disseniceta              5        0.998205               0.261296
1         grano              3        0.998203               0.016324
2         conti              2        0.998107               0.196475
3      mercante              1        0.998132               0.768808
4        guasco              1        0.998030               0.430487
5         merda              1        0.997993               0.514904
6       andando              2        0.998026               0.421339
7         porto              1        0.997944               0.355690
8     ricordato              2        0.998060               0.858529
9      faccenda              1        0.997933               0.616205
10        crema              4        0.998327               0.077596
11      nascita              1        0.998398               0.145316
12        trovo              1        0.998088               0.611742
13       inizia     

### Altre parole correlate

In [86]:
for autore in lista_autori_w2v:
    try:
        print("###" + autore + "###")
        df_autore = similar_words_per_topos("stato", 5, 10, autore)
        print(df_autore[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + autore)

###Alessandro Manzoni###
          Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0          dato              1        0.598816               0.462390
1    comunicato              5        0.588005               0.543870
2       tentato              1        0.598037               0.425906
3      proposto              1        0.594827               0.650699
4       creduto              1        0.591259               0.898778
5       disegno              4        0.596156               0.811450
6         preso              2        0.590539               0.394343
7    immaginato              1        0.587888               0.540021
8        venuto              5        0.585985               0.000000
9          nato              2        0.590537               0.283054
10      sbaglio              4        0.601900               0.626965
11     malattia              1        0.580061               0.282546
12       negato              2        0.580045               0.70

           Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0     altravolta              5        0.715281               0.105959
1     lungotempo              3        0.673098               1.000000
2   riconosciuto              5        0.674904               0.151913
3    esserestato              5        0.687667               0.385590
4         tenuto              3        0.675021               0.000000
5     conosciuto              3        0.665256               0.313551
6      dimandato              1        0.656501               0.060790
7      essendosi              4        0.655363               0.227910
8      accidente              1        0.653657               0.274230
9       dimorata              3        0.660376               0.147217
10     carissimo              1        0.667966               0.203441
11      reputato              2        0.656618               0.130703
12       occulto              1        0.664636               0.599374
13    

             Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0     responsabili              5        0.927107               0.495082
1           sembra              3        0.917881               0.432200
2            stati              3        0.918731               0.309808
3             oggi              5        0.929403               0.910400
4            vuole              3        0.917653               0.473134
5   responsabilità              2        0.917241               0.936164
6             aver              4        0.913874               0.552489
7          afferma              3        0.915594               1.000000
8             deve              4        0.914994               0.000000
9          partito              1        0.902053               0.667179
10          voluto              4        0.927701               0.556741
11        politica              3        0.920301               0.916026
12        giornale              1        0.927657  

In [87]:
for autore in lista_autori_w2v:
    try:
        print("###" + autore + "###")
        df_autore = similar_words_per_topos("impero", 5, 10, autore)
        print(df_autore[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + autore)

###Alessandro Manzoni###
            Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0       invasione              5        0.960756               0.165351
1          eletti              5        0.956647               0.350381
2        chiamati              4        0.956773               0.792635
3     dominazione              3        0.947940               0.000000
4      terzaparte              5        0.951857               0.368088
5         insigni              5        0.952006               0.387363
6           misti              2        0.948872               0.199889
7        militari              2        0.947703               0.332716
8       divisione              3        0.945389               0.786068
9       privilegi              1        0.946963               0.153103
10       divenuti              1        0.948619               0.365919
11         caduti              3        0.948279               0.255696
12       indicati              2       

        Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0     augusto              4        0.939344               0.341989
1      eletto              4        0.929288               1.000000
2     genitor              4        0.930106               0.334597
3   francesco              2        0.929458               0.194457
4       erede              1        0.935748               0.570040
5      romano              1        0.934923               0.540475
6   fortunato              1        0.934119               0.835649
7         diè              5        0.929935               0.583157
8     invitta              3        0.928097               0.761210
9       carlo              3        0.924783               0.548214
10    esperto              4        0.930222               0.577821
11     antico              3        0.924945               0.571871
12  successor              4        0.925151               0.494181
13  guglielmo              4        0.928275    

In [88]:
for autore in lista_autori_w2v:
    try:
        print("###" + autore + "###")
        df_autore = similar_words_per_topos("nazione", 5, 10, autore)
        print(df_autore[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + autore)

###Alessandro Manzoni###
            Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0       proprietà              5        0.943392               0.157319
1        italiana              5        0.939165               0.409631
2     leggeromana              5        0.933624               0.451362
3         scabini              3        0.931702               0.162686
4              gl              3        0.927637               0.403055
5         dominio              5        0.928868               0.125415
6           rachi              4        0.926167               0.359557
7         vivente              5        0.935973               0.828188
8        municìpi              2        0.926823               0.602928
9         lotario              1        0.927356               0.000000
10    tuttaitalia              4        0.941137               0.348134
11        formata              1        0.928707               0.326494
12     fiorentino              2       

La chiave non esiste nel modelloTorquato Tasso
###Ugo Foscolo###
La chiave non esiste nel modelloUgo Foscolo
###Umberto Eco###
La chiave non esiste nel modelloUmberto Eco
###Vittorio Alfieri###
La chiave non esiste nel modelloVittorio Alfieri


In [89]:
for autore in lista_autori_w2v:
    try:
        print("###" + autore + "###")
        df_autore = similar_words_per_topos("bandiera", 5, 10, autore)
        print(df_autore[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + autore)

###Alessandro Manzoni###
La chiave non esiste nel modelloAlessandro Manzoni
###Dante Alighieri###
La chiave non esiste nel modelloDante Alighieri
###Dino Buzzati###
        Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0     fianchi              4        0.999306               0.463473
1   versonord              2        0.999233               0.141557
2      mobili              1        0.999233               0.091517
3    immobili              5        0.999233               0.340915
4      creste              4        0.999220               0.146642
5      ultime              2        0.999217               0.143966
6      girava              3        0.999229               0.153599
7        cono              2        0.999210               0.230533
8        alti              5        0.999246               1.000000
9       rosso              1        0.999206               0.000000
10    palazzi              3        0.999214               0.317188
11     impeto      

La chiave non esiste nel modelloPier Paolo Pasolini
###Primo Levi###
La chiave non esiste nel modelloPrimo Levi
###Torquato Tasso###
La chiave non esiste nel modelloTorquato Tasso
###Ugo Foscolo###
La chiave non esiste nel modelloUgo Foscolo
###Umberto Eco###
La chiave non esiste nel modelloUmberto Eco
###Vittorio Alfieri###
La chiave non esiste nel modelloVittorio Alfieri


### TOPOS: GUERRA

In [90]:
for autore in lista_autori_w2v:
    try:
        print("###" + autore + "###")
        df_autore = similar_words_per_topos("guerra", 5, 10, autore)
        print(df_autore[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + autore)

###Alessandro Manzoni###
          Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0       settala              4        0.813396               0.378420
1        truppe              4        0.815636               0.541185
2        monaco              1        0.799490               0.676771
3   descrizione              1        0.799088               0.157983
4       miserie              2        0.808403               0.786920
5        guasto              5        0.813548               0.549998
6      sospetti              2        0.803504               0.374576
7       francia              3        0.815203               0.616241
8        spagna              2        0.812255               0.430614
9         razza              1        0.793532               0.569175
10      adriano              3        0.812564               0.490357
11       strage              3        0.817891               0.422868
12      consumo              1        0.817331               0.16

                 Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0          combattenti              5        0.904319               0.000000
1                onore              5        0.885020               1.000000
2                 zara              5        0.889474               0.274421
3              legione              2        0.873940               0.141342
4             italiani              5        0.891242               0.483737
5               impero              5        0.883311               0.335578
6             italiana              2        0.863206               0.543791
7             dalmazia              3        0.864778               0.284025
8               italia              3        0.871348               0.107218
9           comandante              1        0.858269               0.716024
10  consiglionazionale              2        0.870906               0.121781
11            esercito              4        0.880545               0.476808

        Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0    vittoria              3        0.928232               0.652904
1   agramante              2        0.939919               0.081536
2   vantaggio              1        0.931743               0.287412
3     giostra              1        0.929511               0.000000
4      stanza              2        0.930943               0.557149
5        lite              3        0.929519               0.868644
6        mori              5        0.937107               0.851462
7     capitan              3        0.925826               0.382991
8    malgrado              5        0.936925               1.000000
9       pugna              2        0.932813               0.590549
10      regno              1        0.943623               0.596549
11    contesa              4        0.936227               0.760200
12      vòlse              1        0.941832               0.383202
13    levante              2        0.944057    

          Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0       signori              2        0.996475               0.000000
1      volevano              2        0.996653               0.597666
2      mercanti              2        0.996754               0.346814
3        vacche              2        0.996143               0.181702
4        strade              1        0.995939               0.812889
5       potente              1        0.995854               0.389769
6   cristianità              2        0.996083               0.549749
7           eva              1        0.995739               0.285118
8        panozi              1        0.995714               0.039569
9       padrone              2        0.995758               0.088338
10        regni              2        0.996760               0.163941
11        saggi              2        0.996207               0.154272
12     chiamava              1        0.995938               0.538802
13     milanesi     

### TOPOS: FIGURA FEMMINILE

In [91]:
for autore in lista_autori_w2v:
    try:
        print("###" + autore + "###")
        df_autore = similar_words_per_topos("donna", 5, 10, autore)
        print(df_autore[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + autore)

###Alessandro Manzoni###
               Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0            giovine              5        0.856283               0.221594
1          lettuccio              5        0.837311               0.109782
2              lesto              1        0.828688               0.313270
3            rivolto              1        0.827785               0.337950
4      promessosposo              4        0.836540               0.209630
5          vocebassa              4        0.835141               1.000000
6         buonanotte              3        0.830913               0.395826
7          guardiano              3        0.833414               0.197536
8              sarto              4        0.837381               0.307386
9             curato              3        0.833759               0.031705
10        cappellano              3        0.836712               0.334266
11             grata              1        0.839065               0.310583


        Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0       color              5        0.760248               0.000000
1        vile              5        0.757235               0.019534
2       bella              5        0.748390               0.294997
3       forte              5        0.743258               0.126317
4    graziosa              1        0.746383               0.747792
5      brutta              5        0.732034               0.399940
6        viso              5        0.751895               0.157541
7   personale              4        0.726570               0.104376
8       cieco              2        0.718136               1.000000
9       colui              1        0.722893               0.205530
10      dotto              4        0.726087               0.103571
11        bel              1        0.719168               0.273473
12     amante              2        0.727099               0.638658
13       uomo              1        0.732611    

            Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0       figliuola              4        0.692735               0.591040
1     disgraziata              5        0.689156               0.698155
2      innamorata              5        0.689109               0.901132
3           amato              5        0.689245               0.427301
4          orfana              5        0.687149               0.695680
5           umile              3        0.675903               0.794796
6      margherita              1        0.671099               0.694378
7      creaturina              2        0.679465               0.195603
8         ragazza              3        0.683696               0.637520
9            uomo              1        0.664036               0.480066
10       compagna              1        0.696574               0.640090
11    poveradonna              4        0.700144               1.000000
12         nubile              1        0.687056               0

       Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0      occhi              5        0.923256               0.357266
1      dolce              5        0.914233               0.148211
2       vidi              5        0.918946               0.567796
3      lieta              4        0.909773               0.591238
4    potessi              4        0.914034               0.306558
5     stessa              1        0.909847               0.095875
6      grata              1        0.904380               0.056929
7    sorella              4        0.907792               0.354205
8     pianto              4        0.906044               0.831599
9   malgrado              1        0.902378               0.000000
10      meco              2        0.913715               0.613930
11     lungo              1        0.919740               0.543005
12   alceste              2        0.909837               1.000000
13       fin              3        0.908778               0.27

In [92]:
for autore in lista_autori_w2v:
    try:
        print("###" + autore + "###")
        df_autore = similar_words_per_topos("madre", 5, 10, autore)
        print(df_autore[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + autore)

###Alessandro Manzoni###
            Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0          figlia              5        0.857510               0.109590
1          moglie              5        0.792152               0.224551
2         signora              5        0.821238               1.000000
3          marito              5        0.762220               0.266788
4           salva              5        0.759312               0.497107
5         sorella              5        0.764045               0.221136
6        compagna              1        0.741790               0.000000
7          fidate              5        0.756730               0.231443
8           sposa              4        0.750886               0.219132
9              ra              1        0.727547               0.244414
10  promessosposo              4        0.756287               0.720908
11      ringrazia              1        0.756026               0.280831
12         tenera              3       

        Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0      giulia              5        0.814073               0.195980
1     vecchio              5        0.808687               0.453536
2       sposa              5        0.808588               0.342890
3     sorella              5        0.786697               0.338682
4    cospetto              5        0.772580               0.202431
5      nipote              4        0.752020               0.261111
6    fratello              3        0.757970               1.000000
7        nata              5        0.764163               0.342674
8   figliuola              4        0.753514               0.182753
9     vergine              1        0.752041               0.639449
10   compagna              1        0.753024               0.927764
11     donata              4        0.764179               0.000000
12       donò              1        0.763860               0.929065
13        zio              1        0.738722    

       Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0    quattro              4        0.938581               0.159238
1       nono              5        0.939342               0.620615
2       moto              5        0.918044               0.119760
3      bagno              5        0.912621               0.045062
4       vede              4        0.915655               0.000000
5       casa              3        0.907560               0.257551
6      carte              3        0.908992               0.258756
7   compagni              1        0.909282               0.054200
8      caffè              4        0.911366               0.572987
9       ciao              3        0.915745               0.194564
10     messa              2        0.923567               0.054727
11   riprese              2        0.910739               0.503669
12     letto              1        0.913743               0.055318
13    cinque              1        0.915784               0.32

In [93]:
for autore in lista_autori_w2v:
    try:
        print("###" + autore + "###")
        df_autore = similar_words_per_topos("femmina", 5, 10, autore)
        print(df_autore[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + autore)

###Alessandro Manzoni###
La chiave non esiste nel modelloAlessandro Manzoni
###Dante Alighieri###
La chiave non esiste nel modelloDante Alighieri
###Dino Buzzati###
La chiave non esiste nel modelloDino Buzzati
###Francesco Petrarca###
La chiave non esiste nel modelloFrancesco Petrarca
###Gabriele D'Annunzio###
             Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0      teneramente              5        0.865613               0.251295
1           subito              1        0.865917               0.665378
2          bambina              5        0.856045               0.428466
3    rabbrividendo              3        0.849901               0.000000
4       mormorando              5        0.855187               0.603374
5       chinandosi              1        0.863418               0.411124
6      mazzagrogna              2        0.855081               0.156624
7   lordheathfield              1        0.862339               0.219993
8    passacantando             

La chiave non esiste nel modelloVittorio Alfieri


In [94]:
for autore in lista_autori_w2v:
    try:
        print("###" + autore + "###")
        df_autore = similar_words_per_topos("sposa", 5, 10, autore)
        print(df_autore[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + autore)

###Alessandro Manzoni###
               Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0            sorella              5        0.949041               0.734280
1              salva              4        0.944125               0.004652
2             fidate              4        0.938047               0.176734
3            vergine              5        0.940091               0.458323
4          piangendo              3        0.936650               0.082547
5           rendette              2        0.935189               0.334556
6            modesta              3        0.930821               0.326069
7      singhiozzando              2        0.933364               0.102256
8        ristabilita              2        0.931351               0.389464
9              ghita              2        0.930421               0.586693
10             porto              3        0.940653               0.303384
11           luigina              1        0.935535               0.017897


           Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0        sorella              5        0.925974               0.393928
1         isposa              5        0.906846               0.067775
2         donata              5        0.903985               0.280342
3         nipote              5        0.878893               0.121933
4         fratel              5        0.875914               0.695892
5          amica              4        0.882151               0.143221
6         figlia              4        0.868454               0.204498
7         vedova              2        0.870446               0.000000
8           nata              3        0.858734               0.307665
9          monna              1        0.854646               0.735462
10          donò              1        0.864023               0.257749
11     damigella              2        0.862484               0.013537
12      compagna              3        0.873938               0.070067
13    

            Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0           sposo              5        0.890036               0.006833
1          vedova              5        0.904835               0.541508
2         cognata              5        0.878965               0.642267
3          orfana              3        0.858054               0.250222
4   stefanoauriti              5        0.867368               0.236088
5     quattroanni              3        0.852775               0.463606
6       fidanzato              3        0.855980               0.324431
7    donfrancesco              2        0.849591               0.418324
8           amica              1        0.833012               0.554497
9          orfano              1        0.832517               0.353111
10      fidanzata              2        0.866044               0.000000
11         ottima              2        0.861370               0.398975
12    tredicianni              3        0.859663               0

### TOPOS: NOTTE/SERA

In [95]:
for autore in lista_autori_w2v:
    try:
        print("###" + autore + "###")
        df_autore = similar_words_per_topos("notte", 5, 10, autore)
        print(df_autore[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + autore)

###Alessandro Manzoni###
          Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0       passata              5        0.856915               0.232097
1      fermarsi              5        0.827662               0.059320
2        vicina              5        0.845594               0.213842
3        finché              5        0.823624               0.252486
4    spedizione              4        0.821665               0.474199
5      passando              4        0.821229               0.401610
6       seguitò              1        0.810161               0.028940
7        veduta              4        0.829705               0.150763
8    continuato              1        0.804580               0.192726
9    sottosopra              1        0.801280               0.358568
10      tornata              2        0.830389               1.000000
11  pochigiorni              2        0.814398               0.235777
12          ore              3        0.812002               0.15

            Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0        vegnente              5        0.696386               0.700329
1         passata              5        0.704457               0.697994
2        dormendo              5        0.700091               0.890223
3         mattina              3        0.687621               0.526876
4      trapassato              1        0.683036               1.000000
5   sopravegnente              2        0.679907               0.440730
6     sopravenuta              5        0.686459               0.341441
7            sera              5        0.705830               0.204741
8        riposare              2        0.687588               0.791222
9          vespro              3        0.678969               0.684685
10         giorno              3        0.714486               0.000000
11     quelgiorno              1        0.666450               0.440045
12           mese              3        0.682851               0

       Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0      sonno              5        0.746590               0.292153
1    dormito              5        0.722467               0.740087
2     sereno              5        0.700228               0.314339
3     veglia              5        0.673702               0.032487
4     dormir              5        0.680895               0.000000
5    pioggia              2        0.664795               0.294479
6    rifatto              5        0.660519               0.209527
7   giornata              5        0.682954               0.118686
8      lassù              2        0.656795               0.072618
9    lugubre              1        0.653780               0.500465
10     notti              4        0.681110               0.064289
11    passar              3        0.673226               1.000000
12    spunta              1        0.655144               0.014698
13       sol              2        0.659746               0.21

In [96]:
for autore in lista_autori_w2v:
    try:
        print("###" + autore + "###")
        df_autore = similar_words_per_topos("sera", 5, 10, autore)
        print(df_autore[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + autore)

###Alessandro Manzoni###
        Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0      partir              5        0.782468               0.098461
1       bonne              5        0.773112               0.901935
2    defresne              5        0.761623               0.282548
3    visconti              5        0.721538               0.279271
4      grossi              5        0.714874               0.781514
5      verrai              5        0.717245               0.529454
6        dame              2        0.713708               0.000000
7       finir              5        0.737576               0.291497
8   grammaire              1        0.687064               0.286259
9   castillia              4        0.714020               1.000000
10        vol              4        0.722920               0.358002
11      sposi              2        0.721219               0.316347
12      maman              1        0.714374               0.361352
13   arconati          

        Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0        vidi              5        0.873331               0.095385
1         ore              5        0.863113               0.218247
2     mattina              5        0.884147               0.517812
3       villa              4        0.861564               0.236828
4      pasqua              1        0.854094               0.117182
5       sasso              3        0.848719               1.000000
6     piaggia              2        0.848358               0.207688
7   carnevale              4        0.851784               0.184728
8        ieri              2        0.847600               0.198248
9   primavera              5        0.852725               0.491909
10     dimora              3        0.864185               0.274050
11     stanza              2        0.845647               0.135484
12    tornato              2        0.843686               0.267332
13     giorni              1        0.852553    

          Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0          cena              5        0.738016               1.000000
1      dopocena              5        0.737420               0.000000
2       mattina              4        0.719115               0.607505
3      domenica              5        0.709187               0.991889
4       uscendo              5        0.687188               0.056959
5         tardi              5        0.687806               0.554029
6          mane              5        0.705259               0.742665
7        sabato              5        0.693223               0.088221
8        dueore              2        0.668749               0.262838
9   ognimattina              2        0.664874               0.004200
10   ognigiorno              1        0.683871               0.290047
11  mezzogiorno              2        0.671045               0.023480
12       soleva              1        0.676583               0.390167
13      ritorno     

        Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0     mattina              5        0.996932               0.446514
1      maggio              4        0.995071               0.529739
2     cavallo              4        0.994833               0.428170
3      londra              3        0.995152               0.012849
4       villa              3        0.995758               0.179902
5    francesi              4        0.995035               0.319598
6        mesi              5        0.994394               0.070907
7         età              3        0.993272               0.574923
8      partii              2        0.992813               0.601086
9     dueanni              2        0.992527               0.583013
10        zio              2        0.994717               1.000000
11     cinque              2        0.994380               0.431250
12   fantasia              2        0.993896               0.487364
13     trovai              1        0.993163    

### Altre parole correlate:

In [97]:
for autore in lista_autori_w2v:
    try:
        print("###" + autore + "###")
        df_autore = similar_words_per_topos("tenebre", 5, 10, autore)
        print(df_autore[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + autore)

###Alessandro Manzoni###
         Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0     immobile              5        0.952735               0.593531
1    pavimento              5        0.961344               0.375520
2       scorse              5        0.956522               0.580864
3       girava              5        0.957008               0.661723
4    camminava              4        0.955095               0.514038
5       parete              3        0.950603               0.176530
6         girò              1        0.944704               0.583558
7     ristette              3        0.950909               0.739684
8     scorreva              2        0.946044               0.238295
9        siepe              1        0.938856               0.565548
10  occhifissi              1        0.958312               0.792798
11      cacciò              4        0.953111               0.478681
12    traverso              2        0.949626               0.916386
13      a

            Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0           verno              5        0.914659               0.101035
1            luna              4        0.900870               0.553751
2           calda              5        0.899724               0.180112
3        tempesta              5        0.898781               0.561710
4           lievi              2        0.899990               0.627302
5          passai              3        0.887371               0.587998
6   sopravegnente              5        0.904354               0.467861
7           secca              2        0.889468               0.237354
8           ombra              2        0.887798               0.197449
9       emisperio              3        0.887218               0.000000
10      tenebroso              4        0.897901               0.184687
11         oscura              1        0.881190               0.714673
12         stelle              1        0.896099               0

        Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0     paterna              3        0.994763               0.721382
1     sepolto              1        0.994760               0.907328
2   sospirato              2        0.995054               0.587326
3      dentro              3        0.994026               0.634712
4      giungo              3        0.994248               0.702775
5       tergo              4        0.995238               0.569166
6     funesto              3        0.993695               0.678412
7     guardia              2        0.993482               0.589952
8   simulacro              3        0.993561               0.436063
9        stan              4        0.992526               0.527146
10      porto              1        0.995875               0.514062
11   asciutto              1        0.995406               0.000000
12     giunta              2        0.993800               0.015769
13      fiume              3        0.994371    

In [98]:
for autore in lista_autori_w2v:
    try:
        print("###" + autore + "###")
        df_autore = similar_words_per_topos("ombra", 5, 10, autore)
        print(df_autore[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + autore)

###Alessandro Manzoni###
          Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0     sottrarsi              5        0.939917               0.498336
1        offesi              4        0.932733               0.624282
2   interrogare              2        0.933055               0.826452
3    gabellieri              1        0.933494               0.687985
4         potei              1        0.932468               0.000000
5   lasciassero              2        0.930477               0.619395
6     passarono              1        0.931444               0.593354
7    accertarsi              2        0.931451               0.440586
8       mostrar              3        0.933472               0.511375
9     vedessero              3        0.927712               0.450824
10       timori              2        0.933099               0.618048
11       scampo              2        0.932240               0.332123
12    attendeva              1        0.936988               0.57

          Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0          luce              5        0.708755               0.015958
1       lampada              5        0.691052               0.000000
2          muta              5        0.680667               0.349784
3    sepolcrale              3        0.654616               0.225220
4       pioveva              3        0.653559               0.174305
5          cupa              5        0.660868               0.218271
6      specchio              1        0.646851               0.759627
7         segue              2        0.647619               1.000000
8          zona              1        0.642172               0.119573
9        glauca              5        0.651694               0.618614
10      tenebre              3        0.651529               0.250536
11  rischiarata              3        0.648427               0.180853
12       immota              2        0.651183               0.169878
13   illuminava     

La chiave non esiste nel modelloLudovico Ariosto
###Luigi Pirandello###
            Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0        sperduto              4        0.855555               0.479604
1      solitudine              5        0.846125               0.864800
2          eterno              1        0.858957               0.615324
3        riflesso              5        0.848873               0.325890
4         paurosa              1        0.853339               0.482514
5          ignota              4        0.852137               0.389165
6        scorgeva              2        0.845060               0.530908
7           arida              1        0.848272               0.085600
8           crudo              1        0.845928               1.000000
9           lungi              2        0.842573               0.411764
10          sorge              3        0.843296               0.754468
11           nuda              1        0.848183               0

### TOPOS: FORTUNA

In [99]:
for autore in lista_autori_w2v:
    try:
        print("###" + autore + "###")
        df_autore = similar_words_per_topos("fortuna", 5, 10, autore)
        print(df_autore[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + autore)

###Alessandro Manzoni###
          Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0      incarico              5        0.928578               0.584632
1       amabile              2        0.918689               0.581845
2   puoicredere              3        0.915916               0.455324
3       obbligo              3        0.921936               0.463396
4         provo              2        0.919113               0.481013
5    degnamente              4        0.915936               0.119421
6      prezioso              3        0.915464               0.465439
7    conoscerla              2        0.915887               0.158506
8       confido              3        0.915696               0.510161
9    dimostrata              1        0.916993               1.000000
10  contentezza              3        0.916304               0.719164
11    scriverle              3        0.917653               0.457468
12   testimonio              2        0.913436               0.63

                 Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0              impresa              4        0.917138               1.000000
1               alunno              4        0.909487               0.649794
2              vicario              4        0.910958               0.651929
3              messere              1        0.896228               0.156697
4                bando              1        0.895248               0.452559
5               stampa              1        0.894973               0.414792
6               titolo              5        0.906688               0.525291
7             dalmazia              2        0.898405               0.266040
8             generale              3        0.905538               0.824483
9               ottimi              1        0.890723               0.513062
10        solennemente              2        0.911852               0.541662
11           napoleone              1        0.906009               0.914756

           Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0          darmi              2        0.995691               0.238104
1       trattare              3        0.995528               0.500497
2       avvenire              2        0.994716               0.290867
3           pace              2        0.996159               0.465432
4        bastato              1        0.996098               0.005962
5       mancanza              1        0.995942               0.977124
6         giusto              2        0.995299               0.405646
7          saper              4        0.994933               0.006183
8         morire              1        0.995859               0.645726
9      interesse              1        0.995728               0.335626
10      concesso              2        0.994366               0.720074
11         utile              1        0.993483               0.850045
12     commercio              1        0.993477               0.826440
13    

       Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0       fato              5        0.842995               0.307572
1    rubella              3        0.828252               0.384227
2     valore              3        0.830450               1.000000
3      lasci              5        0.821080               0.271630
4     premio              2        0.808729               0.381269
5    onorata              4        0.820802               0.397467
6     vincer              1        0.811486               0.463496
7      favor              4        0.813243               0.456683
8     stabil              1        0.806201               0.161142
9    difenda              4        0.817842               0.441862
10     vinca              3        0.820645               0.639068
11     regna              4        0.820196               0.521173
12     vince              4        0.823257               0.099251
13    scampo              1        0.823436               0.31

### TOPOS: NOIA

In [100]:
for autore in lista_autori_w2v:
    try:
        print("###" + autore + "###")
        df_autore = similar_words_per_topos("noia", 5, 10, autore)
        print(df_autore[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + autore)

###Alessandro Manzoni###
              Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0      divertimento              4        0.960879               0.316955
1          impiccio              1        0.960063               0.007900
2             osato              2        0.961432               0.441041
3          rallegro              1        0.957535               0.412890
4          mettermi              2        0.960005               0.393003
5             dovrò              3        0.959184               0.811618
6         indugiare              4        0.958093               0.642325
7           pochino              3        0.957533               0.517184
8             gliel              1        0.955114               0.235877
9     poveragiovane              5        0.962765               0.183446
10          rimesso              1        0.961416               0.730111
11       providenza              1        0.958186               0.533399
12       desi

            Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0    disperazione              5        0.864851               0.228384
1          timore              5        0.859435               0.252030
2          dolore              5        0.862205               1.000000
3        speranza              5        0.861739               0.342080
4      malinconia              5        0.853000               0.935311
5       travaglio              5        0.843586               0.339816
6          riposo              3        0.837094               0.710309
7       godimento              3        0.837844               0.130110
8        sventura              2        0.834354               0.000000
9   collasperanza              4        0.834253               0.321473
10      cagionato              1        0.833285               0.967634
11     dispiacere              4        0.837937               0.923931
12     privazione              1        0.823942               0

La chiave non esiste nel modelloLuigi Pirandello
###Pier Paolo Pasolini###
           Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0      riconobbe              2        0.997474               0.506357
1    leggermente              4        0.996698               0.619018
2       mostrare              3        0.996790               0.067414
3        divenne              3        0.996605               0.518614
4    schiacciato              2        0.996360               0.496121
5     tranquilla              1        0.996689               0.010171
6         cadere              1        0.996594               0.524308
7          tizio              2        0.996290               0.398422
8          fisso              1        0.995719               0.039673
9         gialli              4        0.996632               0.539461
10      luminoso              2        0.996943               0.021157
11        vomito              1        0.997317               0.342874
12

### TOPOS: TEMPORALE/PIOGGIA

In [101]:
for autore in lista_autori_w2v:
    try:
        print("###" + autore + "###")
        df_autore = similar_words_per_topos("temporale", 5, 10, autore)
        print(df_autore[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + autore)

###Alessandro Manzoni###
             Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0      aspettativa              2        0.965135               0.571865
1         sèstesso              2        0.964927               0.000000
2          lusinga              5        0.970303               0.379480
3   insopportabile              4        0.963787               0.524640
4       espiazione              2        0.964273               0.233651
5      invincibile              3        0.963850               0.260468
6        apparisse              1        0.963279               0.512151
7       scomparire              1        0.963118               1.000000
8            retto              2        0.964056               0.353260
9          stimolo              2        0.963041               0.457154
10      spaventosa              1        0.963681               0.857593
11      combattuta              2        0.961758               0.419179
12        troncata        

La chiave non esiste nel modelloVittorio Alfieri


In [102]:
for autore in lista_autori_w2v:
    try:
        print("###" + autore + "###")
        df_autore = similar_words_per_topos("pioggia", 5, 10, autore)
        print(df_autore[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + autore)

###Alessandro Manzoni###
             Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0             durò              4        0.951655               0.285447
1          spedale              4        0.944712               0.199356
2         fabbrica              1        0.942076               0.612288
3              ore              3        0.942366               0.559673
4        sedizione              5        0.946313               0.955939
5           sparsa              3        0.943340               0.709537
6          mattino              1        0.938621               0.448347
7           giunti              1        0.938105               0.130830
8         giardino              2        0.937651               0.000000
9         paesetto              1        0.937670               0.213923
10            mesi              4        0.949367               0.412340
11     susseguente              3        0.940805               0.005565
12  giornoseguente        

       Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0    augelli              5        0.971966               0.993328
1     flutti              5        0.968921               0.172169
2   procella              4        0.964254               0.372177
3      ostil              4        0.968593               0.289040
4      carro              2        0.963202               0.364928
5      colli              3        0.962028               0.598696
6       gelo              3        0.965116               0.606793
7     brando              1        0.960379               0.777514
8      nembo              1        0.959849               0.542922
9     sereno              1        0.957950               0.507866
10   fulmine              2        0.965611               0.409863
11     mogol              1        0.969930               0.262887
12   muhamed              1        0.968762               0.849020
13   schiera              1        0.968626               0.76

      Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0    fiamma              5        0.981648               0.630873
1     folta              5        0.976909               0.313726
2      sole              3        0.980276               1.000000
3    oscura              5        0.980685               0.628827
4     ruote              4        0.976324               0.754698
5    pastor              2        0.977723               0.520091
6    piante              3        0.974651               0.358377
7    sponde              3        0.976888               0.418989
8   inverso              1        0.974229               0.643803
9     sonno              1        0.974146               0.924571
10     aria              2        0.972885               0.692573
11   gregge              1        0.973455               0.451985
12    siede              2        0.975705               0.587938
13     vele              1        0.981403               0.000000
14    torr

### TOPOS: GIOVINEZZA

In [103]:
for autore in lista_autori_w2v:
    try:
        print("###" + autore + "###")
        df_autore = similar_words_per_topos("giovinezza", 5, 10, autore)
        print(df_autore[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + autore)

###Alessandro Manzoni###
            Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0        oppressa              5        0.964837               0.341535
1   supplicazione              4        0.966450               0.482382
2       eloquenza              1        0.957707               0.000000
3          cangiò              1        0.957689               0.342485
4      istantaneo              2        0.958504               0.821637
5          odiava              2        0.960409               1.000000
6   costernazione              5        0.960305               0.753366
7         orrendo              1        0.952840               0.598209
8         orrenda              1        0.951673               0.715475
9         dolente              1        0.951345               0.385414
10     giocondità              4        0.969920               0.218650
11       schietto              2        0.962640               0.487989
12     ineffabile              2       

               Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0             occupa              5        0.977724               0.597558
1          dimoranza              3        0.971941               0.414128
2               rime              4        0.972497               0.599560
3             donava              4        0.973121               0.030829
4             interi              2        0.973803               0.740775
5           mattezza              2        0.972356               0.551170
6            etterne              2        0.972510               0.288651
7               lega              2        0.974470               0.727509
8      ciascungiorno              2        0.969845               0.000000
9          disiguali              4        0.975509               0.433836
10           celeste              2        0.974468               0.358621
11  qualunquepersona              1        0.972761               0.517678
12            istato     

In [104]:
for autore in lista_autori_w2v:
    try:
        print("###" + autore + "###")
        df_autore = similar_words_per_topos("giovane", 5, 10, autore)
        print(df_autore[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + autore)

###Alessandro Manzoni###
                Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0             giovine              5        0.923170               0.249882
1        vorreisapere              2        0.866665               0.189158
2              fidato              2        0.866939               0.076112
3            contezio              3        0.876872               0.039922
4         poveralucia              4        0.869400               0.302478
5           figliuola              2        0.861305               0.152815
6              forese              5        0.880023               0.067937
7              quieto              3        0.868480               0.147933
8               sposa              3        0.861294               0.349952
9               brava              4        0.869351               0.221241
10          conoscete              2        0.859446               1.000000
11  lorenzotramaglino              2        0.862390           

           Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0        vecchio              5        0.837886               0.355312
1          ricco              5        0.842732               0.202419
2         maturo              5        0.816496               0.157708
3        amabile              5        0.799969               0.220037
4      inesperto              5        0.801679               0.381101
5         strano              4        0.796501               0.089546
6          dotto              5        0.789827               0.604476
7      fanciullo              4        0.786861               0.193491
8          spera              4        0.776400               1.000000
9   maraviglioso              2        0.782340               0.000000
10      mediocre              2        0.789235               0.303039
11    sventurato              3        0.785134               0.131671
12     fortunato              1        0.790996               0.926957
###Gio

           Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0        giovine              5        0.795575               0.239936
1          ricco              5        0.794356               0.243090
2         vedova              5        0.760928               0.323246
3          liceo              5        0.771905               0.156782
4       fratello              2        0.747013               0.061384
5          spoto              3        0.745020               0.121899
6   diciottoanni              4        0.749168               0.050802
7     quelpovero              2        0.742726               0.081127
8       marchese              4        0.752557               0.083605
9     bellissima              2        0.755573               1.000000
10       cognata              1        0.759809               0.325661
11       collega              1        0.751012               0.552114
12      deputato              2        0.745970               0.326647
13    

### TOPOS: BACIO

In [105]:
for autore in lista_autori_w2v:
    try:
        print("###" + autore + "###")
        df_autore = similar_words_per_topos("bacio", 5, 10, autore)
        print(df_autore[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + autore)

###Alessandro Manzoni###
              Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0            saluto              5        0.928723               0.047759
1          giorgino              5        0.912881               0.357274
2         umilmente              5        0.921956               0.214827
3         abbraccia              5        0.905189               0.355461
4             rosso              5        0.903770               0.381316
5        giovannina              4        0.905747               0.084054
6       benedizione              2        0.898699               0.180023
7          fratello              1        0.892677               0.068113
8          abbracci              2        0.893856               0.015557
9      cordialmente              2        0.894601               0.567353
10        ringrazia              2        0.900984               0.372498
11       antonietta              1        0.895185               0.270271
12  affettuos

          Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0      camerata              4        0.997504               0.247360
1      guardata              4        0.997424               0.305630
2          coll              2        0.996665               0.000000
3        indice              2        0.997246               0.503344
4           mal              3        0.996387               0.843212
5      torquato              2        0.996405               0.327970
6       diventò              1        0.996580               0.096977
7         scusa              2        0.996090               0.451873
8   queglialtri              1        0.996151               0.345004
9    capoccella              1        0.995903               0.551100
10      campane              2        0.996399               0.781955
11      lorenzo              2        0.997204               0.124347
12         bere              3        0.996775               0.412249
13       sirena     

La chiave non esiste nel modelloVittorio Alfieri


### TOPOS: LUNA

In [106]:
for autore in lista_autori_w2v:
    try:
        print("###" + autore + "###")
        df_autore = similar_words_per_topos("luna", 5, 10, autore)
        print(df_autore[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + autore)

###Alessandro Manzoni###
         Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0        siepe              5        0.936450               0.397178
1     spianata              4        0.940382               0.404920
2         cima              4        0.937372               0.489980
3     sentiero              5        0.930879               0.000000
4        bosco              3        0.925790               0.877270
5     torrente              4        0.929821               0.503540
6       raggio              1        0.929541               0.397839
7        ritti              2        0.929656               0.546355
8         riva              2        0.929624               0.557901
9     apparire              1        0.925601               0.562590
10      sparso              2        0.935055               0.561265
11     macchie              2        0.929258               0.536100
12  guardavano              4        0.925617               0.612445
13       

         Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0       stelle              5        0.901509               0.257333
1      tenebre              4        0.900870               0.265135
2    primavera              5        0.907716               0.264351
3       nuvoli              5        0.906189               0.943345
4        verno              5        0.903893               0.410724
5        secca              1        0.891068               0.622292
6        ombra              2        0.891831               0.191365
7     profonda              5        0.890698               0.760777
8     discerne              2        0.887885               1.000000
9        passa              1        0.885917               0.368697
10       raggi              2        0.897899               0.635804
11        aere              1        0.887696               0.422732
12      albero              3        0.887906               0.000000
13   ritondità              2     

      Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0     cielo              5        0.989266               0.493560
1     verde              5        0.982488               0.683082
2      mare              5        0.977790               1.000000
3    bianca              5        0.983025               0.658547
4      erba              5        0.982542               0.393528
5   piccolo              5        0.976655               0.417245
6      alto              5        0.979293               0.149804
7      sole              3        0.978216               0.359609
8     ombra              3        0.972523               0.151164
9     prati              1        0.969573               0.000000
10     luci              4        0.977323               0.438880
11    vuoto              2        0.976583               0.152998
12   strade              1        0.972586               0.655803
13    piena              1        0.972550               0.355974
###Primo L

### TOPOS: SILENZIO

In [107]:
for autore in lista_autori_w2v:
    try:
        print("###" + autore + "###")
        df_autore = similar_words_per_topos("silenzio", 5, 10, autore)
        print(df_autore[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + autore)

###Alessandro Manzoni###
            Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0      turbamento              5        0.837610               0.108145
1      solitudine              4        0.835585               0.855737
2        spavento              5        0.847450               0.054395
3       passavano              2        0.822574               0.172464
4        divenuto              3        0.826601               0.363859
5         mistero              5        0.837473               0.318169
6     contemplare              3        0.827998               0.278933
7         turbato              2        0.823934               0.160142
8         istante              2        0.821769               0.000000
9          severo              1        0.817611               0.263003
10          sogno              4        0.836298               0.673722
11  dolorosamente              2        0.825402               0.186469
12       minaccia              1       

           Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0        difatti              3        0.998401               0.532940
1           tipi              1        0.998190               0.363069
2       discorsi              1        0.998183               0.853884
3         strano              2        0.998304               0.838247
4         marito              2        0.998216               0.364607
5        sparare              4        0.998439               0.462702
6        rancore              1        0.998103               1.000000
7        tornava              2        0.998319               0.895411
8       sentirsi              1        0.998064               0.825857
9        parlano              1        0.998060               0.489105
10         utile              1        0.998540               0.547894
11        sapone              1        0.998435               0.176963
12          pena              1        0.998425               0.522686
13    

           Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0          vuoto              3        0.754656               0.004893
1       attonito              5        0.752352               0.811161
2   sopravvenuto              5        0.752169               0.471013
3     misterioso              5        0.759499               0.723645
4           gelo              2        0.748039               0.712053
5        sospesa              3        0.745097               1.000000
6    sospensione              1        0.733107               0.169362
7        tenebra              3        0.732927               0.019298
8          lento              5        0.748648               0.726037
9         rumore              5        0.755606               0.975402
10     infantile              2        0.760569               0.885947
11          cupo              4        0.748544               0.806962
12       sospeso              1        0.748939               0.368877
13    

        Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0    favellar              2        0.988591               0.989609
1       asilo              1        0.989312               0.485969
2     venirne              1        0.989183               0.330452
3      iniquo              2        0.987364               0.594463
4      ardire              2        0.987871               0.837031
5      presti              3        0.988626               0.553537
6       cadde              1        0.987628               0.793001
7     traccia              1        0.987317               0.569043
8     favella              2        0.987832               0.587868
9   tarquinio              1        0.986631               0.715729
10      odimi              3        0.988237               0.476611
11      perir              1        0.990281               0.401831
12      tardo              4        0.988749               0.509182
13       duce              1        0.987720    

### TOPOS: AMICIZIA

In [108]:
for autore in lista_autori_w2v:
    try:
        print("###" + autore + "###")
        df_autore = similar_words_per_topos("amicizia", 5, 10, autore)
        print(df_autore[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + autore)

###Alessandro Manzoni###
               Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0         affettuosa              5        0.950293               0.301366
1           presenta              5        0.934038               1.000000
2            volermi              3        0.936452               0.171777
3           cordiale              5        0.939971               0.620263
4           rammenti              2        0.927727               0.284637
5            sincero              5        0.938466               0.476445
6           rammenta              2        0.927450               0.529569
7         degnissima              5        0.930848               0.000000
8      osoaggiungere              5        0.937506               0.121289
9      contraccambio              2        0.927780               0.402010
10           affetto              1        0.931302               0.162325
11           potermi              1        0.926407               0.159651


         Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0    ringrazio              4        0.993708               0.316295
1    essendoci              3        0.993088               0.623354
2       ridere              3        0.993183               0.713615
3    disgrazia              4        0.993703               0.381559
4   certissimo              2        0.991892               0.401348
5         dite              1        0.991580               0.168357
6     vogliolo              1        0.991262               0.619827
7        fammi              1        0.991200               0.961148
8    accorgere              3        0.991634               0.367803
9    difficile              1        0.990869               0.063947
10      pazzia              1        0.993234               0.998590
11    legitima              1        0.991881               0.298314
12  maraviglio              1        0.991672               0.136816
13   perdonami              2     

              Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0        queiluoghi              1        0.999309               0.387124
1         esistesse              2        0.999078               0.290469
2          sfuggire              2        0.999125               0.511346
3   definitivamente              1        0.999142               0.451084
4              riva              1        0.999130               0.645907
5             trama              1        0.999126               0.527652
6         ricordava              1        0.999116               0.292402
7       ragionevole              1        0.999115               0.475038
8           normale              2        0.999135               0.346445
9     indubbiamente              1        0.999093               0.673559
10             puro              2        0.999051               0.142881
11        seguivano              2        0.999084               0.045890
12        ricchezza              1    

In [109]:
for autore in lista_autori_w2v:
    try:
        print("###" + autore + "###")
        df_autore = similar_words_per_topos("amico", 5, 10, autore)
        print(df_autore[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + autore)

###Alessandro Manzoni###
             Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0           nipote              5        0.859007               0.123322
1              zio              5        0.827179               0.284894
2         protesto              5        0.796940               0.219145
3            arese              2        0.798252               0.120776
4      signorconte              2        0.788728               0.098858
5        calderarj              4        0.792666               0.260244
6    veneratissimo              4        0.798645               0.190374
7        servitore              3        0.793668               1.000000
8         amicizia              1        0.784525               0.180171
9          potermi              1        0.783521               0.208980
10          ottimo              1        0.789354               0.111513
11            caro              2        0.784308               0.269461
12       seccatore        

              Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0             servo              5        0.843556               0.505791
1         credetemi              5        0.840521               0.241444
2            cugino              4        0.831922               0.263100
3           tenermi              5        0.834923               0.835585
4            povero              4        0.831156               0.465822
5         cavaliere              5        0.828096               0.478907
6         carissimo              2        0.827707               0.093487
7       volermibene              1        0.822328               0.897697
8           obbligo              2        0.818123               0.607875
9        gratissimo              1        0.815431               0.069046
10       affettuoso              2        0.828893               0.052058
11           amarmi              3        0.821050               0.142786
12      comandatemi              1    

          Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0       maestro              5        0.832990               0.358488
1         lèuca              5        0.801891               0.156166
2        signor              1        0.796937               0.225761
3       collega              1        0.790408               0.457503
4          ruvo              4        0.791097               0.173881
5       stefano              2        0.794575               0.270035
6   giornalista              5        0.797020               0.302166
7     imbecille              2        0.781445               0.000000
8        cesare              3        0.793082               0.396662
9    presentato              5        0.799991               1.000000
10      chiesto              4        0.805027               0.322788
11    domandato              4        0.795364               0.099387
12     promesso              2        0.788396               0.139790
13     ministro     

### TOPOS: SOLITUDINE

In [110]:
for autore in lista_autori_w2v:
    try:
        print("###" + autore + "###")
        df_autore = similar_words_per_topos("solitudine", 5, 10, autore)
        print(df_autore[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + autore)

###Alessandro Manzoni###
            Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0          smania              1        0.949965               0.470558
1      turbamento              3        0.940546               0.402187
2    abbattimento              5        0.941482               0.438271
3     trascorrere              5        0.940153               0.283467
4        leggiero              2        0.943082               0.068897
5       apparisse              3        0.940387               0.000000
6      stanchezza              4        0.942554               0.167623
7      istantanea              2        0.934649               0.109883
8   costernazione              4        0.935047               0.044047
9         fermava              4        0.935704               0.570382
10          udiva              4        0.938050               0.365635
11         scossa              2        0.946983               0.640977
12         rapido              2       

La chiave non esiste nel modelloLudovico Ariosto
###Luigi Pirandello###
            Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0          ignota              5        0.916944               0.425863
1        infinito              5        0.888809               0.029110
2      lontananza              5        0.893935               0.168916
3            gelo              5        0.896637               0.102186
4            noja              3        0.887851               0.286537
5            vana              2        0.883070               0.503937
6         paurosa              3        0.883574               0.138993
7          ignoto              4        0.883772               1.000000
8      indistinto              1        0.879137               0.189689
9   impenetrabile              3        0.879957               0.096490
10       sperduto              3        0.883183               0.076454
11     giovinezza              2        0.881697               0

In [111]:
for autore in lista_autori_w2v:
    try:
        print("###" + autore + "###")
        df_autore = similar_words_per_topos("solitario", 5, 10, autore)
        print(df_autore[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + autore)

###Alessandro Manzoni###
          Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0           oro              4        0.973080               0.700855
1    giovanetto              4        0.970011               0.521245
2         tomba              3        0.970522               0.450442
3        venere              1        0.970836               0.690011
4     maledetto              1        0.970777               0.000000
5          duce              3        0.972918               0.713227
6        aspira              1        0.969930               0.744153
7     ricevendo              1        0.969479               0.527313
8       sciolti              2        0.968900               0.203749
9       ricolto              1        0.967568               0.573001
10        invan              2        0.971500               0.638390
11   tumultuosa              4        0.973530               0.584428
12   scellerata              1        0.967679               1.00

La chiave non esiste nel modelloLudovico Ariosto
###Luigi Pirandello###
                  Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0                 vigna              1        0.968725               0.577189
1               levante              5        0.963462               0.490043
2                alture              4        0.963399               0.632630
3                miglio              4        0.961984               0.372679
4                miglia              4        0.965770               0.311468
5               collina              1        0.960822               0.561317
6               ponente              3        0.958885               0.582203
7                 prato              3        0.960189               0.765467
8             solitaria              1        0.956686               0.464890
9                roccia              1        0.956127               0.231525
10             notturna              1        0.965921               0

### TOPOS: INFINITO

In [112]:
for autore in lista_autori_w2v:
    try:
        print("###" + autore + "###")
        df_autore = similar_words_per_topos("infinito", 5, 10, autore)
        print(df_autore[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + autore)

###Alessandro Manzoni###
La chiave non esiste nel modelloAlessandro Manzoni
###Dante Alighieri###
La chiave non esiste nel modelloDante Alighieri
###Dino Buzzati###
La chiave non esiste nel modelloDino Buzzati
###Francesco Petrarca###
La chiave non esiste nel modelloFrancesco Petrarca
###Gabriele D'Annunzio###
              Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0            remoto              5        0.896649               0.540352
1            abisso              4        0.870036               0.134094
2    senzamutamento              4        0.851950               0.036498
3           nascere              3        0.852939               0.134371
4         senzafine              5        0.857093               0.132515
5         immensità              3        0.846423               0.072901
6           torbido              2        0.845680               0.277729
7          notturno              1        0.842647               0.000000
8         nostalgia   

                Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0             paurosa              3        0.959079               1.000000
1          profondità              4        0.961765               0.285356
2           soffocava              4        0.955326               0.743767
3                 afa              5        0.962547               0.908728
4               tedio              3        0.957436               0.241972
5            angustia              2        0.954174               0.351379
6   stranaimpressione              1        0.955738               0.390694
7             destava              1        0.953978               0.626709
8          indistinto              5        0.957173               0.268634
9       impenetrabile              3        0.955818               0.000000
10            pauroso              1        0.957067               0.425683
11         improvvise              1        0.952647               0.155076
12          

# ANALISI CADE

## ANALISI PER FASE LETTERARIA

In [113]:
os.chdir(path_letterario_cade)

In [114]:
lista_periodi_letterari_cade = ['CADE_1_duecento_poetica_e_prosa Medievo_cade', 'CADE_2_dolce_stil_novo_cade', 
                                'CADE_3_petrarchismo_cade', 'CADE_4_boccaccio_e_umanesimo_cade', 
                                'CADE_5_manierismo_e_barocco_cade', 'CADE_6_classicismo_arcadia_cade', 
                                'CADE_7_illuminismo_neoclassicismo_cade', 'CADE_8_romanticismo_cade', 'CADE_9_verismo_cade',
                                'CADE_10_decadentismo_cade', 'CADE_11_avanguardie_primo_novecento_cade', 
                                'CADE_12_neorealismo_cade']

### TOPOS: PASTORE

In [115]:
for periodo in lista_periodi_letterari_cade:
    try:
        print("###" + periodo + "###")
        df_periodo = similar_words_per_topos("pastore", 5, 10, periodo)
        print(df_periodo[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + periodo)

###CADE_1_duecento_poetica_e_prosa Medievo_cade###
              Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0          vigoroso              1        0.835042               0.591971
1           dimesse              1        0.831432               0.405801
2            strema              1        0.830521               0.175832
3      incontravano              1        0.829210               0.606285
4             vesta              1        0.828477               0.062376
5             giovi              1        0.827310               0.154896
6         obbligato              2        0.765940               0.313496
7         osservate              1        0.826795               0.182647
8             fanne              1        0.826371               0.978230
9          metterne              1        0.825497               0.009823
10         acquistò              3        0.767384               0.419627
11              dèe              4        0.738806           

             Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0            agnel              5        0.623499               0.228086
1        pescatore              5        0.580507               0.836265
2            tirso              1        0.644123               0.881069
3          agnello              2        0.592068               0.586738
4          sorgete              1        0.640460               0.467050
5          agnella              1        0.629142               0.511599
6        montanina              2        0.601524               0.371408
7           romito              1        0.623013               0.130139
8            nenia              4        0.574161               0.059948
9      semplicetto              2        0.588475               0.742459
10         edificò              1        0.611683               0.431389
11          paschi              1        0.598985               0.661804
12         bifolci              3        0.564945  

             Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0        vincastro              4        0.455991               0.206390
1           modula              5        0.439558               0.315578
2           pascea              5        0.488174               0.136531
3           pastor              3        0.453025               0.649587
4        pecorelle              4        0.451159               0.806781
5         pecoraio              3        0.447097               0.131818
6           belato              1        0.474137               0.412495
7          bicorne              2        0.445490               0.185381
8           pecore              2        0.442252               0.081746
9          belando              1        0.462716               0.433320
10         blocchi              1        0.428990               0.107817
11        casipola              1        0.421461               0.330834
12       indecenti              3        0.423355  

### Altre parole correlate

In [116]:
for periodo in lista_periodi_letterari_cade:
    try:
        print("###" + periodo + "###")
        df_periodo = similar_words_per_topos("pastori", 5, 10, periodo)
        print(df_periodo[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + periodo)

###CADE_1_duecento_poetica_e_prosa Medievo_cade###
            Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0       mercenarj              5        0.800599               0.188796
1         novelli              4        0.755541               0.986193
2       ventimila              1        0.799987               0.258282
3         andarvi              1        0.798668               0.162533
4       pescatori              2        0.736884               0.093668
5         mastini              5        0.727424               0.254841
6           fieri              1        0.783316               0.049011
7       minuzzoli              1        0.782699               0.355201
8         piúsavi              1        0.779411               0.121245
9         fazioni              2        0.745633               0.607053
10           capi              2        0.710404               0.876447
11  venneincontro              1        0.724565               0.149597
12         po

             Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0         bifolchi              5        0.649580               0.890837
1         coronati              5        0.605795               0.854364
2          silvani              4        0.611451               0.775942
3          bifolci              5        0.639919               0.530199
4         pascolar              4        0.590153               0.168893
5          cornuti              1        0.667522               0.949305
6        usignuoli              2        0.631761               1.000000
7         cantasti              1        0.661277               0.428028
8            fauni              3        0.628132               0.498950
9      agricoltori              1        0.654073               0.000000
10        coronate              3        0.597058               0.680266
11     cacciatrici              1        0.609645               0.284203
12  caniarrabbiati              3        0.565133  

            Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0         nuoresi              5        0.497879               0.471344
1         paesani              4        0.459620               0.357678
2         banditi              5        0.453937               0.409824
3           ovili              3        0.451763               0.363667
4           sardi              1        0.479019               0.492622
5     seminagioni              2        0.456266               0.677878
6           porci              1        0.473632               0.324939
7         foraggi              1        0.471104               0.221793
8       porchetto              1        0.470701               0.267878
9          gregge              4        0.441767               1.000000
10   servipastori              1        0.481507               0.445200
11       tosatura              3        0.443830               0.539715
12        porcari              4        0.466884               0

### TOPOS: AMORE

In [117]:
for periodo in lista_periodi_letterari_cade:
    try:
        print("###" + periodo + "###")
        df_periodo = similar_words_per_topos("amore", 5, 10, periodo)
        print(df_periodo[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + periodo)

###CADE_1_duecento_poetica_e_prosa Medievo_cade###
         Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0        disia              4        0.409299               0.336860
1   gioventute              5        0.400220               0.045199
2      portali              1        0.431444               0.924362
3        lauda              1        0.430714               0.920278
4       autore              5        0.419069               0.842060
5        grand              2        0.393667               0.172647
6       lealtà              2        0.391989               0.075209
7      amadore              1        0.425517               0.165198
8      amoroso              1        0.425197               0.396254
9       dovemo              1        0.424702               0.330212
10     deletto              3        0.384139               0.717367
11   ingegnare              1        0.398632               0.913954
12    prossimo              1        0.393627       

              Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0              amor              5        0.465654               0.162604
1       amarperdona              5        0.422004               0.232562
2            nemmen              3        0.413716               0.489330
3           affetto              3        0.400057               1.000000
4        nulloamato              5        0.436688               0.223608
5               ven              3        0.395542               0.251030
6        innamorate              5        0.418235               0.124302
7            ardore              5        0.399291               0.065917
8           inganna              2        0.396915               0.203547
9         endimione              4        0.392185               0.140466
10              end              2        0.397577               0.195812
11           cinzia              1        0.401635               0.445239
12           dividi              2    

                Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0              lavami              5        0.500728               0.176394
1               tange              4        0.367596               0.273351
2           ambizione              3        0.369214               0.235957
3          parlandone              4        0.357736               0.154601
4         disgraziato              4        0.347888               0.120168
5              amarsi              2        0.351665               0.155521
6            passione              1        0.362943               0.145802
7           trasformi              5        0.346989               0.202430
8            assetata              1        0.362446               0.230583
9           fuggitivo              1        0.361473               0.170766
10           meritavi              1        0.368499               1.000000
11          governava              2        0.350647               0.269406
12          

### Altre parole correlate

In [118]:
for periodo in lista_periodi_letterari_cade:
    try:
        print("###" + periodo + "###")
        df_periodo = similar_words_per_topos("amor", 5, 10, periodo)
        print(df_periodo[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + periodo)

###CADE_1_duecento_poetica_e_prosa Medievo_cade###
          Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0        prendo              5        0.535072               0.884634
1   gentildonna              4        0.514836               0.068186
2        servir              1        0.581324               0.679712
3        portar              2        0.532033               0.011431
4       amoroso              2        0.548374               0.890336
5         merzé              3        0.527599               0.187508
6       coverto              1        0.572259               0.221848
7          cher              1        0.570043               0.259651
8      alquanto              1        0.569456               0.392971
9       deletto              5        0.521951               0.911884
10        porea              2        0.522644               0.392682
11    dubitanza              1        0.529515               0.422861
12     malaggia              1        0

           Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0          amore              5        0.568250               0.134908
1   spirtogentil              2        0.416356               0.078138
2        stempre              3        0.420628               1.000000
3     malgradito              5        0.422354               0.076743
4         laccio              5        0.426987               0.087288
5      nobilcore              2        0.413210               0.062705
6         godete              2        0.410678               0.039324
7   dolcisguardi              1        0.418180               0.082111
8    dolceardore              2        0.407709               0.141978
9           ardi              4        0.406770               0.099083
10          acro              3        0.416943               0.192330
11       vischio              3        0.416030               0.000000
12  veraamicizia              3        0.417375               0.165845
13    

            Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0      nulloamato              5        0.487873               0.720469
1       corgentil              5        0.484429               0.194448
2     amarperdona              5        0.455747               0.217870
3        vandesio              3        0.388729               0.001842
4        combatti              1        0.407768               0.073878
5          spiace              1        0.406124               0.030790
6   amorsoverchio              3        0.395292               0.303005
7       operazion              1        0.403979               0.970039
8           oblìa              1        0.401995               0.171105
9           disio              2        0.396733               0.053992
10         tetide              4        0.395556               0.206986
11        beltate              1        0.397984               0.000000
12         tramme              3        0.403034               0

In [119]:
for periodo in lista_periodi_letterari_cade:
    try:
        print("###" + periodo + "###")
        df_periodo = similar_words_per_topos("innamorato", 5, 10, periodo)
        print(df_periodo[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + periodo)

###CADE_1_duecento_poetica_e_prosa Medievo_cade###
            Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0       altamente              5        0.617357               0.385985
1        saggezza              2        0.683120               0.987576
2        mettendo              1        0.719418               0.419221
3        spietata              2        0.654164               0.096511
4          biasmi              1        0.717353               0.172602
5             dur              3        0.631475               0.288464
6       impiccato              1        0.716590               0.207677
7        malgrado              1        0.713367               0.178675
8            mess              1        0.710139               0.470919
9   ognidiligenza              1        0.710049               0.363419
10          rusca              4        0.631939               0.982984
11     sciagurato              4        0.606266               0.459993
12   leggeram

             Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0   orlandofurioso              5        0.553244               0.924563
1    pietroaretino              5        0.546114               0.489398
2           stoico              3        0.528963               0.410745
3          riamato              5        0.541246               0.241089
4    torquatotasso              4        0.514920               0.388714
5          scaltra              1        0.570252               0.491163
6           nerina              1        0.563096               0.151187
7        attempata              4        0.508767               0.931414
8           amasse              1        0.562381               0.375543
9          scusate              4        0.514759               0.836996
10      specchiava              2        0.503544               0.768668
11   riprendendolo              2        0.489705               0.009777
12       giovenile              1        0.517158  

                Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0         gelosissimo              3        0.424780               0.729318
1              amasse              2        0.406884               0.674190
2      perfettoamante              4        0.406748               0.407134
3            vilipeso              3        0.400645               0.363758
4           smorfiosa              5        0.395453               0.000000
5         corrisposto              2        0.406108               0.660078
6            irafolle              4        0.391082               0.427027
7          innamorata              4        0.392148               1.000000
8           adoratore              1        0.409912               0.342362
9   ardentissimamente              4        0.392215               0.405916
10          schernito              3        0.384604               0.436294
11      indelicatezza              1        0.388657               0.386515
12       per

### TOPOS: CHIESA

In [120]:
for periodo in lista_periodi_letterari_cade:
    try:
        print("###" + periodo + "###")
        df_periodo = similar_words_per_topos("chiesa", 5, 10, periodo)
        print(df_periodo[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + periodo)

###CADE_1_duecento_poetica_e_prosa Medievo_cade###
            Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0       sosteneva              5        0.594574               0.272508
1        giunsero              1        0.617031               0.255978
2      uccidergli              1        0.609804               0.891609
3     consiglieri              1        0.609658               0.900495
4          odiava              1        0.607810               0.463402
5     arcivescovo              1        0.604093               0.000000
6       pregavano              1        0.602946               0.943296
7     arcivescovi              1        0.602938               0.367326
8         tolsono              5        0.540517               0.359611
9            uscì              4        0.558912               0.028277
10     guardavano              4        0.557343               0.301710
11  pregandoiddio              4        0.554712               0.092677
12       aiut

            Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0      seppellire              5        0.411627               0.456990
1         saverio              5        0.425995               0.364264
2    sanbenedetto              1        0.470151               0.233056
3     santachiesa              3        0.421792               0.628708
4        piamente              3        0.406246               0.000000
5           duomo              1        0.457314               0.879583
6        agustino              4        0.412264               0.225805
7       religiosa              1        0.452197               0.174898
8      parrocchia              4        0.412370               0.235947
9   deliberazioni              2        0.430570               0.457988
10       deguelfi              4        0.388391               0.400542
11  potevanascere              3        0.381468               0.168115
12     santissimo              1        0.395299               0

            Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0   metropolitana              2        0.510754               0.319334
1        convento              2        0.494280               0.035186
2     convertirlo              1        0.525745               0.401893
3         monache              1        0.521747               0.537656
4       campanile              4        0.458896               0.239736
5        mangioni              1        0.509136               0.718482
6           stola              1        0.502369               1.000000
7         abruzzo              3        0.449668               0.139921
8        cappella              4        0.474070               0.014091
9   ognisettimana              5        0.449649               0.514066
10           jesù              4        0.471433               0.851404
11         saliti              3        0.440358               0.865874
12        collocò              3        0.440772               0

### Altre parole correlate

In [121]:
for periodo in lista_periodi_letterari_cade:
    try:
        print("###" + periodo + "###")
        df_periodo = similar_words_per_topos("papa", 5, 10, periodo)
        print(df_periodo[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + periodo)

###CADE_1_duecento_poetica_e_prosa Medievo_cade###
          Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0   duefrategli              5        0.724185               0.731276
1          acri              5        0.693213               0.251239
2       disseli              5        0.664618               0.219228
3         marco              1        0.687167               0.483174
4        istati              1        0.682149               0.489931
5   arcivescovi              4        0.634198               1.000000
6    sottoposto              2        0.647621               0.284535
7     partirono              2        0.641063               0.229727
8       dueanni              4        0.665397               0.024134
9   duefratelli              2        0.641724               0.635275
10   pregandoli              4        0.693648               0.213150
11      mandava              2        0.640572               0.000000
12   ambasciata              3        0

                  Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0       cardinalelegato              5        0.455624               0.485213
1            boccabella              2        0.480798               0.294335
2          buoncompagno              1        0.505665               0.815290
3                 mozzò              4        0.473609               0.704135
4         preciseparole              2        0.478117               1.000000
5               sassone              1        0.496719               0.340655
6            scrittegli              1        0.492555               0.784448
7             barberino              1        0.490141               0.404613
8   segretarioarostigui              1        0.488488               0.446996
9             carcerato              1        0.487548               0.262470
10              capuano              4        0.450248               0.142366
11         rimettessero              4        0.435364          

               Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0          donliccio              5        0.507381               0.415653
1           vaticano              2        0.457132               0.151439
2        francescoii              5        0.418238               1.000000
3         santopadre              5        0.439273               0.000000
4        scomunicati              1        0.462220               0.271037
5         usurpatori              5        0.413652               0.403377
6          sguainata              5        0.437643               0.162694
7            vieille              1        0.451450               0.197371
8   dominiotemporale              3        0.403613               0.332922
9         spodestato              2        0.430688               0.073084
10     acquistassero              1        0.435923               0.443047
11  poterespirituale              4        0.425806               0.630696
12               stà     

In [122]:
for periodo in lista_periodi_letterari_cade:
    try:
        print("###" + periodo + "###")
        df_periodo = similar_words_per_topos("prete", 5, 10, periodo)
        print(df_periodo[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + periodo)

###CADE_1_duecento_poetica_e_prosa Medievo_cade###
             Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0             beda              5        0.803530               0.190738
1         panevino              5        0.773518               0.170891
2        verginità              5        0.766925               0.949423
3        scrivendo              1        0.810705               0.000000
4    confermazione              3        0.752527               0.589896
5       santissimo              5        0.743038               0.399395
6      confessione              5        0.725503               0.088249
7           rinato              3        0.743334               0.203727
8           strema              1        0.788845               0.209662
9          infinta              3        0.724557               0.087253
10       oliosanto              1        0.742110               0.392731
11         diviene              4        0.698587               0.516462


                Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0           belcolore              5        0.780299               0.508661
1               cunto              5        0.763501               0.408100
2               gradì              1        0.836757               0.473230
3          licenziato              1        0.833278               0.941278
4           tavernaro              3        0.772532               0.587624
5          ravvivasse              1        0.829679               0.302742
6              smunta              1        0.828947               0.170076
7         aspettavate              1        0.828718               0.470796
8          diminutivo              1        0.827889               0.470200
9            prevista              1        0.825106               0.305076
10           federico              2        0.745789               0.464931
11           allungar              1        0.769488               0.355123
12          

             Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0         chierico              5        0.384877               0.968971
1        arciprete              2        0.394045               0.245072
2        abruzzese              2        0.401061               0.307712
3       sagrestano              1        0.402154               0.769823
4           ilario              5        0.389509               0.313278
5      dongiuseppe              1        0.397281               0.553722
6          zelante              1        0.388727               0.174489
7            stola              5        0.390813               0.509573
8          vaccaro              1        0.386900               0.473548
9          burlare              4        0.386432               0.217001
10     collafrusta              1        0.383607               0.000000
11          crisma              3        0.374569               0.156452
12         auribus              1        0.377961  

In [123]:
for periodo in lista_periodi_letterari_cade:
    try:
        print("###" + periodo + "###")
        df_periodo = similar_words_per_topos("frate", 5, 10, periodo)
        print(df_periodo[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + periodo)

###CADE_1_duecento_poetica_e_prosa Medievo_cade###
           Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0        nocteet              5        0.642442               0.625928
1       creature              5        0.599306               0.602087
2          tucte              5        0.595717               0.482986
3         boccio              4        0.598062               0.367403
4   spetialmente              5        0.611071               0.636416
5      perdonano              3        0.592140               0.875836
6          patre              1        0.628736               0.399188
7           ello              5        0.571161               0.311366
8        cavando              5        0.595233               0.481889
9       domenico              1        0.627711               0.132357
10    concordato              3        0.567391               1.000000
11         guido              2        0.580973               0.884472
12        figlio          

            Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0        speziale              5        0.890301               0.161271
1   liberalissimo              5        0.834536               0.647008
2    alcunrancore              3        0.841085               0.531030
3      stupefatto              1        0.871430               0.522315
4         fallire              1        0.866538               0.121712
5     mirabilcosa              1        0.866288               0.264467
6       precettor              1        0.865067               0.604529
7           dormo              1        0.862230               0.201785
8        rapporto              2        0.849596               0.107269
9         vertici              1        0.861764               0.185255
10      adoperati              1        0.853257               0.732517
11         eretto              1        0.849596               0.612129
12        cordone              1        0.848799               0

               Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0                cum              5        0.660596               0.335426
1              tucte              5        0.646534               0.047650
2           serafico              5        0.647198               0.083576
3               lupo              3        0.588292               0.021832
4              pudor              1        0.657063               0.655473
5           bibbiena              4        0.607454               0.003187
6               mara              1        0.651089               1.000000
7              zorzi              1        0.649439               0.263866
8              ofthe              1        0.648095               0.904013
9               ejus              1        0.645790               0.359661
10        lungascala              1        0.567628               0.001346
11             vocem              1        0.565860               0.207499
12      paternamente     

In [124]:
for periodo in lista_periodi_letterari_cade:
    try:
        print("###" + periodo + "###")
        df_periodo = similar_words_per_topos("dio", 5, 10, periodo)
        print(df_periodo[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + periodo)

###CADE_1_duecento_poetica_e_prosa Medievo_cade###
            Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0          grazie              4        0.386331               0.994046
1   fermacredenza              5        0.389631               0.586914
2       osservare              5        0.386432               0.945630
3          crucci              2        0.378891               0.796253
4    detteragioni              5        0.397294               0.995846
5        meritato              4        0.378823               0.603888
6           iddio              3        0.372258               0.000000
7          giusti              1        0.400083               1.000000
8   fermasperanza              1        0.399870               0.731934
9        creatore              1        0.399778               0.246360
10    onnipotente              4        0.367137               0.457623
11   gastigamenti              2        0.379762               0.159644
12         me

              Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0             iddio              5        0.526424               0.062534
1          creatore              5        0.400661               0.040950
2         risguardo              3        0.397753               0.000000
3             giesù              5        0.410012               0.030003
4       onnipotente              2        0.389137               0.182864
5      misericordia              1        0.401861               0.135298
6   scelleratissimi              1        0.399946               0.243618
7      mediatorefra              5        0.401536               0.073296
8      ricordassero              3        0.389409               1.000000
9      aversofferto              3        0.382142               0.188544
10             nume              1        0.385268               0.190659
11         consacra              2        0.372518               0.042760
12         rivelata              4    

                    Words  Abs.frequency  Med.similarity  \
0                   iddio              5        0.436816   
1                   saulo              5        0.420240   
2            misericordia              5        0.394307   
3            spiritosanto              2        0.387635   
4                benedica              5        0.407836   
5               redentore              3        0.380542   
6            soccorretemi              5        0.392418   
7           cristosorrise              2        0.393755   
8                    gesú              2        0.382696   
9             farmimorire              1        0.375045   
10  salvatoredulcimascolo              2        0.393738   
11      santissimavergine              3        0.385460   
12            proclamarsi              2        0.387779   
13                 messia              2        0.393482   
14            signoregesù              1        0.384107   
15               arrabbio              1

In [125]:
for periodo in lista_periodi_letterari_cade:
    try:
        print("###" + periodo + "###")
        df_periodo = similar_words_per_topos("cristo", 5, 10, periodo)
        print(df_periodo[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + periodo)

###CADE_1_duecento_poetica_e_prosa Medievo_cade###
             Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0          farassi              5        0.473044               0.000000
1       crocifisso              2        0.488168               0.301690
2        esaminerà              5        0.462260               0.226643
3         passione              5        0.489044               0.239433
4          salvano              1        0.511321               0.842682
5          portata              5        0.464855               0.717418
6          manderà              4        0.456359               0.401203
7          sedendo              5        0.472718               0.532823
8     corpusdomini              1        0.498431               0.361166
9     incarnazione              4        0.458980               0.426048
10       risuscitò              2        0.460541               0.329175
11            jesù              1        0.464296               0.728106


                Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0           redentore              4        0.461323               0.662884
1          gesùcristo              5        0.452723               0.800636
2           appostoli              5        0.464231               0.725356
3            apostoli              5        0.468766               0.209879
4           risuscitò              2        0.477307               0.000000
5            concilia              5        0.470816               0.980756
6            redentor              5        0.463158               0.652321
7              pasqua              1        0.480777               0.834655
8   chiedergliperdono              1        0.479618               0.177896
9     chiesacristiana              5        0.459831               0.534344
10       predicazione              1        0.463775               0.247468
11       resurrezione              1        0.455309               0.566329
12         r

### TOPOS: FELICITA'

In [126]:
for periodo in lista_periodi_letterari_cade:
    try:
        print("###" + periodo + "###")
        df_periodo = similar_words_per_topos("felicità", 5, 10, periodo)
        print(df_periodo[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + periodo)

###CADE_1_duecento_poetica_e_prosa Medievo_cade###
             Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0         fallisse              5        0.821281               0.785055
1          implora              1        0.855279               0.386599
2         deludere              5        0.824031               0.256770
3        recandosi              1        0.848597               0.074490
4        procurano              5        0.829439               0.068462
5          essersi              1        0.844392               0.354441
6        accidente              1        0.841162               0.270813
7            userà              1        0.841054               0.524223
8          stringi              5        0.819553               0.228877
9     rincresciuto              1        0.840067               0.120075
10        limosine              2        0.825190               0.120535
11      gioventute              1        0.827361               0.834247


             Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0      esserfelici              2        0.406751               0.772206
1     perseveranza              1        0.416783               0.302565
2       ricompensi              3        0.387675               0.000000
3       prosperità              3        0.387212               0.073100
4         perfette              2        0.391905               0.079681
5        fabbricar              5        0.387182               0.202023
6      augurandole              1        0.403840               0.147406
7           felice              1        0.399604               0.285588
8    serieinfinita              2        0.379041               0.296991
9      solitamente              3        0.376762               0.823438
10        connessa              4        0.376190               0.479030
11      parlandosi              1        0.378932               0.697664
12       nuovoanno              1        0.370322  

                Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0            suddetta              2        0.456864               0.154749
1            accusati              5        0.455531               0.982512
2      vederlipassare              5        0.435967               0.373927
3          occhiavidi              2        0.443991               0.544411
4            seguitai              3        0.436398               0.000000
5        sfavillarono              4        0.409291               0.052259
6             macchiò              4        0.414946               0.913891
7             mezzani              2        0.439472               0.449992
8         buonaugurio              4        0.409149               0.771802
9           insperata              1        0.450301               0.831092
10       dimenticarsi              1        0.422142               0.208204
11         piangevano              4        0.396519               0.076881
12          

### Altre parole correlate

In [127]:
for periodo in lista_periodi_letterari_cade:
    try:
        print("###" + periodo + "###")
        df_periodo = similar_words_per_topos("gioia", 5, 10, periodo)
        print(df_periodo[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + periodo)

###CADE_1_duecento_poetica_e_prosa Medievo_cade###
             Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0             noia              5        0.588101               0.109895
1              nòi              5        0.553349               0.129492
2          gioiosa              5        0.543203               0.258097
3          gioioso              2        0.554254               0.005024
4          ritegno              3        0.523967               0.442185
5            beltà              5        0.530304               0.844135
6            fella              1        0.573264               0.224512
7            spero              1        0.572374               0.217227
8          biasmar              1        0.571951               0.681856
9        dubitanza              2        0.555137               0.143421
10          avenir              2        0.511230               0.856808
11           tenìa              3        0.511401               0.000000


           Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0        terrore              4        0.490107               0.183377
1         stupor              3        0.508443               0.419178
2        vedessi              1        0.549145               0.000000
3      intenerir              3        0.477729               0.408474
4     dirtiaddio              1        0.532744               0.880779
5    contentezza              4        0.467771               0.293821
6     raffrenare              1        0.522008               0.201024
7        lagnare              1        0.520284               0.323469
8         insane              5        0.456077               0.480864
9         brilla              3        0.469243               0.082031
10     scintillò              4        0.470876               0.790203
11        esulta              3        0.451998               0.168229
12     piangesti              4        0.454433               0.311521
13    

              Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0           provato              1        0.392460               0.049469
1       resuscitato              4        0.359678               0.155184
2           mescola              4        0.362217               0.522826
3            apriti              4        0.375964               0.710490
4      schienacurva              1        0.374959               0.150028
5          pensarlo              1        0.371254               0.437783
6          felicità              1        0.367943               0.098013
7             pazza              2        0.360712               0.000000
8          andarvia              1        0.365271               0.190265
9           calcare              5        0.360425               0.569726
10        montanari              1        0.347347               0.136253
11   queipochissimi              3        0.349356               0.457682
12     pastasciutta              3    

### TOPOS: PATRIA/ITALIA

In [128]:
for periodo in lista_periodi_letterari_cade:
    try:
        print("###" + periodo + "###")
        df_periodo = similar_words_per_topos("patria", 5, 10, periodo)
        print(df_periodo[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + periodo)

###CADE_1_duecento_poetica_e_prosa Medievo_cade###
                Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0        quintodecimo              3        0.736082               0.234874
1           scendesti              1        0.826108               0.231472
2              erbosa              1        0.825985               0.005512
3            traggano              3        0.748695               0.272733
4             tremerà              1        0.822164               0.404339
5        dispiacciono              1        0.818933               0.063477
6            compresi              1        0.815709               0.000179
7             montati              2        0.773934               0.944833
8             prodigo              1        0.813586               0.932642
9        consigliando              1        0.813411               0.279427
10           agricola              4        0.681884               0.386256
11        contristato              4 

               Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0      studiosamente              1        0.402341               0.000000
1             ignori              2        0.377666               0.453156
2        oltraggiata              1        0.397227               0.101120
3         distruzion              1        0.392839               0.436829
4           rivolger              5        0.366460               0.268228
5       dissimulando              1        0.389310               0.788649
6       concittadino              2        0.367618               0.845890
7         stabilirvi              1        0.384099               0.469906
8            riveder              3        0.366243               0.343982
9              vivrà              1        0.379462               0.398740
10          disporlo              2        0.357222               0.564291
11           fraudar              2        0.361893               0.599808
12        fuggirsene     

                Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0     esercitopotente              5        0.512266               0.000000
1       prolungamento              5        0.459186               1.000000
2           separiamo              3        0.468904               0.318575
3          concezione              1        0.516136               0.352151
4           nutriente              5        0.471023               0.957327
5      impetuosamente              1        0.513602               0.419468
6   intellettualmente              1        0.513458               0.264909
7            stupenda              5        0.469458               0.972054
8           empedocle              5        0.457383               0.970463
9           progresso              2        0.485703               0.100787
10            diletta              2        0.454338               0.116403
11          fortunoso              1        0.463488               0.236906
12        na

In [129]:
for periodo in lista_periodi_letterari_cade:
    try:
        print("###" + periodo + "###")
        df_periodo = similar_words_per_topos("italia", 5, 10, periodo)
        print(df_periodo[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + periodo)

###CADE_1_duecento_poetica_e_prosa Medievo_cade###
              Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0          ubidente              1        0.833425               0.556962
1          garrendo              1        0.830852               0.937933
2          barberia              1        0.828931               0.967709
3      intervenisse              1        0.825574               0.488169
4            apunto              1        0.824788               0.181973
5       disaventura              1        0.824649               0.016532
6           tribuno              1        0.823634               0.512972
7           patirne              1        0.823420               0.936933
8         concedere              3        0.762203               0.334019
9         rincontro              1        0.819610               0.981509
10           taglio              3        0.746557               0.471336
11        volendosi              2        0.761871           

            Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0     buonasalute              1        0.458908               0.218079
1         velette              4        0.383421               0.399663
2    camminoverso              4        0.399573               0.662860
3     statoeletto              1        0.426802               1.000000
4          estive              4        0.394247               0.486452
5         provava              3        0.391487               0.231491
6        prefissa              1        0.420939               0.225254
7    promettevano              1        0.420643               0.288334
8      brevetempo              1        0.419955               0.249101
9      molteparti              1        0.419663               0.440357
10       germania              4        0.396931               0.337993
11    proseguisse              2        0.380683               0.463581
12   carlobroschi              3        0.370115               0

          Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0      penisola              5        0.428551               0.356369
1      vedevamo              5        0.404858               0.000000
2       sputato              4        0.404525               0.692730
3     riassunto              1        0.432537               0.294025
4     manifesto              1        0.430718               0.245217
5     diffusero              5        0.393032               0.430104
6        duetto              1        0.426404               0.911528
7        goethe              1        0.426232               0.236514
8      saporita              3        0.392504               0.437956
9   gentilmente              3        0.387124               0.344880
10      austria              1        0.411237               0.909051
11       urlano              3        0.388579               0.380817
12   grannumero              3        0.389615               0.214539
13     convinca     

### Altre parole correlate

In [130]:
for periodo in lista_periodi_letterari_cade:
    try:
        print("###" + periodo + "###")
        df_periodo = similar_words_per_topos("stato", 5, 10, periodo)
        print(df_periodo[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + periodo)

###CADE_1_duecento_poetica_e_prosa Medievo_cade###
           Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0          afare              5        0.422506               0.121537
1        tornato              2        0.433226               0.587495
2       biasmato              1        0.462749               0.492366
3       sormonta              4        0.408106               0.144524
4         spendi              2        0.439677               0.161756
5         palese              1        0.455152               0.252496
6          pieta              2        0.412591               1.000000
7       glorïoso              3        0.405534               0.165603
8        gentile              1        0.450479               0.201710
9         altura              4        0.413225               0.292669
10       follore              1        0.416442               0.169661
11          cxvi              3        0.393743               0.161165
12        quetar          

                 Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0        impraticabile              4        0.363183               0.087676
1               istato              3        0.349017               0.504021
2         ultimigiorni              1        0.361363               0.105276
3           potevastar              1        0.360120               0.519110
4           sariastato              1        0.356535               0.239010
5         giustificato              4        0.346285               0.246861
6           indisposto              2        0.347443               0.210247
7      importantissimo              1        0.347811               0.070831
8          cangiamento              1        0.347470               0.060544
9            portomeco              3        0.343153               1.000000
10            raffermo              1        0.360076               0.555024
11         affliggermi              3        0.346905               0.487473

                Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0        potevadurare              1        0.374028               0.515986
1          disdegnato              3        0.365494               0.404592
2           sembrarmi              1        0.355548               0.026219
3           prevenuto              1        0.355303               0.431749
4          degradante              3        0.357610               0.595552
5           disonesto              1        0.351448               0.420521
6         maltrattato              4        0.358457               0.690350
7   mortalmenteferito              4        0.367993               0.209622
8   sapevapersuadersi              1        0.346514               0.601190
9             amadore              1        0.346089               0.148310
10         restaurato              4        0.363292               0.029002
11           obbliato              2        0.364762               0.232813
12    potuto

In [131]:
for periodo in lista_periodi_letterari_cade:
    try:
        print("###" + periodo + "###")
        df_periodo = similar_words_per_topos("impero", 5, 10, periodo)
        print(df_periodo[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + periodo)

###CADE_1_duecento_poetica_e_prosa Medievo_cade###
           Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0    ammonizione              1        0.812295               0.765573
1     iniquitade              5        0.736089               0.209917
2     refettorio              1        0.803577               0.901976
3    danneggiare              1        0.802726               1.000000
4         appone              1        0.802010               0.937162
5     abbattendo              2        0.773927               0.210118
6        astenne              1        0.797519               0.909722
7        gustare              1        0.797026               0.170509
8        intanto              4        0.721114               0.000000
9        alterar              1        0.796251               0.189879
10       delizie              4        0.726093               0.335587
11     immediata              1        0.751253               0.602360
12   conversione          

            Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0         monarca              5        0.498856               0.295917
1      vendicator              3        0.500735               0.380455
2          gracco              4        0.486599               0.413776
3         etruria              1        0.543447               0.030120
4          ceduto              3        0.483920               0.199670
5       usurpator              1        0.537077               0.824253
6       resuperno              1        0.535902               1.000000
7      ribellante              4        0.492342               0.000000
8            domò              1        0.525601               0.228406
9           macon              1        0.525017               0.097164
10         macone              2        0.488692               0.440163
11          regno              1        0.485834               0.114846
12         arroge              1        0.480536               0

            Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0         italico              5        0.483361               0.154888
1   benedettoviii              3        0.464020               0.760966
2    appartenersi              5        0.490523               0.749033
3       liberator              4        0.457813               0.534138
4        vassallo              4        0.471441               0.000000
5          arroga              2        0.489129               0.046349
6       fondatore              1        0.518452               0.050750
7    leggescritta              5        0.468209               0.097436
8    restauratore              1        0.503220               1.000000
9    popoloromano              1        0.502137               0.487265
10     obbedirono              1        0.477781               0.699664
11    sacroromano              4        0.438501               0.569984
12   hohenzollern              2        0.458544               0

In [132]:
for periodo in lista_periodi_letterari_cade:
    try:
        print("###" + periodo + "###")
        df_periodo = similar_words_per_topos("nazione", 5, 10, periodo)
        print(df_periodo[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + periodo)

###CADE_1_duecento_poetica_e_prosa Medievo_cade###
            Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0          centre              1        0.842055               0.325397
1          groppo              1        0.839219               0.124676
2         vegnano              1        0.837348               0.108515
3     danneggiare              1        0.836942               0.943521
4         stimato              1        0.835024               0.118057
5        arboscel              1        0.834081               0.442932
6         graffio              1        0.833806               0.030885
7          gradir              1        0.832389               1.000000
8          nomare              1        0.832072               0.031791
9          tenire              4        0.777904               0.115529
10        sonnate              3        0.747046               0.963788
11           vogl              3        0.752760               0.022696
12  donnamari

           Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0      anteposta              3        0.501899               0.860197
1       adattata              3        0.498459               0.448745
2    letteratura              2        0.517350               0.487056
3        querula              3        0.506889               0.474934
4    detestabile              1        0.570874               0.443428
5    separandosi              3        0.509251               0.894122
6         cinica              1        0.556965               0.107679
7       italiana              2        0.526972               1.000000
8      valendosi              1        0.555424               0.107698
9      aborigeni              1        0.552509               0.296800
10     trasfonde              3        0.477719               0.055059
11    professano              2        0.487350               0.490017
12        fluida              1        0.503880               0.024105
13    

               Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0       proletariato              4        0.676016               0.146104
1         proponiamo              1        0.734789               0.388293
2       collettività              4        0.659683               0.367697
3        individuale              2        0.661803               0.442005
4          economica              2        0.683621               0.515588
5      rappresentati              5        0.660963               0.312374
6          nazionali              4        0.651732               0.256485
7   senzadistinzione              2        0.655348               0.347157
8           igienica              1        0.721099               0.669976
9          razionale              1        0.719767               0.286186
10       maggioranza              1        0.671308               0.911699
11        costituita              2        0.628176               0.005884
12   geograficamente     

In [133]:
for periodo in lista_periodi_letterari_cade:
    try:
        print("###" + periodo + "###")
        df_periodo = similar_words_per_topos("bandiera", 5, 10, periodo)
        print(df_periodo[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + periodo)

###CADE_1_duecento_poetica_e_prosa Medievo_cade###
La chiave non esiste nel modelloCADE_1_duecento_poetica_e_prosa Medievo_cade
###CADE_2_dolce_stil_novo_cade###
           Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0         purgar              1        0.871272               0.554622
1     piacerebbe              1        0.865622               0.056686
2      sfogliare              1        0.860517               0.000000
3           lxix              1        0.860123               0.902891
4       schianti              1        0.857106               0.537633
5        croazia              1        0.856785               0.607823
6       commossi              1        0.856594               0.024093
7       micidial              1        0.856183               0.612946
8       paterini              1        0.856160               0.229935
9        pensavi              1        0.856146               0.876512
10        leanza              2        0.866407          

             Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0          tengasi              4        0.584469               0.473013
1        balenando              3        0.600383               0.095618
2            ulivo              1        0.668412               0.585084
3            scopa              1        0.667549               0.289670
4         portiera              1        0.662623               0.440236
5     eccomipronto              1        0.661501               0.957846
6          saltato              3        0.605983               0.473601
7        troncasse              1        0.657843               0.588265
8     magnanimocor              1        0.657498               0.447302
9        falconara              2        0.600904               0.933432
10        affilati              4        0.582008               0.330711
11       mandestra              4        0.558676               0.153009
12       bracciale              4        0.551947  

                Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0               vinco              5        0.499589               0.406397
1        ventoagitava              5        0.478745               0.000000
2             pennone              5        0.468712               0.190105
3               palio              5        0.463592               0.337799
4             antenna              5        0.435217               0.794450
5           tricolore              2        0.457726               0.210042
6              stemma              4        0.434490               0.452812
7       bandiererosse              4        0.427778               0.668060
8                bara              1        0.477298               0.715278
9         lievesoffio              4        0.440250               0.399696
10           bandiere              3        0.411761               0.613967
11       gianbattista              3        0.413923               0.807796
12          

### TOPOS: GUERRA

In [134]:
for periodo in lista_periodi_letterari_cade:
    try:
        print("###" + periodo + "###")
        df_periodo = similar_words_per_topos("guerra", 5, 10, periodo)
        print(df_periodo[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + periodo)

###CADE_1_duecento_poetica_e_prosa Medievo_cade###
            Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0       consolato              5        0.453357               0.440836
1        scipione              2        0.440221               0.289381
2       terminata              5        0.445897               0.495332
3      perigliosa              1        0.470511               0.752491
4        disfatta              1        0.468956               0.977566
5        paladini              3        0.435323               0.227955
6          romani              1        0.466406               0.268850
7            movi              5        0.429250               0.000000
8         portato              1        0.461923               0.837807
9         giudici              1        0.459270               0.288734
10          infin              3        0.421214               0.404670
11  cominciassero              4        0.435533               0.492293
12  dovessete

                     Words  Abs.frequency  Med.similarity  \
0                  cardini              1        0.486403   
1                  pirenei              2        0.431532   
2               apparecchi              5        0.406493   
3                scatenano              1        0.461609   
4                  querela              2        0.403209   
5                  accorte              5        0.408769   
6                 sossopra              1        0.441798   
7                garamanti              1        0.441615   
8               cessassero              4        0.409953   
9                   cucina              1        0.440128   
10                 ruinosa              1        0.408104   
11                imparerà              2        0.395969   
12           cassamilitare              3        0.388009   
13  desideravaardentemente              3        0.386561   
14                  orrori              1        0.398839   
15             sovversio

                Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0           battaglia              3        0.398913               0.388994
1         rivoluzione              4        0.397575               0.140476
2             europea              3        0.387930               0.257183
3        contrabbandi              5        0.396049               1.000000
4               alalà              1        0.376662               0.508799
5   figliuolochiamato              3        0.373986               0.921347
6             assetta              2        0.371862               0.698411
7           sfruttare              1        0.368661               0.315524
8      moltodissimile              1        0.367962               0.226417
9          imperversa              1        0.364869               0.766137
10          patiranno              1        0.389506               0.441347
11            tindaro              1        0.389381               0.065181
12          

### TOPOS: FIGURA FEMMINILE

In [135]:
for periodo in lista_periodi_letterari_cade:
    try:
        print("###" + periodo + "###")
        df_periodo = similar_words_per_topos("donna", 5, 10, periodo)
        print(df_periodo[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + periodo)

###CADE_1_duecento_poetica_e_prosa Medievo_cade###
          Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0       amorosa              5        0.462495               0.218519
1   lungiamente              1        0.501815               0.318050
2      coraggio              1        0.491309               0.583108
3       pietosa              1        0.490815               0.124980
4      piagente              1        0.490649               0.215225
5         spero              5        0.456912               0.888614
6        esorta              1        0.481513               0.071234
7        saggia              5        0.450528               0.221721
8        amanza              3        0.437497               0.089265
9        strano              1        0.472544               0.784747
10     protesta              4        0.434865               0.125541
11      villana              4        0.437741               0.176185
12      fallato              2        0

           Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0        eccelsa              5        0.412281               0.334245
1         decina              4        0.406879               0.345956
2        donaste              5        0.420952               0.209063
3   benefattrice              1        0.469062               1.000000
4       predissi              2        0.436896               0.438606
5      immortale              1        0.459369               0.356044
6    cieldestina              3        0.419133               0.300820
7      magnanima              3        0.413884               0.819125
8         recito              2        0.437720               0.000000
9        delfino              1        0.452975               0.459053
10  arciduchessa              3        0.409852               0.116335
11        cinese              1        0.411790               0.361567
12   duceinvitto              4        0.390471               0.891014
13   a

             Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0         placarla              4        0.354735               0.124466
1             odia              5        0.349395               0.000000
2           presta              5        0.348531               0.376110
3          fingere              4        0.339199               0.560311
4        approccio              4        0.335734               0.303641
5            avido              1        0.351459               0.822088
6         cagnetta              1        0.350654               0.799242
7          deprime              1        0.347707               1.000000
8           pudico              2        0.338615               0.715661
9         ascetica              1        0.342229               0.254379
10   compiacendosi              3        0.357732               0.474370
11        graduato              4        0.338051               0.441818
12    donnaadorata              4        0.331442  

In [136]:
for periodo in lista_periodi_letterari_cade:
    try:
        print("###" + periodo + "###")
        df_periodo = similar_words_per_topos("madre", 5, 10, periodo)
        print(df_periodo[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + periodo)

###CADE_1_duecento_poetica_e_prosa Medievo_cade###
             Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0           ventre              5        0.574965               0.168971
1         matrigna              5        0.581223               0.401206
2            fuggì              5        0.513950               0.603746
3        uccidesti              4        0.482163               0.000000
4   cosenecessarie              4        0.500684               0.499838
5            piatà              2        0.501000               0.193913
6         creatura              1        0.527926               1.000000
7         sovenuto              2        0.497953               0.009607
8        rinchiusa              4        0.475259               0.238150
9        riverisce              3        0.489358               0.222075
10         ubidito              3        0.479916               0.147543
11       ipocrisia              2        0.472803               0.220231


            Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0    benefattrice              2        0.441646               0.511291
1         nudrice              2        0.441721               0.051882
2        assalita              3        0.419231               0.168252
3    poveravedova              5        0.421406               0.525587
4     abbiamfatta              4        0.415041               0.232959
5         accorra              5        0.416198               0.563079
6       disprezzi              1        0.454581               0.191177
7          perseo              1        0.452137               0.840123
8         calmati              1        0.445591               0.888894
9         dolente              1        0.444763               0.188646
10       vilipeso              4        0.421088               0.448756
11  riguardandola              2        0.408570               0.000000
12   festeggiando              1        0.420433               1

            Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0           mamma              5        0.555507               0.094573
1        matrigna              4        0.426319               0.086664
2   poverapiccina              5        0.426684               0.064364
3      istupidita              1        0.403605               0.082313
4   poverasorella              1        0.401050               0.050766
5      mammamamma              5        0.403933               1.000000
6           titti              1        0.392705               0.084298
7    signoraagata              2        0.395116               0.219535
8         piccina              1        0.389980               0.162684
9         sorella              5        0.402589               0.000000
10      separarli              4        0.430156               0.070374
11     creaturina              2        0.400633               0.019253
12         lietta              3        0.398383               0

In [137]:
for periodo in lista_periodi_letterari_cade:
    try:
        print("###" + periodo + "###")
        df_periodo = similar_words_per_topos("femmina", 5, 10, periodo)
        print(df_periodo[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + periodo)

###CADE_1_duecento_poetica_e_prosa Medievo_cade###
               Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0           creatura              5        0.586138               0.280871
1            maschio              5        0.543050               0.000000
2             creata              5        0.522100               0.019900
3   figliuolomaschio              3        0.512687               0.475438
4                 iu              5        0.521344               1.000000
5          creazione              1        0.556231               0.755015
6                 eh              2        0.518461               0.309924
7            gravida              5        0.503397               0.445628
8           ingenera              4        0.488492               0.398327
9          poterfare              1        0.528252               0.143426
10           miseria              4        0.506705               0.322232
11            cugine              1        0.5018

          Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0      vilipesa              5        0.753640               0.056947
1      ginestra              1        0.830204               0.976590
2         ardon              1        0.826476               0.975444
3     faretrato              1        0.826293               0.335218
4        gioghi              1        0.822894               0.190569
5    salamandra              1        0.822860               1.000000
6         tauro              1        0.820322               0.954099
7        treman              4        0.735624               0.081785
8        impura              1        0.819718               0.934152
9         sorda              1        0.819218               0.608033
10       trofeo              1        0.782838               0.203217
11     infocata              1        0.767786               0.009899
12      prevede              1        0.765096               0.561668
13         leda     

                Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0        consenziente              5        0.581554               0.940044
1         considerata              5        0.528857               0.449345
2           istituito              4        0.538646               0.474738
3           magnetica              3        0.533639               0.798004
4               genìa              2        0.577130               0.387893
5   intelligentissima              1        0.607509               0.258843
6          pretendano              1        0.603477               0.472932
7            bastarda              1        0.599805               0.466849
8           eccomiqui              5        0.539784               0.763575
9      seducentissima              1        0.598847               0.210228
10        mercantessa              4        0.536924               1.000000
11          tremaschi              1        0.542501               0.145062
12        ci

In [138]:
for periodo in lista_periodi_letterari_cade:
    try:
        print("###" + periodo + "###")
        df_periodo = similar_words_per_topos("sposa", 5, 10, periodo)
        print(df_periodo[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + periodo)

###CADE_1_duecento_poetica_e_prosa Medievo_cade###
           Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0    avventurata              5        0.726666               0.000000
1     animabeata              5        0.764554               1.000000
2          sposo              5        0.755120               0.654592
3   dilettissimo              5        0.728922               0.321083
4   dilettissima              5        0.717580               0.133689
5    nobilissimo              5        0.744772               0.603551
6   contemplante              2        0.721068               0.571752
7     soavissimo              3        0.707260               0.675157
8      benedetta              3        0.690084               0.454513
9     gesùcristo              3        0.704720               0.317872
10  pietosissimo              4        0.718887               0.819649
11    jesùcristo              2        0.689732               0.583670
12      cognosci          

          Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0       suddita              2        0.518151               0.072554
1        ricusi              1        0.552326               0.422454
2         sposo              5        0.497037               0.163550
3        german              1        0.536864               0.424269
4        talamo              5        0.470401               0.199249
5       calcide              2        0.482904               0.238257
6        numida              3        0.487361               0.024574
7        uccido              2        0.485683               0.871367
8      vassalla              3        0.479708               0.205622
9       svenato              2        0.498902               0.395601
10   compatisci              1        0.483122               0.459535
11   vendicarti              1        0.482335               0.000000
12  invittoduce              1        0.479676               1.000000
13   vendicasse     

            Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0        immaginò              5        0.472202               0.502409
1      commissari              5        0.462963               0.460750
2         adorava              4        0.465204               0.185020
3       fidanzata              2        0.497099               0.481749
4       nazzarena              2        0.493567               1.000000
5      giàvarcato              3        0.464312               0.206297
6      antonietta              3        0.460684               0.109619
7    congedandosi              1        0.519193               0.219325
8        posporre              4        0.460501               0.796366
9       uscissero              5        0.475263               0.494183
10    svergognata              2        0.458376               0.411679
11    grandissimo              1        0.455360               0.566904
12  correpericolo              2        0.433076               0

### TOPOS: NOTTE/SERA

In [139]:
for periodo in lista_periodi_letterari_cade:
    try:
        print("###" + periodo + "###")
        df_periodo = similar_words_per_topos("notte", 5, 10, periodo)
        print(df_periodo[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + periodo)

###CADE_1_duecento_poetica_e_prosa Medievo_cade###
            Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0       vegghiare              2        0.486866               0.745689
1            alba              2        0.465150               0.123286
2       dormivano              3        0.446631               0.136746
3          parria              4        0.433346               0.372395
4            mese              1        0.469567               0.528817
5          vegghi              5        0.440967               0.139328
6           serpe              1        0.467656               0.403515
7          ottodí              2        0.439906               0.036927
8   sollicitudini              4        0.433544               0.428829
9         pascere              2        0.434637               0.095691
10           èmmi              3        0.460516               0.156092
11         giorno              2        0.438092               0.797417
12       dorm

             Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0     discacciarne              5        0.485327               0.289603
1       crepuscolo              5        0.515836               0.485314
2       festeggiar              1        0.518216               0.255089
3           riposò              5        0.480499               0.299699
4   architrionfali              5        0.468606               0.291325
5          troviam              5        0.472990               0.975308
6          splenda              1        0.509126               0.658795
7        tramontar              3        0.455633               1.000000
8       introdurvi              5        0.471503               0.770875
9       fiammeggia              1        0.496131               0.515375
10        meriggio              2        0.465964               0.457905
11       comandata              1        0.450714               0.008564
12         allungò              1        0.449741  

           Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0          notti              4        0.341801               0.501282
1       fattoria              2        0.348351               0.322382
2         cubica              2        0.341916               0.513778
3           buia              4        0.339694               0.073584
4         incubi              1        0.361737               0.219044
5        vagando              5        0.334295               0.562779
6         nevosa              4        0.340172               0.470062
7      morsicata              1        0.346129               0.704722
8      spelonche              2        0.329967               0.286082
9       disumano              5        0.337712               1.000000
10      avanzerà              2        0.331017               0.655718
11  attentissima              4        0.339128               0.524317
12       taciute              2        0.325025               0.560245
13    

In [140]:
for periodo in lista_periodi_letterari_cade:
    try:
        print("###" + periodo + "###")
        df_periodo = similar_words_per_topos("sera", 5, 10, periodo)
        print(df_periodo[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + periodo)

###CADE_1_duecento_poetica_e_prosa Medievo_cade###
          Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0         suona              5        0.622990               0.494962
1          alba              1        0.696002               1.000000
2        scampò              1        0.683779               0.914568
3       adrieto              2        0.600446               0.910566
4        fecene              1        0.681014               0.588511
5    discenderà              1        0.680025               0.401769
6       rifanno              5        0.620577               0.335134
7     appiccato              1        0.679838               0.314687
8   celatamente              1        0.679081               0.915558
9      entrammo              1        0.679019               0.272442
10         cenò              1        0.618146               0.910241
11    facevagli              1        0.608733               0.538763
12       sonata              2        0

              Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0        dopopranzo              5        0.570286               0.243040
1           mezzodì              5        0.532781               0.453770
2            sabato              5        0.540097               0.259445
3            dimani              4        0.533232               0.854869
4           martedì              1        0.583693               0.241636
5           venturo              1        0.583504               0.000000
6            pranzo              2        0.529732               0.285255
7            treore              2        0.538906               0.157403
8          domenica              4        0.515280               1.000000
9           mattina              5        0.547228               0.605268
10       avantiieri              2        0.513765               0.122482
11  rappresentarono              1        0.523831               0.448888
12           lunedi              1    

                   Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0               primeore              3        0.339843               0.383988
1                 lunedí              4        0.334679               0.190457
2               corriere              5        0.340829               0.356465
3             pomeriggio              4        0.339885               0.252420
4               dopocena              4        0.336125               0.291864
5                mattina              5        0.378628               0.249654
6            commentando              1        0.342833               0.212450
7               domenica              3        0.333252               0.272019
8           quintogiorno              2        0.327078               0.875553
9        mattinoseguente              1        0.333899               0.261297
10                 notte              4        0.387690               0.392941
11         giornifestivi              1        0.330

### Altre parole correlate:

In [141]:
for periodo in lista_periodi_letterari_cade:
    try:
        print("###" + periodo + "###")
        df_periodo = similar_words_per_topos("tenebre", 5, 10, periodo)
        print(df_periodo[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + periodo)

###CADE_1_duecento_poetica_e_prosa Medievo_cade###
          Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0     mettetelo              5        0.763627               0.465966
1     battiture              5        0.695432               0.234704
2       atterrò              5        0.644111               0.373744
3         solfo              1        0.694438               0.642664
4   oscurissimo              3        0.623863               0.151609
5        abisso              2        0.661711               0.101736
6       mandalo              2        0.636112               0.269226
7         formò              1        0.682289               0.573793
8      stridore              1        0.677726               0.331828
9       manderà              5        0.623866               0.267661
10     stridori              4        0.664787               0.223308
11   affliggono              3        0.617576               1.000000
12        messe              3        0

            Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0        oscurità              5        0.495536               0.483770
1        caligine              4        0.481652               0.774215
2       rischiara              4        0.493614               0.257354
3         sepolte              2        0.496576               0.000000
4         giacean              1        0.539311               0.083758
5         sepolti              4        0.480668               1.000000
6       oblivione              3        0.499813               0.413550
7        inimiche              3        0.473809               0.281690
8        caligini              1        0.514092               0.766168
9        nascoste              1        0.513193               0.305072
10        involta              4        0.459081               0.646366
11         odiata              2        0.469787               0.377537
12  superstiziose              2        0.464650               0

               Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0             abissi              3        0.474631               0.350030
1            potenze              1        0.554431               0.061516
2           frangono              3        0.485723               0.314940
3           inondata              4        0.474013               0.856753
4          scolorate              1        0.541907               0.058204
5         immutabile              1        0.537958               0.221941
6         balenarono              1        0.536844               0.840068
7        risplendere              1        0.536230               0.807685
8                evo              1        0.534795               0.440379
9         firmamento              1        0.530819               0.310473
10          converso              3        0.458904               0.171759
11        primiraggi              3        0.469927               0.865825
12            fugate     

In [142]:
for periodo in lista_periodi_letterari_cade:
    try:
        print("###" + periodo + "###")
        df_periodo = similar_words_per_topos("ombra", 5, 10, periodo)
        print(df_periodo[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + periodo)

###CADE_1_duecento_poetica_e_prosa Medievo_cade###
             Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0      rallegrarti              3        0.638179               0.556480
1        maravigli              2        0.663335               0.468090
2             ista              4        0.621599               0.471636
3       tempestosa              5        0.616522               0.959486
4         truovono              1        0.678777               0.257663
5        avvilisce              1        0.672879               0.399428
6       sospezione              1        0.672076               0.257424
7         nascendo              1        0.671287               0.448151
8           lucano              1        0.670433               0.260723
9        saramenti              1        0.668714               0.607258
10        disfarsi              4        0.598435               0.942689
11          alcune              3        0.601854               0.893934


           Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0           aura              4        0.566793               0.790027
1     agghiaccio              5        0.590142               0.371619
2        orribil              4        0.567673               0.601482
3   raccapriccia              3        0.559503               0.487903
4       susurrar              1        0.616145               0.480553
5         fronda              2        0.578916               0.452273
6          sparì              1        0.607090               0.365679
7          sedea              2        0.572398               0.208522
8         tralci              2        0.569860               0.558630
9      moribonda              1        0.604064               0.699371
10       inchina              4        0.550469               0.071526
11        spenga              1        0.554264               0.224337
12       credilo              2        0.548315               0.469667
13    

            Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0   settecentesca              1        0.560614               0.268209
1        chiarore              1        0.555935               0.394890
2          cubica              4        0.478625               0.966081
3        sentieri              2        0.491048               0.198120
4           tetra              1        0.541852               0.610830
5    crepuscolare              2        0.506935               0.405581
6      plenilunio              1        0.536423               0.197807
7       triangolo              2        0.515819               0.351479
8          gelidi              1        0.534253               0.808882
9          scorge              1        0.533084               0.000000
10        animato              4        0.459677               0.195570
11         scorgo              1        0.489019               0.054744
12       corrompe              4        0.450010               0

### TOPOS: FORTUNA

In [143]:
for periodo in lista_periodi_letterari_cade:
    try:
        print("###" + periodo + "###")
        df_periodo = similar_words_per_topos("fortuna", 5, 10, periodo)
        print(df_periodo[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + periodo)

###CADE_1_duecento_poetica_e_prosa Medievo_cade###
          Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0       nochier              5        0.672407               0.243362
1   saggiamente              1        0.703405               0.808313
2   infortunato              5        0.670328               0.370948
3     doglienza              5        0.654688               0.783043
4          tira              2        0.662917               0.267014
5       pesanti              4        0.622229               0.039931
6        altero              1        0.678515               0.783545
7      dimostro              1        0.675299               0.000000
8          beno              1        0.675234               0.229231
9         porge              1        0.671657               0.624813
10          ont              3        0.618409               0.301507
11         foll              3        0.611994               0.296017
12   canoscenza              3        0

                 Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0                sorte              4        0.364827               0.193995
1               godono              1        0.359812               0.008120
2             raffreni              1        0.358526               0.823089
3         persecutrice              4        0.360903               0.381179
4               durano              1        0.357082               0.427461
5       estraordinaria              1        0.350111               0.263348
6              sedotta              4        0.359150               1.000000
7              fortune              1        0.345329               0.150762
8               tempre              4        0.359216               0.491726
9              intrica              1        0.338925               0.000000
10           congiurar              2        0.373886               0.735985
11           trascinar              3        0.366898               0.335502

            Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0          amando              5        0.444278               0.781946
1       tollerare              3        0.420362               0.301493
2         trovata              1        0.467928               0.124442
3      pochissimi              2        0.436319               0.452422
4      campicello              1        0.460480               0.931331
5         crediti              3        0.401128               0.012875
6       inclinare              5        0.405298               0.431326
7         farvela              3        0.419762               0.082566
8        ottenuta              2        0.432758               0.384106
9      conoscervi              2        0.406250               0.555910
10     belsonetto              4        0.408538               0.318854
11         uccida              2        0.403718               0.422550
12     trattenuta              1        0.407944               0

### TOPOS: NOIA

In [144]:
for periodo in lista_periodi_letterari_cade:
    try:
        print("###" + periodo + "###")
        df_periodo = similar_words_per_topos("noia", 5, 10, periodo)
        print(df_periodo[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + periodo)

###CADE_1_duecento_poetica_e_prosa Medievo_cade###
             Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0            croia              5        0.665595               0.382147
1              nòi              5        0.617908               0.998189
2          donando              5        0.611843               0.026583
3          soffrir              3        0.610150               1.000000
4        dubitanza              5        0.611097               0.172665
5        dannaggio              1        0.665845               0.479178
6          gioiosa              2        0.597623               0.608279
7           noiosa              1        0.662352               0.602871
8           piacer              1        0.659456               0.215251
9             moro              1        0.655920               0.346832
10          calere              3        0.580669               0.505128
11         leggera              4        0.561214               0.497462


                  Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0           occupazione              3        0.513697               0.239834
1              insipida              5        0.502407               0.000000
2            espiazione              1        0.556944               0.443404
3   fisicainsufficienza              1        0.541837               0.046521
4        maliziosamente              2        0.493555               0.083736
5            mescolasse              1        0.538021               1.000000
6             renitenza              1        0.536904               0.866015
7              parlerei              1        0.534246               0.229532
8           maggioragio              1        0.530807               0.516315
9                 vinco              1        0.527893               0.140236
10             pochetto              4        0.512469               0.398202
11           prevenisse              4        0.490863          

             Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0      moderazione              5        0.526792               0.223248
1         postanca              1        0.600066               0.592321
2        intessere              2        0.555101               0.109507
3            pigra              2        0.552899               0.424796
4        soverchie              2        0.552433               0.269270
5       esasperata              1        0.588041               0.183192
6         alterato              2        0.531084               0.453833
7   sentimentalità              1        0.584686               0.906526
8      distrazioni              1        0.584250               0.928930
9          funerea              2        0.548545               0.125205
10          usando              4        0.493148               0.199965
11           polpo              3        0.495239               0.695511
12      attingendo              3        0.502738  

### TOPOS: TEMPORALE/PIOGGIA

In [145]:
for periodo in lista_periodi_letterari_cade:
    try:
        print("###" + periodo + "###")
        df_periodo = similar_words_per_topos("temporale", 5, 10, periodo)
        print(df_periodo[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + periodo)

###CADE_1_duecento_poetica_e_prosa Medievo_cade###
           Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0         finita              4        0.663681               0.942071
1           ehno              5        0.682134               0.905747
2          mesta              1        0.723089               0.768938
3        compone              3        0.665293               0.252890
4        lassuso              1        0.718069               0.297212
5     abbellisce              1        0.714830               0.594627
6        bollati              1        0.709651               0.484622
7         sanare              1        0.709456               0.241036
8   furtivamente              1        0.707744               0.374117
9          botta              4        0.690145               0.712751
10      liberare              4        0.673643               0.583320
11       delizie              3        0.633853               0.892370
12        ultima          

                Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0          quattroore              5        0.830613               0.641393
1              caduti              5        0.823194               0.929961
2        annunciavano              4        0.791310               0.862286
3           cosenuove              1        0.843072               0.528883
4             cavasse              2        0.775070               0.700983
5          mezzanotte              2        0.794433               1.000000
6              maisen              1        0.835181               0.427470
7             cordone              2        0.799911               0.933269
8             danzica              1        0.833440               0.641160
9               cacio              1        0.832963               0.046375
10  senzainterruzione              3        0.773208               0.000000
11  diluviouniversale              1        0.791277               0.468509
12         s

           Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0       cornetta              2        0.615199               0.986782
1       mitigato              4        0.600195               0.031547
2      rosseggia              2        0.658737               0.066333
3     argentooro              5        0.613718               0.526553
4   soletramonta              3        0.614991               0.076727
5      piovevano              1        0.688945               0.374266
6     incessanti              2        0.651099               0.371713
7   abbeveratoio              1        0.686845               0.535873
8       tramonta              4        0.606441               0.011384
9          mosso              1        0.686709               0.355879
10    ghiacciata              4        0.586600               0.761812
11       brocche              3        0.589521               0.000000
12         calar              2        0.589115               0.089782
13    

In [146]:
for periodo in lista_periodi_letterari_cade:
    try:
        print("###" + periodo + "###")
        df_periodo = similar_words_per_topos("pioggia", 5, 10, periodo)
        print(df_periodo[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + periodo)

###CADE_1_duecento_poetica_e_prosa Medievo_cade###
             Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0             cadi              2        0.810146               0.685414
1            dardi              1        0.834051               0.618508
2        defendere              1        0.830337               0.574389
3         sorpreso              2        0.772014               0.909691
4         verrebbe              1        0.828277               0.071341
5         seguiamo              2        0.813972               0.671894
6            riede              1        0.827612               0.066627
7             ista              2        0.804180               0.800990
8             cità              1        0.825347               0.927533
9         appetito              1        0.823203               0.676917
10            suto              3        0.797627               0.601495
11          adotta              3        0.782926               1.000000


           Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0       grondano              5        0.633810               0.075346
1           neve              5        0.598513               0.236496
2      stillando              5        0.612633               0.141618
3   serpeggiando              5        0.606815               0.000000
4      sanguigne              1        0.648847               0.072208
5        scaglie              3        0.578034               0.409582
6       scendono              2        0.603124               0.064844
7      mattutino              1        0.631702               0.416814
8    infiammando              5        0.575677               0.883920
9          pesce              1        0.623427               0.435148
10       dittamo              4        0.572365               0.867645
11       bagnati              3        0.549944               0.611438
12         vapor              1        0.594161               0.803765
13    

                Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0          primegocce              5        0.492644               0.034309
1              dànoia              3        0.455405               0.428772
2           nevischio              5        0.453330               0.581004
3       qualchegoccia              1        0.475421               0.492119
4         sgocciolare              5        0.439904               0.329223
5             durando              3        0.441875               0.246333
6           fischiata              5        0.447505               0.557657
7                plac              5        0.473702               0.307321
8             scrosci              1        0.443609               0.786868
9          schiantava              2        0.428512               1.000000
10  quartieripopolari              1        0.439093               0.239216
11        grossegocce              4        0.425661               0.806208
12      punt

### TOPOS: GIOVINEZZA

In [147]:
for periodo in lista_periodi_letterari_cade:
    try:
        print("###" + periodo + "###")
        df_periodo = similar_words_per_topos("giovinezza", 5, 10, periodo)
        print(df_periodo[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + periodo)

###CADE_1_duecento_poetica_e_prosa Medievo_cade###
La chiave non esiste nel modelloCADE_1_duecento_poetica_e_prosa Medievo_cade
###CADE_2_dolce_stil_novo_cade###
              Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0         temperata              5        0.722257               0.228450
1         autentica              5        0.672863               0.549774
2         snellezza              5        0.643400               0.657204
3       adolescenza              5        0.664831               0.134394
4             senio              5        0.624903               0.612745
5      acrescimento              4        0.623846               0.270335
6    principalparte              1        0.681246               0.058339
7          affabile              1        0.678534               0.017587
8          imperciò              1        0.667573               0.212041
9       pigliandola              1        0.667076               0.000000
10         deeavere     

           Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0          etade              1        0.696906               0.151707
1         senili              5        0.626438               0.342831
2         toscar              4        0.614718               0.429439
3         muoion              5        0.612552               0.339804
4         scorda              1        0.665806               0.178724
5     risplendea              3        0.605545               1.000000
6      benedissi              3        0.612228               0.423507
7          vivrò              1        0.659498               0.264605
8      lagrimoso              1        0.658872               0.483199
9      giovenili              2        0.620206               0.743725
10         solar              2        0.592949               0.000000
11      evircoma              2        0.611347               0.431627
12   vagoaspetto              1        0.615013               0.151507
13    

                Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0              goditi              5        0.448329               0.666225
1          avvampante              5        0.454298               0.560677
2            gioventù              5        0.452043               0.731262
3         adolescenza              5        0.446972               0.410110
4            indomita              1        0.484571               0.830502
5          anniinteri              4        0.435082               0.250923
6   indissolubilmente              2        0.442290               0.426488
7            maturità              1        0.466981               0.580492
8            sfiorire              4        0.414263               0.374132
9         coincidente              1        0.465477               0.711242
10           fatidica              2        0.437314               0.209487
11          stroncata              3        0.419094               0.678278
12       fan

In [148]:
for periodo in lista_periodi_letterari_cade:
    try:
        print("###" + periodo + "###")
        df_periodo = similar_words_per_topos("giovane", 5, 10, periodo)
        print(df_periodo[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + periodo)

###CADE_1_duecento_poetica_e_prosa Medievo_cade###
            Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0     svergognato              5        0.621368               0.111001
1         vecchio              5        0.556503               0.711318
2        superbio              4        0.538222               0.282143
3          puniti              5        0.536110               0.195296
4   disubbidienza              1        0.592909               0.803943
5           pazzo              5        0.554345               0.552598
6          pagolo              1        0.587664               0.376755
7        bugiardo              1        0.579464               0.284369
8         formoso              5        0.530899               0.000000
9         rimasto              1        0.576496               0.307168
10      domandata              1        0.556424               0.351619
11          lodai              1        0.527250               0.767809
12        sal

             Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0   gentilimaniere              5        0.492900               0.085368
1          garbato              3        0.465363               0.209995
2     ventottoanni              4        0.473296               0.418568
3     giudicandolo              4        0.465815               0.399932
4         modanese              5        0.485759               0.448293
5         navigava              1        0.520139               0.725653
6           vegeto              2        0.481376               0.172672
7      dongabriele              5        0.462411               0.452851
8    figurasferica              2        0.460561               0.000000
9      trasportate              1        0.493394               0.653723
10         soldato              3        0.435118               1.000000
11        radunava              2        0.450461               0.253280
12         curiale              4        0.441703  

            Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0     avventuroso              5        0.413160               0.414278
1         educato              5        0.416493               0.579854
2      belgiovane              5        0.420077               0.672689
3        ventanni              2        0.410219               0.933495
4       fiammingo              1        0.444462               0.323476
5      novantadue              2        0.424786               0.132036
6    cinquantenne              1        0.439507               0.074927
7           ebrea              1        0.438597               0.921281
8        invalido              1        0.435865               0.624586
9       simpatico              5        0.396601               0.334933
10      fanciulla              2        0.394913               1.000000
11       ritornar              2        0.390231               0.884601
12      accoppato              1        0.400825               0

### TOPOS: BACIO

In [149]:
for periodo in lista_periodi_letterari_cade:
    try:
        print("###" + periodo + "###")
        df_periodo = similar_words_per_topos("bacio", 5, 10, periodo)
        print(df_periodo[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + periodo)

###CADE_1_duecento_poetica_e_prosa Medievo_cade###
La chiave non esiste nel modelloCADE_1_duecento_poetica_e_prosa Medievo_cade
###CADE_2_dolce_stil_novo_cade###
La chiave non esiste nel modelloCADE_2_dolce_stil_novo_cade
###CADE_3_petrarchismo_cade###
           Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0         teodor              2        0.805395               0.305017
1     tornandomi              2        0.789928               0.147558
2      vocebassa              3        0.776331               0.563402
3     ricordarle              1        0.828244               0.958021
4       grandama              1        0.825469               0.299323
5        cristal              2        0.803213               0.138497
6       rendessi              1        0.823614               0.207936
7          atena              1        0.823604               0.908533
8    trapassando              2        0.780621               0.142550
9       concluse              1      

             Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0           sanato              2        0.640809               0.847847
1          piegato              1        0.681961               0.173687
2         annodata              1        0.678755               0.974269
3          riposar              1        0.674279               0.029545
4         puntando              1        0.671859               0.142005
5         ateniese              1        0.669454               0.899615
6         rinvenne              1        0.667282               0.682965
7          tengasi              3        0.627031               0.858132
8        coglierne              1        0.664285               0.000000
9   abbracciandola              1        0.663004               0.512117
10          caschi              4        0.642460               0.082060
11      procedessi              4        0.639259               0.014470
12         tiepida              2        0.619466  

             Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0          baciato              5        0.440950               1.000000
1     maternamente              2        0.440119               0.023414
2         baciarlo              4        0.424567               0.674246
3        abbraccio              1        0.457999               0.347178
4           chinai              4        0.428672               0.667089
5       ubbidiente              3        0.439447               0.427330
6        sfiorarla              3        0.434479               0.745241
7           ponevo              2        0.429902               0.078364
8         piegarla              5        0.423673               0.203232
9     ringraziarlo              1        0.444165               0.650862
10          deposi              4        0.444952               0.329732
11      scambiammo              3        0.419243               0.451355
12      arrischiai              4        0.441316  

### TOPOS: LUNA

In [150]:
for periodo in lista_periodi_letterari_cade:
    try:
        print("###" + periodo + "###")
        df_periodo = similar_words_per_topos("luna", 5, 10, periodo)
        print(df_periodo[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + periodo)

###CADE_1_duecento_poetica_e_prosa Medievo_cade###
               Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0       maravigliano              5        0.722093               0.359412
1           cadranno              5        0.681024               0.862163
2             spessi              5        0.702041               0.761630
3          avvengono              5        0.698345               0.000000
4   spessointerviene              5        0.652571               1.000000
5             stelle              5        0.641592               0.755555
6       settepianeti              5        0.657599               0.558453
7          rarevolte              5        0.646019               0.625662
8               sole              5        0.657416               0.624601
9           oscurata              1        0.679978               0.883617
10          apparire              3        0.611727               0.596480
11           formate              1        0.5498

            Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0          stelle              5        0.485318               0.000000
1          fosche              3        0.486780               0.732867
2            orli              4        0.491285               0.320042
3            nubi              3        0.493711               0.957941
4      occidental              2        0.499997               0.031651
5         pianeta              2        0.496310               0.900353
6            nube              2        0.495066               0.872951
7       orizzonte              2        0.495520               1.000000
8   giranointorno              3        0.497916               0.909512
9      splendente              5        0.487299               0.823922
10        pianeti              2        0.475871               0.925494
11         fumosa              1        0.466355               0.512380
12     primiraggi              1        0.465889               0

### TOPOS: SILENZIO

In [151]:
for periodo in lista_periodi_letterari_cade:
    try:
        print("###" + periodo + "###")
        df_periodo = similar_words_per_topos("silenzio", 5, 10, periodo)
        print(df_periodo[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + periodo)

###CADE_1_duecento_poetica_e_prosa Medievo_cade###
              Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0      temperamento              5        0.802391               0.602324
1           ubriaco              2        0.782986               0.545135
2         difension              2        0.780305               0.150779
3              gote              1        0.817983               0.285653
4         leggiadro              1        0.817278               0.635906
5            lucano              3        0.768424               0.201213
6          assembra              2        0.770912               0.234490
7        aspetterai              4        0.776830               0.093879
8          parlarmi              1        0.813920               0.124397
9         ritornerà              2        0.773297               0.132265
10         qualcuno              1        0.789578               0.185202
11            sanar              1        0.785487           

           Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0   ingratamente              5        0.455500               0.322708
1     nottebruna              5        0.393475               0.307609
2        attenti              3        0.386523               0.205957
3       sibilava              5        0.379005               0.462173
4      bisbiglio              1        0.401921               0.050892
5        loquace              3        0.384411               0.149736
6          oblio              1        0.396417               1.000000
7   osservatrice              3        0.386811               0.373164
8      ricopriva              1        0.394381               0.286403
9   ingratissimo              1        0.393054               0.377385
10    atteggiato              4        0.388028               0.406918
11    plausibili              2        0.383650               0.310497
12        ridire              1        0.388548               0.079021
13    

               Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0   silenzioprofondo              5        0.379404               0.347047
1      lungosilenzio              3        0.345214               0.033633
2       sprofondasse              5        0.361329               0.047471
3          risonando              1        0.332991               0.638145
4                evi              2        0.334680               0.114648
5         solitudine              5        0.357387               0.268865
6         ultimenote              1        0.329399               0.205962
7      lasciòpassare              1        0.329012               0.345007
8             atonia              2        0.330588               0.002434
9       racchiudesse              4        0.348327               0.111633
10           regnava              3        0.348581               0.515221
11        tiraifuori              2        0.336045               0.323174
12   lungointervallo     

### TOPOS: AMICIZIA

In [152]:
for periodo in lista_periodi_letterari_cade:
    try:
        print("###" + periodo + "###")
        df_periodo = similar_words_per_topos("amicizia", 5, 10, periodo)
        print(df_periodo[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + periodo)

###CADE_1_duecento_poetica_e_prosa Medievo_cade###
           Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0         vantar              5        0.752079               0.024870
1          laudi              1        0.833222               0.133611
2         impone              2        0.764691               0.258152
3      disfaccia              3        0.767038               0.890192
4       consenta              2        0.770061               0.177929
5     neghittoso              1        0.822865               0.345373
6       temporal              1        0.819961               0.415033
7      proveduto              1        0.819723               0.144091
8        apparer              1        0.818731               0.262022
9          fingi              1        0.818493               0.045127
10      sostenne              3        0.751409               0.521387
11       importa              2        0.751574               0.032266
12         brame          

               Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0            vincolo              1        0.588092               0.059378
1          contrarsi              5        0.527060               0.058983
2            ambisco              1        0.549801               0.774736
3         emulazione              1        0.544258               0.221368
4          reciproco              2        0.523557               0.602030
5      bellezzaumana              2        0.520445               0.707858
6           benefizi              1        0.538433               0.208975
7        mostrandoci              1        0.537947               0.640947
8        correlativo              3        0.499616               0.305070
9         professato              4        0.489009               0.479493
10  qualunquemaniera              2        0.492216               0.214920
11       fidelissimo              2        0.496318               0.038660
12         contrassi     

                 Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0               tandem              5        0.429805               0.024549
1   sempliceconoscenza              5        0.481823               0.000000
2                siimi              4        0.427126               0.801816
3            relazione              2        0.431866               0.411538
4               amelia              1        0.461606               0.075395
5     tenerezzapaterna              2        0.440356               0.255402
6         veraamicizia              3        0.418271               0.153217
7              stabilì              1        0.454569               0.419297
8          avvicinarlo              4        0.421794               0.152441
9              vincolo              3        0.421701               0.032103
10            ricevete              2        0.417705               0.223022
11          informarlo              1        0.422585               0.072870

In [153]:
for periodo in lista_periodi_letterari_cade:
    try:
        print("###" + periodo + "###")
        df_periodo = similar_words_per_topos("amico", 5, 10, periodo)
        print(df_periodo[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + periodo)

###CADE_1_duecento_poetica_e_prosa Medievo_cade###
             Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0            leale              2        0.524454               0.127498
1              car              2        0.504186               0.436742
2      sostenitore              1        0.528540               0.146032
3             caro              5        0.480985               0.000000
4           intero              4        0.475875               0.418740
5   messergiovanni              5        0.471311               0.749271
6         riprenda              1        0.521514               0.510406
7          ingegna              3        0.481700               0.202044
8           mostro              1        0.515082               0.847830
9          gentile              1        0.513759               0.228771
10          aitare              4        0.473830               0.154003
11      buoniamici              1        0.472081               0.517773


              Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0           paesano              3        0.391672               0.000000
1    carissimoamico              4        0.374255               0.423097
2        confidente              2        0.391349               0.298214
3           daniele              3        0.379979               0.391086
4          arsenale              2        0.363872               0.473142
5   observandissimo              5        0.386598               0.643545
6           galante              1        0.388202               0.924065
7        stimandolo              1        0.387819               0.550526
8         servidore              1        0.384682               0.560586
9        gentiluomo              3        0.369129               0.737473
10   fattoarrestare              1        0.395976               1.000000
11      fidelissimo              3        0.382516               0.779108
12         cornelia              4    

                  Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0             catellani              1        0.402462               0.180116
1               bernabò              1        0.394950               0.174489
2       riconobbisubito              2        0.376174               0.091860
3             rassicuri              2        0.364056               0.873294
4              coetaneo              2        0.372460               0.327612
5           fidatissimo              5        0.362682               0.207649
6          garbatissimo              2        0.358638               1.000000
7            impiccarsi              1        0.365697               0.493916
8             eugenioiv              3        0.363539               0.097661
9        carissimoamico              1        0.362601               0.328304
10         onoratissimo              2        0.362970               0.237431
11                 ruvo              1        0.355617          

### TOPOS: SOLITUDINE

In [154]:
for periodo in lista_periodi_letterari_cade:
    try:
        print("###" + periodo + "###")
        df_periodo = similar_words_per_topos("solitudine", 5, 10, periodo)
        print(df_periodo[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + periodo)

###CADE_1_duecento_poetica_e_prosa Medievo_cade###
La chiave non esiste nel modelloCADE_1_duecento_poetica_e_prosa Medievo_cade
###CADE_2_dolce_stil_novo_cade###
La chiave non esiste nel modelloCADE_2_dolce_stil_novo_cade
###CADE_3_petrarchismo_cade###
La chiave non esiste nel modelloCADE_3_petrarchismo_cade
###CADE_4_boccaccio_e_umanesimo_cade###
            Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0         diserta              5        0.496965               0.891872
1       rimozione              5        0.520429               0.239550
2         ioconda              4        0.468498               0.158128
3       consortio              1        0.524197               0.847784
4         declini              2        0.500659               0.664754
5     accerchiato              1        0.512831               1.000000
6          goderà              1        0.509040               0.516490
7      frequentia              4        0.494978               0.776069
8 

              Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0          isolarsi              1        0.443692               0.338018
1      segregazione              1        0.438759               0.407789
2       desolazione              1        0.437909               0.886730
3         immensità              1        0.435023               0.610762
4     vastacampagna              1        0.432597               0.121501
5    disoccupazione              3        0.413777               0.414091
6   cattivipensieri              5        0.413456               0.511198
7            snerva              1        0.426988               0.204412
8          verdezza              1        0.426752               0.409855
9          dimorate              1        0.423819               0.000000
10     vialedeserto              1        0.428260               0.830201
11        pigliarne              1        0.426682               0.307845
12         nuvolosi              3    

In [155]:
for periodo in lista_periodi_letterari_cade:
    try:
        print("###" + periodo + "###")
        df_periodo = similar_words_per_topos("solitario", 5, 10, periodo)
        print(df_periodo[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + periodo)

###CADE_1_duecento_poetica_e_prosa Medievo_cade###
La chiave non esiste nel modelloCADE_1_duecento_poetica_e_prosa Medievo_cade
###CADE_2_dolce_stil_novo_cade###
La chiave non esiste nel modelloCADE_2_dolce_stil_novo_cade
###CADE_3_petrarchismo_cade###
               Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0           selvagge              2        0.704644               0.161731
1             battro              2        0.682204               0.507065
2        cacciatrice              1        0.764974               0.213919
3            pastori              1        0.763729               0.904949
4             snelle              2        0.694179               1.000000
5          saettando              1        0.755854               0.895050
6                ima              1        0.749699               0.033001
7            bifolci              1        0.749014               0.361334
8            nudrito              5        0.674659               0.4601

             Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0      quartierino              5        0.569826               0.585536
1             gaio              3        0.540235               0.002362
2          pecchia              2        0.579130               0.000000
3          foresta              3        0.572232               0.474236
4           errava              5        0.532363               0.768967
5           rurale              1        0.603484               0.127006
6        solitaria              1        0.593277               0.532431
7          guidami              2        0.537512               0.512301
8        delizioso              4        0.547418               0.425826
9         vivevamo              3        0.540256               0.303895
10        passarle              2        0.538774               0.443628
11           gustò              3        0.525814               0.521631
12  particolarmodo              2        0.528222  

            Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0        sperduto              4        0.433362               0.144589
1     riconduceva              3        0.457241               0.437379
2          leccio              2        0.435990               0.186060
3         mammana              5        0.423034               0.545838
4      piacentino              2        0.441032               0.583053
5      campagnolo              3        0.423835               1.000000
6       passeggia              2        0.443308               0.223014
7       derelitto              1        0.470482               0.691694
8     presuntuoso              1        0.468734               0.441229
9   pochefamiglie              1        0.467858               0.228909
10      bisbetico              1        0.419672               0.575887
11        vermine              4        0.410806               0.757107
12        agreste              2        0.407538               0

### TOPOS: INFINITO

In [156]:
for periodo in lista_periodi_letterari_cade:
    try:
        print("###" + periodo + "###")
        df_periodo = similar_words_per_topos("infinito", 5, 10, periodo)
        print(df_periodo[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + periodo)

###CADE_1_duecento_poetica_e_prosa Medievo_cade###
             Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0       accostarsi              5        0.873721               1.000000
1      compunzione              5        0.828131               0.548660
2            pater              1        0.849135               0.136394
3    soddisfacendo              1        0.848654               0.263673
4        solleciti              2        0.830452               0.716888
5        conchiudo              1        0.846586               0.053397
6           strema              3        0.812192               0.449256
7          pulirsi              1        0.843197               0.025652
8            druda              1        0.843168               0.595122
9          capitar              1        0.841842               0.759022
10        affligga              1        0.822899               0.122032
11        fuggirlo              1        0.822146               0.728663


                Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0         interminato              5        0.593429               0.159206
1      spacioinfinito              5        0.521996               0.000000
2              sarebe              5        0.505493               0.169526
3           intensiva              3        0.507796               0.143972
4             inmenso              5        0.499072               0.330922
5       interminabile              5        0.530236               0.317329
6            inmobile              2        0.507151               0.262636
7         singularità              5        0.514909               0.325775
8           individuo              1        0.507810               0.330816
9            infinita              2        0.506070               0.506170
10          operatore              4        0.489580               1.000000
11      minorraggione              1        0.501551               0.282013
12  mondiinn

                Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0            regnerai              5        0.476475               0.430878
1            oceanico              2        0.445234               0.000000
2         germogliare              5        0.435280               0.229660
3         senzalimiti              1        0.472582               0.906963
4            universo              1        0.468568               0.015359
5           ascendere              1        0.467954               0.176632
6          alimentato              4        0.424353               0.173600
7          possedersi              3        0.434504               0.221803
8    crescevacresceva              1        0.462226               0.430350
9          dissolveva              1        0.460079               0.844422
10            incanta              1        0.454589               0.820978
11        raggisolari              2        0.425734               0.559610
12          

## ANALISI PER AUTORE

In [157]:
os.chdir(path_autori_cade)

lista_autori_cade = ['CADE_Alessandro Manzoni_cade', 'CADE_Dante Alighieri_cade', 
                     'CADE_Dino Buzzati_cade', 'CADE_Francesco Petrarca_cade', 
                     'CADE_Gabriele D\'Annunzio_cade', 'CADE_Giacomo Leopardi_cade', 
                     'CADE_Giovanni Boccaccio_cade', 'CADE_Giuseppe Parini_cade', 
                     'CADE_Italo Calvino_cade', 'CADE_Italo Svevo_cade', 
                     'CADE_Ludovico Ariosto_cade', 'CADE_Luigi Pirandello_cade', 
                     'CADE_Pier Paolo Pasolini_cade', 'CADE_Primo Levi_cade', 
                     'CADE_Torquato Tasso_cade', 'CADE_Ugo Foscolo_cade', 
                     'CADE_Umberto Eco_cade', 'CADE_Vittorio Alfieri_cade']

### TOPOS: PASTORE

In [158]:
for autore in lista_autori_cade:
    try:
        print("###" + autore + "###")
        df_autore = similar_words_per_topos("pastore", 5, 10, autore)
        print(df_autore[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + autore)

###CADE_Alessandro Manzoni_cade###
             Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0            palpa              5        0.555195               0.000000
1       sonnolento              5        0.591756               0.230211
2        strascina              5        0.544165               0.404171
3          recasse              4        0.521216               0.457130
4     scarmigliata              1        0.572036               0.335586
5     raggiungerlo              3        0.518151               0.702970
6        cacciarlo              2        0.521177               0.789275
7          beccaio              5        0.514292               0.581357
8       infiammati              1        0.553139               0.718782
9       lungabarba              5        0.537328               0.174114
10       insidiare              4        0.564360               0.433856
11        difforme              4        0.505375               0.457434
12  potevaarriva

           Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0        plebeio              5        0.500871               0.508062
1       allevato              4        0.518238               0.528029
2    poveradonna              1        0.616530               0.525984
3             ca              5        0.500223               0.439106
4        agapito              5        0.514522               0.820477
5        agreste              4        0.518662               0.151010
6    giudicavano              2        0.520414               0.281760
7       leonardo              2        0.519353               0.536479
8      nutricato              1        0.581099               0.421916
9          ebreo              1        0.579304               0.531359
10       nudrito              4        0.479566               0.339487
11       scettro              1        0.507227               0.829131
12  solennissimo              4        0.454092               0.442230
13    

             Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0        pecorelle              5        0.647254               0.222485
1        alberetti              5        0.602384               0.560949
2           danese              5        0.617686               0.624251
3         levriere              5        0.614675               0.178641
4          montoni              3        0.606849               0.957307
5     rivoltoverso              1        0.666337               0.714159
6          agnelli              4        0.591609               0.015746
7        meridiano              2        0.624872               0.956169
8         buttavia              1        0.659071               0.000000
9         invalidi              1        0.658877               0.696468
10     minacciasse              2        0.549592               0.050275
11   abbandonavano              3        0.534002               0.176336
12  sentitesentite              1        0.565030  

           Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0        ridenti              1        0.904773               0.737750
1        sparite              1        0.902915               0.682675
2      pastorali              1        0.900760               0.000000
3      splendere              1        0.895919               0.435327
4        voluttà              1        0.893635               0.191151
5        avvolto              2        0.844746               0.258364
6     attenderlo              2        0.855165               0.912024
7     frettolose              1        0.889212               0.402143
8       difforme              1        0.888131               0.230901
9         tumulo              1        0.887303               0.296128
10     torneremo              2        0.780514               0.138202
11       fornito              2        0.771625               0.917735
12      smanioso              4        0.766994               0.304337
13    

### Altre parole correlate

In [159]:
for autore in lista_autori_cade:
    try:
        print("###" + autore + "###")
        df_autore = similar_words_per_topos("pastori", 5, 10, autore)
        print(df_autore[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + autore)

###CADE_Alessandro Manzoni_cade###
               Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0          scoprisse              5        0.695229               0.090081
1   personificazione              1        0.746664               0.216386
2   proprisentimenti              1        0.735537               0.885521
3           rabbiosi              2        0.637248               0.182112
4        sacerdotale              1        0.728692               0.033465
5           sdegnati              5        0.605960               0.000000
6     qualunquesorta              1        0.723306               0.302917
7         sempiterno              1        0.721390               0.181299
8           britanno              1        0.718597               0.153169
9            tribuni              1        0.717582               0.257229
10           lasciam              4        0.564558               0.044823
11       subordinati              4        0.559826              

          Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0         goffi              5        0.786664               0.015099
1     selvatici              5        0.767760               0.018107
2     guardiani              5        0.794762               0.282772
3       sghembo              5        0.770104               0.036629
4   svergognati              2        0.787927               0.000000
5      scaffali              2        0.781430               1.000000
6        svelti              5        0.760767               0.760642
7        spiche              4        0.718883               0.801402
8        giochi              1        0.834220               0.252561
9       piccini              2        0.732748               0.305809
10      muggito              2        0.696297               0.489275
11   susurrando              1        0.724720               0.734299
12       arguti              1        0.691720               0.665497
13       vipere     

           Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0           bovi              5        0.765694               0.056536
1           magi              1        0.818894               0.175602
2       facondia              5        0.705768               0.246982
3       sagacità              5        0.700118               0.792451
4       rispuosi              1        0.806547               0.001508
5         focosi              2        0.748235               0.078313
6          spazi              2        0.747045               0.372530
7      dimandata              1        0.796800               0.913804
8   maravigliosi              1        0.796686               0.527200
9      sconfitte              1        0.795205               0.558662
10       lasciam              4        0.666573               0.492099
11    dimensioni              1        0.697704               0.724336
12          gufi              1        0.695321               0.517904
13    

          Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0      secolari              2        0.662164               0.028870
1        gregge              1        0.722110               0.442950
2      spargete              3        0.627303               0.539774
3          cani              5        0.635987               0.386182
4          lupi              3        0.649289               0.189830
5     guerrieri              4        0.619192               0.507108
6     spergiuri              5        0.619585               0.849276
7         avari              5        0.614858               0.454913
8      chiamati              1        0.695774               0.451602
9         aurei              2        0.641695               0.471616
10  promettesse              4        0.622000               1.000000
11      riunire              2        0.621253               0.410990
12       feccia              1        0.629786               0.088644
13   combattono     

### TOPOS: AMORE

In [160]:
for autore in lista_autori_cade:
    try:
        print("###" + autore + "###")
        df_autore = similar_words_per_topos("amore", 5, 10, autore)
        print(df_autore[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + autore)

###CADE_Alessandro Manzoni_cade###
             Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0        implorava              3        0.402390               0.014004
1     figliuolanza              3        0.405162               0.000000
2     imperterrito              4        0.398915               0.188675
3   propriavolontà              2        0.409957               0.945791
4         figurina              1        0.453780               0.146172
5   commiserazione              1        0.452539               0.987650
6         disporsi              2        0.399206               0.017770
7   disinteressata              1        0.449755               0.279407
8    rimproverando              1        0.448448               0.524562
9         assumere              1        0.448333               0.959948
10      sacrificii              4        0.388036               0.456904
11            zelo              1        0.402805               0.107071
12      ricordia

           Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0      olocausto              1        0.333172               0.528683
1      offrirgli              5        0.317346               0.000000
2       amplesso              4        0.323659               0.227227
3           ambi              3        0.312718               0.347391
4     indomabile              1        0.322625               0.579093
5        persino              3        0.328409               0.696482
6     indulgenza              1        0.321136               0.856976
7        accogli              1        0.318400               0.151273
8       eleonora              1        0.317916               0.534198
9     inebriarsi              1        0.312843               0.703573
10         tendo              1        0.321526               0.513242
11      astratto              4        0.328689               0.226310
12          amor              4        0.319980               0.068914
13    

           Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0          iroso              5        0.421239               0.000000
1   insegnamento              1        0.477957               0.099058
2     assassinio              1        0.465131               0.149306
3       vendette              3        0.407445               0.220743
4       ispirato              5        0.419904               0.900500
5        avidità              3        0.396944               0.371538
6   fervidamente              2        0.408597               0.158051
7        falsità              1        0.446130               0.753100
8   farglisapere              3        0.398662               0.384867
9      lusingata              2        0.413387               0.461939
10      sposarlo              2        0.374184               0.030082
11       voltava              2        0.364146               0.110572
12      ascoltai              2        0.377506               1.000000
13    

          Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0     reciproco              5        0.673596               0.057837
1     platonico              5        0.650542               0.376991
2     interiore              5        0.656031               0.022675
3    disciplina              5        0.640964               0.086424
4       intatto              1        0.736868               0.000000
5    spirituale              5        0.636639               1.000000
6       irreale              1        0.713325               0.474865
7        giunge              5        0.596236               0.847060
8   esseriumani              3        0.586422               0.005886
9     razionale              1        0.699106               0.008900
10    concordia              4        0.591835               0.439208
11         nata              4        0.583838               0.754689
12    inducesse              4        0.582932               0.588973
13       nativo     

### Altre parole correlate

In [161]:
for autore in lista_autori_cade:
    try:
        print("###" + autore + "###")
        df_autore = similar_words_per_topos("amor", 5, 10, autore)
        print(df_autore[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + autore)

###CADE_Alessandro Manzoni_cade###
                Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0   verginesantissima              5        0.484296               0.228542
1                ahno              4        0.483611               0.520660
2    lasciatemiandare              2        0.514138               1.000000
3          zittozitto              2        0.506228               0.655607
4            alterate              5        0.501663               0.355974
5            vadavada              5        0.486219               0.116881
6           aiutatemi              1        0.547733               0.396338
7             rendete              1        0.546953               0.197437
8         lasciandare              1        0.543529               0.000000
9             pregate              3        0.465458               0.968572
10             patrio              4        0.465930               0.748859
11          disciolta              1        0.466980 

           Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0         abbiti              2        0.442769               0.860031
1    trasformava              5        0.435975               0.534686
2     ricordarti              5        0.425119               0.739868
3      cariuccio              4        0.407513               0.184221
4       cacciate              3        0.433168               0.418769
5   ringraziarti              4        0.407374               0.083068
6      benedette              3        0.416775               0.087372
7       fraterno              3        0.415050               0.513103
8       sospinto              3        0.414460               0.203719
9    voglimibene              1        0.453952               0.442334
10        starmi              3        0.401405               0.639129
11    guardatevi              3        0.390332               0.417028
12      pocacura              1        0.409396               0.409026
13    

             Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0            amore              4        0.419075               0.724282
1             goda              1        0.443328               0.777037
2          castità              1        0.424619               0.394387
3          consumi              1        0.421279               0.140562
4        tantafede              1        0.420889               0.000000
5         dolcezza              1        0.414633               0.827999
6         impresso              1        0.413988               0.184742
7           aversa              4        0.377452               0.797295
8          affetto              1        0.413337               0.491569
9           martìr              1        0.410056               0.212785
10      convengono              1        0.388023               0.073260
11          vodire              4        0.363703               0.736204
12       mostraste              3        0.366111  

           Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0           mori              3        0.688005               0.988192
1        indegna              2        0.702647               0.823133
2        ferisci              3        0.664000               0.179893
3           cada              2        0.722396               0.000000
4           fora              1        0.759842               0.662825
5         poichè              4        0.651736               0.272967
6   accostandosi              1        0.757342               0.547318
7          viver              4        0.622031               1.000000
8       periglio              2        0.718998               0.313635
9      obbrobrio              2        0.660398               0.729856
10  occultamente              2        0.627509               0.020122
11          duro              1        0.688455               0.412118
12         merto              3        0.635375               0.660702
13    

In [162]:
for autore in lista_autori_cade:
    try:
        print("###" + autore + "###")
        df_autore = similar_words_per_topos("innamorato", 5, 10, autore)
        print(df_autore[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + autore)

###CADE_Alessandro Manzoni_cade###
              Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0          burlesco              1        0.704896               0.211310
1            legava              2        0.653435               0.110347
2       discorrendo              2        0.635966               0.045914
3          spuntata              1        0.681081               0.097112
4         persevera              2        0.635820               1.000000
5        pensandovi              1        0.678086               0.064143
6          riacceso              3        0.575851               0.221556
7         cucchiajo              2        0.628540               0.631271
8        sconsolato              1        0.676620               0.667133
9           tintura              1        0.670833               0.042133
10       ragazzacci              3        0.549950               0.181179
11      lasciandomi              2        0.555501               0.424648
12 

                Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0             fiorini              1        0.688247               0.137712
1         severamente              2        0.629118               0.222768
2            reliquia              1        0.680337               0.077021
3          bravissimo              3        0.601946               0.207247
4            infedeli              5        0.566970               0.620393
5           duevecchi              2        0.626422               0.148037
6            frascati              2        0.626027               0.925359
7              sapevo              1        0.672836               0.000000
8            curatore              1        0.671278               0.385196
9              ditelo              4        0.548476               0.139533
10          inesperta              1        0.584847               0.728052
11           torquato              1        0.572576               0.048694
12          

              Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0            geloso              1        0.652491               0.039123
1          contenta              5        0.532258               0.212070
2   sorellamaggiore              4        0.532860               0.556815
3       disprezzava              2        0.573307               0.329489
4            onesto              4        0.527665               0.144884
5            amarlo              2        0.560691               0.006292
6          credesse              1        0.624107               0.419551
7         dimentica              1        0.621076               0.116848
8          schietto              1        0.619263               0.202050
9           sedotta              1        0.617874               0.862969
10           amasse              3        0.513603               0.848338
11          fidarsi              2        0.503076               0.011393
12    significativa              1    

              Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0           balordo              5        0.808964               0.679866
1          vorrebbe              5        0.799445               0.317006
2         fanciulla              2        0.763382               0.952702
3               osa              5        0.780065               0.134780
4       dichiararsi              5        0.801021               0.646115
5         pronunzia              1        0.884301               0.486172
6             suona              1        0.878882               0.055888
7         sardonica              1        0.877808               0.309650
8             porgo              1        0.876531               0.557066
9          corresse              1        0.873170               0.506348
10         pompieri              4        0.768130               0.966981
11     rispondergli              1        0.763913               1.000000
12        soggiunse              2    

### TOPOS: CHIESA

In [163]:
for autore in lista_autori_cade:
    try:
        print("###" + autore + "###")
        df_autore = similar_words_per_topos("chiesa", 5, 10, autore)
        print(df_autore[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + autore)

###CADE_Alessandro Manzoni_cade###
             Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0         funzioni              5        0.460499               0.317628
1         laterale              5        0.487758               0.251671
2           divini              5        0.442797               0.542476
3        celebrare              2        0.450571               0.000000
4         sospinse              2        0.448990               0.481042
5        piazzetta              1        0.464765               0.372544
6          serrata              1        0.464325               0.041596
7       assistendo              5        0.434135               0.619592
8            zeppa              2        0.437078               0.186552
9          sciolgo              3        0.440143               1.000000
10       terminate              3        0.430075               0.112553
11        imperial              4        0.429469               0.679127
12     ameròsemp

           Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0        vicario              2        0.469200               0.438371
1       sanpiero              1        0.501482               0.548651
2       cappella              4        0.450857               0.506559
3         pasqua              5        0.455268               0.369860
4    fratiminori              5        0.439388               0.426254
5    esaltazione              1        0.484650               0.136007
6    settantadue              1        0.484482               0.835944
7        campane              5        0.443862               0.394766
8      monistero              1        0.480561               0.275332
9     campanelle              3        0.455176               0.796088
10       celebra              3        0.436833               0.000000
11   comunicarsi              4        0.442618               0.549552
12    sagrestano              3        0.427449               0.173321
13    

            Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0       domeniche              5        0.464345               0.025810
1       sagrestia              5        0.455285               1.000000
2       campanile              3        0.466712               0.655029
3      immacolata              4        0.460051               0.787495
4         badiola              1        0.494599               0.436398
5        domenica              1        0.489320               0.358220
6         pulpito              5        0.458263               0.367978
7         pregare              1        0.478699               0.127870
8      cattedrale              1        0.477420               0.934701
9        condurci              3        0.443507               0.625751
10     sagrestano              4        0.456059               0.000000
11       chiesina              1        0.449038               0.290900
12   sanfrancesco              1        0.443097               0

             Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0          portale              4        0.424220               0.378819
1   salacapitolare              3        0.414049               0.310648
2      frastornato              1        0.434217               0.329147
3           romana              3        0.398546               0.652978
4          uscimmo              1        0.425579               0.520526
5       costituito              2        0.408339               0.287279
6       costantino              1        0.417652               0.381920
7   riconoscimento              3        0.400447               0.249323
8           ammira              4        0.398375               0.888552
9       precursore              4        0.389464               0.191949
10         sedetti              4        0.442053               0.746375
11    diresseverso              4        0.398593               0.252083
12         dandole              1        0.391938  

### Altre parole correlate

In [164]:
for autore in lista_autori_cade:
    try:
        print("###" + autore + "###")
        df_autore = similar_words_per_topos("papa", 5, 10, autore)
        print(df_autore[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + autore)

###CADE_Alessandro Manzoni_cade###
            Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0        elettori              5        0.501834               0.959522
1      liutprando              1        0.547174               0.341067
2        agilulfo              1        0.542148               0.051370
3           dettò              1        0.539805               0.756647
4      giuramenti              1        0.538385               0.306956
5      longobardo              1        0.538000               0.940657
6       richelieu              2        0.519669               0.620845
7       donazione              4        0.500089               0.634891
8        cardinal              2        0.516954               0.452560
9             los              1        0.526821               0.000000
10        astolfo              4        0.465345               0.929224
11      macedonia              1        0.480874               0.171465
12  pacificamente            

            Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0            reco              5        0.850192               0.015639
1          ciarle              4        0.810757               0.995284
2          pianga              1        0.885689               0.960092
3             ago              1        0.884848               0.174989
4           farle              1        0.884572               0.000000
5        favolose              2        0.839088               0.580191
6       osservati              1        0.881243               0.250832
7         ristoro              1        0.881082               0.204495
8          mosche              1        0.878811               0.252491
9          arrise              1        0.878566               0.993740
10        materie              1        0.808520               0.738914
11    espressioni              3        0.752266               0.178040
12      scimunito              1        0.803641               0

            Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0   risolutamente              1        0.762053               0.687125
1       andatovia              5        0.622192               0.150590
2     primogenito              1        0.745822               0.920700
3        alloggio              1        0.742957               0.419203
4           peppe              1        0.739890               0.000000
5         istinto              1        0.739514               0.262721
6      portarsela              1        0.730630               0.434539
7     abbracciava              2        0.686710               0.386009
8        servisse              2        0.675916               0.494145
9        facilita              3        0.612045               0.142904
10        fattore              3        0.587436               0.377063
11     pigliarono              3        0.583305               0.274873
12       convinta              2        0.614199               0

In [165]:
for autore in lista_autori_cade:
    try:
        print("###" + autore + "###")
        df_autore = similar_words_per_topos("prete", 5, 10, autore)
        print(df_autore[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + autore)

###CADE_Alessandro Manzoni_cade###
                 Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0          buonagrazia              3        0.478429               0.050611
1           ricogliere              5        0.478033               0.130235
2       sentitoparlare              1        0.541977               0.194075
3             serafino              5        0.460292               0.609035
4        stataaffidata              1        0.541626               0.169351
5            seguitava              1        0.538612               0.945232
6              sveglio              1        0.538195               0.318871
7         padrevittore              1        0.533559               0.253256
8               espose              1        0.533075               0.270493
9            novissimi              1        0.530409               0.408012
10              ponete              4        0.489930               0.928834
11  guardòattentamente              4    

           Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0       birbante              5        0.668144               0.000000
1       senatore              1        0.697381               0.985014
2        collega              2        0.639984               0.829079
3       chierico              5        0.627385               0.461398
4      battesimo              1        0.694817               0.119919
5       deputato              1        0.690202               0.462155
6      sacerdote              4        0.599224               0.590807
7         paggio              2        0.635795               0.396865
8       canonico              4        0.605248               0.664460
9     dodicianni              1        0.683391               0.481872
10   costringeva              4        0.608751               0.958030
11         clero              4        0.594210               0.918216
12     piangerlo              1        0.620148               0.437515
13   m

                  Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0          presentarono              2        0.430298               0.933130
1           baldacchino              5        0.415635               0.435855
2               romelli              1        0.480495               0.498995
3             dottorbax              4        0.429202               0.230760
4            biondiccio              1        0.477061               0.973470
5             gambenude              1        0.473454               0.502709
6              accudire              1        0.471838               0.000000
7             michelino              2        0.438861               0.916274
8                 spirò              2        0.412408               0.088108
9              compunto              1        0.469656               0.377191
10            capobasso              1        0.416115               0.086783
11              unirono              4        0.391256          

             Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0        decrepito              5        0.689647               0.678200
1         persuase              4        0.675459               0.404720
2         avanzato              3        0.697009               0.493462
3      guardandola              1        0.757318               0.542064
4        convenuta              1        0.751172               0.619746
5           quadro              1        0.749384               0.967206
6             donò              1        0.748270               0.045681
7          suggerì              1        0.747554               0.638914
8           guscio              5        0.648762               0.437050
9   caratteristico              3        0.671496               0.951723
10    capofasciato              3        0.662387               0.346233
11      domandasse              3        0.651815               0.400960
12       buonprete              2        0.645756  

In [166]:
for autore in lista_autori_cade:
    try:
        print("###" + autore + "###")
        df_autore = similar_words_per_topos("frate", 5, 10, autore)
        print(df_autore[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + autore)

###CADE_Alessandro Manzoni_cade###
            Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0    accostandosi              5        0.434889               0.723350
1       portinajo              4        0.426659               0.605584
2          stucco              5        0.432281               0.487686
3         pensaci              5        0.449995               0.048686
4      provocarlo              3        0.422957               0.677158
5    padrevittore              2        0.429594               0.196101
6        traboccò              2        0.419004               0.000000
7        ammoniva              3        0.422021               0.626383
8   impenetrabile              1        0.432367               0.586117
9    afferrandolo              3        0.428458               1.000000
10  verticalmente              4        0.437967               0.572624
11    potevadarsi              4        0.421390               0.476139
12        astanti            

              Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0           cotesta              5        0.487716               0.000000
1   serciappelletto              5        0.500625               0.900350
2           scusava              1        0.548446               0.193913
3        dicendogli              1        0.546714               0.043899
4             sozio              1        0.541645               0.000826
5     messerfilippo              4        0.441272               0.070204
6        santofrate              1        0.540088               0.008062
7        volevadire              1        0.539734               0.587489
8         curarsene              1        0.537639               0.926592
9         belcolore              1        0.533776               0.988235
10          beldono              4        0.429774               0.141278
11          restato              4        0.467105               0.356441
12            zeppa              1    

             Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0    dovutopassare              1        0.757073               0.551217
1    alcunelettere              3        0.639433               0.152012
2       compimento              1        0.747973               0.125374
3             rata              1        0.746444               0.254606
4       terminasse              1        0.744187               0.241274
5       informarsi              1        0.743630               0.194132
6    intercessione              2        0.680095               0.247076
7         tramezzo              1        0.736900               0.965284
8        magistero              1        0.736743               0.093488
9      preoccupare              1        0.736298               1.000000
10     indirizzare              1        0.640028               0.439365
11  promettendogli              2        0.576471               0.052680
12             bea              2        0.561681  

          Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0   provinciali              5        0.674110               0.466175
1      ministro              5        0.603322               0.253094
2       arnaldo              5        0.603116               0.000000
3      suggello              5        0.605015               0.990122
4      minorita              5        0.579013               0.522798
5      fernando              5        0.610646               0.376587
6        enrico              1        0.672797               0.467724
7       fidanza              4        0.591201               0.284940
8     contraria              5        0.574778               1.000000
9    santissimo              1        0.668550               0.095515
10       simone              4        0.563419               0.958188
11         vece              1        0.564754               0.167682
12  raccontarmi              1        0.553821               0.480452
13     veemenza     

In [167]:
for autore in lista_autori_cade:
    try:
        print("###" + autore + "###")
        df_autore = similar_words_per_topos("dio", 5, 10, autore)
        print(df_autore[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + autore)

###CADE_Alessandro Manzoni_cade###
           Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0          iddio              5        0.396792               0.110578
1       benedica              5        0.439638               0.261665
2   misericordia              2        0.395916               1.000000
3        madonna              4        0.381646               0.337332
4       benedice              5        0.377358               0.153154
5      aiutatemi              2        0.370247               0.109413
6      concederà              5        0.360049               0.127960
7      rivedremo              1        0.373404               0.544115
8    rendamerito              5        0.366060               0.198989
9    lasciandare              1        0.364356               0.382949
10      rimeriti              1        0.366858               0.534792
11    provvederà              4        0.371888               0.065207
12    consolarti              2        0.3

           Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0           idio              5        0.374938               0.093767
1        diavolo              5        0.364105               0.056966
2      domenedio              1        0.385806               0.000000
3     gesùcristo              4        0.349939               0.279700
4       ostinati              3        0.349440               0.433613
5      peccatore              3        0.343488               0.624490
6   santospirito              5        0.358202               0.082783
7         fedeli              3        0.340145               1.000000
8   misericordia              3        0.340265               0.209901
9       crediamo              1        0.353074               0.379359
10     rimettere              1        0.339870               0.811935
11         idoli              1        0.331438               0.059229
12         timor              4        0.339698               0.064228
13    

               Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0             scampi              3        0.339828               0.249849
1        ringraziato              1        0.351946               0.505003
2           cocomeri              3        0.329247               0.120231
3   signorpresidente              1        0.337199               0.554588
4          costumati              5        0.332669               1.000000
5          castigato              5        0.358459               0.397652
6       disperandosi              1        0.331171               0.468221
7       signorcurato              2        0.321022               0.406170
8       statevizitto              1        0.329410               0.437330
9           benedica              4        0.334453               0.253002
10           castiga              3        0.336858               0.294663
11          meritata              2        0.330698               0.427578
12   illustresignore     

           Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0         divina              1        0.411796               0.248283
1          verbo              3        0.362371               0.136392
2          iddio              2        0.374676               0.164839
3     redenzione              5        0.372731               0.092162
4     interpreti              1        0.397432               1.000000
5     vitaeterna              1        0.389159               0.062713
6       agostino              3        0.352701               0.231895
7    onnipotente              1        0.377223               0.011367
8        ribelli              2        0.368951               0.000000
9       maledice              3        0.356581               0.064326
10   manifestato              3        0.359116               0.527815
11       perdoni              4        0.369075               0.817289
12   onnipotenza              4        0.357079               0.297643
13   b

In [168]:
for autore in lista_autori_cade:
    try:
        print("###" + autore + "###")
        df_autore = similar_words_per_topos("cristo", 5, 10, autore)
        print(df_autore[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + autore)

###CADE_Alessandro Manzoni_cade###
           Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0      adempiuto              5        0.642646               0.010356
1      obbedisce              1        0.722422               0.643277
2       infedeli              1        0.699401               0.880287
3      straziata              1        0.698915               0.089657
4          fenno              1        0.698704               0.040476
5        incauto              1        0.697106               0.418519
6      ascendere              1        0.695650               0.166613
7       virgineo              1        0.693960               0.042251
8         negate              1        0.693682               0.867891
9          degnò              1        0.692877               0.426877
10       spumoso              3        0.547829               0.396919
11        marini              2        0.556514               0.310242
12        divoto              2        0.5

         Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0        mario              4        0.629893               0.437181
1        epist              2        0.660195               0.375212
2      funebre              1        0.710820               0.314428
3        ecuba              5        0.604274               0.174600
4       tracia              1        0.700842               0.381503
5         mosè              2        0.645984               0.706120
6         tebe              1        0.693995               0.528568
7      apparve              5        0.613866               1.000000
8   firmamento              5        0.629609               0.218450
9   attribuito              4        0.603190               0.168258
10       magno              2        0.581453               0.018057
11      taciti              3        0.576787               0.249029
12    scolpita              1        0.603443               0.530222
13     martoro              1     

            Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0         storpio              5        0.845975               0.240841
1       giudicato              1        0.896695               0.489739
2           torme              1        0.895969               0.940503
3         salimmo              1        0.891624               0.965171
4   superstizioso              1        0.889659               0.169919
5        belvolto              1        0.889451               0.493356
6        debitori              1        0.888778               0.041819
7           nullo              1        0.886103               0.961938
8          intimi              1        0.884485               0.092428
9         baratto              1        0.884319               0.108037
10      tremolava              4        0.784977               0.227156
11         spanna              4        0.747623               0.053717
12          sasso              4        0.746481               0

              Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0         predicata              5        0.865814               1.000000
1      altrapersona              1        0.889920               0.153904
2         cattività              1        0.884553               0.202553
3         frizzante              1        0.883122               0.271569
4        concedesse              1        0.881775               0.965194
5           utilità              1        0.878706               0.421977
6          enormità              1        0.877678               0.078911
7   scrupolosamente              1        0.877478               0.947175
8     esercitazioni              2        0.850615               0.147580
9           pensata              1        0.874847               0.051768
10         chiusero              4        0.800792               0.920606
11     trasfigurata              2        0.826897               0.174218
12     rispettabile              1    

### TOPOS: FELICITA'

In [169]:
for autore in lista_autori_cade:
    try:
        print("###" + autore + "###")
        df_autore = similar_words_per_topos("felicità", 5, 10, autore)
        print(df_autore[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + autore)

###CADE_Alessandro Manzoni_cade###
              Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0          perfetta              5        0.547773               0.460499
1        immutabile              4        0.516464               0.934108
2        consacrata              2        0.569482               0.585922
3          figliola              1        0.611299               0.760093
4         accordare              3        0.517263               0.101774
5     intellettuale              5        0.531309               0.943102
6   indistruttibile              5        0.569651               0.022271
7          benefico              4        0.539124               1.000000
8        dolcissima              1        0.601381               0.304211
9           augusta              1        0.599814               0.455920
10   incorruttibile              2        0.494860               0.000000
11           onestà              2        0.507640               0.331973
12 

                Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0     propriafelicità              5        0.482974               0.090865
1            primario              5        0.480129               0.344981
2          conducenti              5        0.482706               0.524910
3     piacereinfinito              5        0.469542               0.186964
4         complemento              5        0.473077               0.650127
5   maggiorperfezione              1        0.509611               0.521153
6         beatitudine              5        0.459241               0.073995
7       conseguimento              2        0.472788               0.000000
8       felicitàumana              2        0.466810               0.817510
9           destinata              1        0.495577               0.443412
10       statosociale              1        0.447446               1.000000
11         assaggiare              2        0.439700               0.005238
12          

              Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0          debitore              5        0.483543               0.000000
1         godimento              4        0.472766               0.529854
2   volontariamente              3        0.485036               0.928147
3     soddisfazione              1        0.548295               0.251767
4         ricchezza              5        0.465122               0.038232
5       sagrificare              5        0.466711               0.451604
6            odiati              4        0.457308               0.021953
7     dovevabastare              1        0.538399               0.470407
8           modesti              3        0.475355               0.107424
9           suprema              4        0.453948               0.339372
10          duevite              4        0.445243               0.235152
11          sapersi              2        0.439035               0.042516
12          portati              1    

            Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0        estatica              5        0.743656               0.615135
1         pallore              5        0.745438               0.593015
2   deliberazione              4        0.724568               0.967698
3      atteggiato              5        0.765075               1.000000
4     carabinieri              1        0.876424               0.303691
5           amara              5        0.771127               0.275478
6      umoristica              1        0.873274               0.444961
7          brusca              1        0.867586               0.429735
8          nativa              1        0.865950               0.514728
9        triviali              1        0.863769               0.000000
10     espressiva              4        0.720402               0.490481
11     confusione              3        0.678198               0.253355
12      combinato              4        0.685917               0

### Altre parole correlate

In [170]:
for autore in lista_autori_cade:
    try:
        print("###" + autore + "###")
        df_autore = similar_words_per_topos("gioia", 5, 10, autore)
        print(df_autore[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + autore)

###CADE_Alessandro Manzoni_cade###
           Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0        mondana              5        0.567119               0.001474
1     giocondità              3        0.500608               0.648748
2        ripieni              5        0.532178               0.243674
3       rumorosa              3        0.489225               0.452760
4          gioja              4        0.469061               0.102734
5        austera              5        0.491653               0.018499
6         serena              5        0.468251               0.140750
7     assaporare              3        0.462820               0.517694
8     refrigerio              1        0.524707               0.288930
9        apporta              1        0.518680               0.158169
10  dibattendosi              2        0.448626               1.000000
11     brontolio              4        0.443384               0.000000
12         angel              2        0.4

           Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0     indicibile              1        0.553229               0.464485
1          diman              5        0.449214               0.183086
2   sopravvenuto              5        0.475663               0.035359
3   inquietudine              1        0.523979               0.516823
4     starsicuro              4        0.435542               0.274176
5      cerimonia              2        0.470160               0.305032
6        rompono              5        0.442156               0.394986
7      godimenti              1        0.516114               0.252578
8     allegrezza              2        0.461162               0.326521
9         follia              1        0.512855               0.765163
10      danzando              4        0.433749               0.784118
11      ebbrezza              4        0.437443               1.000000
12     collocata              1        0.428444               0.123847
13    

               Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0           risibili              5        0.607557               0.571357
1           velenoso              1        0.669469               0.130811
2          gorgoglio              1        0.662853               0.502769
3            ridesta              2        0.579669               0.930650
4           ahilasso              2        0.581531               0.261508
5              brame              1        0.655242               0.226921
6            premute              2        0.610855               0.452289
7        suscitavano              2        0.613352               0.264651
8          rimpianti              1        0.648070               0.967752
9              dubbî              2        0.557104               0.117889
10            émpito              2        0.532893               0.023604
11           rimossa              3        0.511803               0.156463
12       avviluppava     

             Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0           gaudio              1        0.624834               0.105360
1        interiore              3        0.526450               0.182334
2         dolcezza              2        0.543705               0.000000
3        folgorato              1        0.599783               0.084404
4       dolcissima              1        0.592152               0.758245
5        esultanza              5        0.494584               0.558730
6       indicibile              3        0.500460               0.822235
7          spasimo              2        0.533757               0.173045
8           estasi              1        0.582917               0.127125
9     disperazione              1        0.580387               0.772005
10         valesse              1        0.520852               0.291551
11         tornavo              1        0.496266               0.200362
12          cantar              4        0.474504  

### TOPOS: PATRIA/ITALIA

In [171]:
for autore in lista_autori_cade:
    try:
        print("###" + autore + "###")
        df_autore = similar_words_per_topos("patria", 5, 10, autore)
        print(df_autore[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + autore)

###CADE_Alessandro Manzoni_cade###
             Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0            ostia              5        0.445820               0.430796
1        taiparole              3        0.481783               0.883836
2         contende              4        0.441496               1.000000
3          estrema              1        0.495025               0.343455
4          onorate              1        0.490544               0.197143
5           marino              1        0.484779               0.731973
6           decade              5        0.484101               0.891046
7       librosesto              5        0.469819               0.080575
8          speglio              4        0.450234               0.952356
9         stranier              1        0.465738               0.476780
10      interafede              4        0.433282               0.264434
11          quinta              4        0.425851               0.119225
12            ro

            Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0      venerabile              1        0.609830               0.378982
1       notissimo              1        0.597054               0.849850
2       alcibiade              4        0.491473               0.000000
3           natio              5        0.507732               0.270674
4         augusto              1        0.581214               0.392634
5   perfettissima              1        0.578095               0.427144
6        federico              3        0.494075               0.210973
7       mantovani              5        0.504578               0.357419
8        fiorenza              3        0.500652               0.024987
9       perseverò              2        0.521439               0.447744
10        ingrata              1        0.487364               0.197330
11          usque              3        0.442766               0.074492
12       dilatato              1        0.470832               0

             Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0           nemici              2        0.467528               0.856768
1        frontiera              1        0.499972               0.120253
2        tollerati              4        0.428891               0.001605
3          trieste              2        0.452342               1.000000
4            scudo              4        0.428182               0.350987
5         ignobili              4        0.434128               0.403706
6        republica              5        0.430443               0.324923
7         protegge              1        0.487951               0.706182
8          fulgide              5        0.428306               0.000000
9         acerrimo              1        0.484156               0.137144
10       tirannide              4        0.443716               0.891136
11        mendichi              2        0.425428               0.370335
12  spiritualmente              3        0.412096  

             Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0        furibondi              1        0.759437               0.210405
1       nessunuomo              5        0.611558               0.383175
2        prigionia              1        0.750958               0.947275
3      formalmente              1        0.750680               0.192824
4        pescatore              1        0.750516               0.628608
5        garantiva              1        0.750171               0.489099
6    cesareaugusto              2        0.662025               0.337933
7            henri              3        0.617488               0.174238
8            avari              1        0.745608               0.077347
9          honeste              1        0.744738               0.966612
10         dalmati              4        0.585784               1.000000
11     transazione              2        0.578327               0.964673
12  comandosupremo              1        0.625434  

In [172]:
for autore in lista_autori_cade:
    try:
        print("###" + autore + "###")
        df_autore = similar_words_per_topos("italia", 5, 10, autore)
        print(df_autore[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + autore)

###CADE_Alessandro Manzoni_cade###
           Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0        francia              3        0.462748               0.555035
1        fiandra              2        0.465881               0.846292
2     assuefatta              5        0.448749               0.480105
3         calato              4        0.441059               0.058597
4    dominazione              5        0.451970               0.586421
5        fiandre              1        0.494418               0.205946
6       ubbidiva              3        0.433096               0.721957
7      posseduta              2        0.451547               1.000000
8         gallie              1        0.479325               0.691434
9      boccaccio              1        0.478642               0.852947
10           ugo              3        0.425935               0.217101
11  impadronirsi              4        0.414066               0.000000
12  stabilimenti              1        0.4

             Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0       ultimianni              1        0.459877               0.146569
1          disputa              3        0.392736               0.952640
2          francia              1        0.458497               0.183019
3          polonia              3        0.393613               0.000000
4      cinquecento              1        0.454310               0.428857
5          ispagna              1        0.448750               0.087156
6     settentrione              2        0.404939               0.062811
7          sicilia              2        0.403964               0.220073
8           gallia              3        0.389047               0.988253
9          trionfò              1        0.441689               0.091081
10        spensero              2        0.367487               0.397482
11           velli              3        0.367199               0.166939
12     pubblicando              2        0.363639  

           Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0   insuperabile              5        0.670516               0.031503
1        creando              5        0.682369               1.000000
2      banchieri              1        0.743346               0.079998
3   casacolonica              1        0.731756               0.950777
4   lungocammino              4        0.606580               0.135117
5      frontiera              1        0.727407               0.000000
6       seminati              2        0.623835               0.741021
7          siepi              2        0.676462               0.223761
8     scacchiera              1        0.722730               0.025807
9       transito              5        0.636466               0.383994
10      vedranno              3        0.598069               0.002134
11         tende              1        0.635859               0.932305
12      riempiti              1        0.633734               0.690681
13    

            Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0          spagna              5        0.510796               0.408927
1          europa              4        0.492495               0.908130
2        germania              5        0.485484               0.651968
3       milleanni              5        0.484454               0.853895
4       cartagine              3        0.499289               0.168601
5     inghilterra              2        0.502130               0.106895
6            roma              5        0.492742               0.797916
7          napoli              3        0.475693               0.149088
8      vincitrice              3        0.483497               0.930816
9       chiamarvi              5        0.467202               0.789698
10         avanzò              2        0.436759               0.719754
11     famaantica              2        0.406657               0.293753
12        polonia              2        0.422333               0

### Altre parole correlate

In [173]:
for autore in lista_autori_cade:
    try:
        print("###" + autore + "###")
        df_autore = similar_words_per_topos("stato", 5, 10, autore)
        print(df_autore[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + autore)

###CADE_Alessandro Manzoni_cade###
               Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0         confidarsi              2        0.324129               0.398403
1        imbroglione              5        0.305534               0.631580
2            privare              1        0.303368               0.165986
3         possodirlo              2        0.299618               0.287258
4          posterità              1        0.295692               0.168864
5            volerti              1        0.295429               0.353331
6         interviene              1        0.294934               0.529240
7             paruto              1        0.293683               1.000000
8           mostrato              1        0.292353               0.243669
9        fisicamente              1        0.290737               0.071598
10         illusorio              1        0.306896               0.188940
11          episodio              1        0.303199              

                  Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0            definitivo              1        0.381814               0.200477
1            modificato              2        0.348758               0.084345
2             mantenuto              1        0.366896               0.320410
3          riconosciuta              1        0.366125               0.066037
4               gabbato              1        0.364024               0.287296
5              organico              2        0.340062               0.523484
6             comunicar              1        0.361380               0.484796
7             riferisce              1        0.359095               0.733149
8               esporre              1        0.358257               0.221826
9                datomi              1        0.357610               0.157950
10           unicoamico              4        0.407821               0.004299
11           riflessivo              3        0.333142          

              Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0            timido              1        0.405723               0.490711
1        alcunaltro              4        0.346106               0.400513
2      meraviglioso              3        0.357041               0.078479
3        licenziato              1        0.395312               0.221719
4           assunto              1        0.393892               0.881035
5         eccezione              5        0.346740               0.032989
6      sicurosicuro              1        0.387363               0.365677
7       autorizzato              5        0.342642               0.272929
8           recente              1        0.381826               0.406889
9         accettato              2        0.355076               0.208828
10   esplicitamente              4        0.327043               0.188711
11        vigliacco              2        0.327420               0.154707
12            bando              1    

             Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0       ingranaggi              4        0.356571               0.270378
1       funzionare              5        0.375033               0.448612
2        complotto              3        0.337484               0.408729
3          fallito              1        0.350710               0.153275
4        sottratto              4        0.340138               0.395098
5        attentato              1        0.340806               0.162547
6       pienamente              1        0.339642               0.208394
7   coinvolgimento              1        0.338330               0.126702
8          investe              1        0.335697               0.058336
9       momentaneo              1        0.332941               0.608160
10      maisentito              1        0.335948               1.000000
11       altissimo              1        0.329742               0.261107
12          giuoco              1        0.327419  

               Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0   indubitabilmente              2        0.370304               0.806336
1          informato              4        0.345543               0.070365
2            gioioso              5        0.339155               0.151928
3           divenuto              4        0.346113               0.511791
4           filosofo              1        0.380494               0.185774
5             scopre              1        0.375010               0.094294
6        facilissimo              4        0.334023               0.340105
7           precetto              3        0.348687               1.000000
8            impiego              1        0.368790               0.447709
9           abbietto              1        0.366856               0.412986
10        fondamenti              3        0.341601               0.833806
11          violento              2        0.334704               0.855296
12            spiato     

In [174]:
for autore in lista_autori_cade:
    try:
        print("###" + autore + "###")
        df_autore = similar_words_per_topos("impero", 5, 10, autore)
        print(df_autore[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + autore)

###CADE_Alessandro Manzoni_cade###
             Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0     stabilimenti              5        0.577859               0.670858
1         invasori              5        0.620926               0.000000
2          sassoni              1        0.669935               0.882730
3     varienazioni              5        0.581664               0.250237
4            autor              1        0.648762               0.831203
5            greci              1        0.643800               0.434453
6       nuoveleggi              1        0.643456               0.066880
7         arsenale              2        0.610508               0.104026
8      conquistate              1        0.639459               0.855245
9         universo              1        0.637640               0.122662
10       possedute              4        0.523615               0.226406
11         vandali              4        0.530254               0.728557
12       barbari

            Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0        persiano              5        0.574500               0.240403
1   conquistatore              1        0.643361               0.968838
2       babilonia              1        0.637518               0.168742
3         colosso              4        0.554154               0.000000
4        pervenne              1        0.628598               0.459920
5      longobardi              2        0.557695               0.524248
6       redentore              1        0.626402               1.000000
7          rimise              5        0.546075               0.257082
8      vespasiano              1        0.624806               0.481089
9          tracia              1        0.623745               0.115412
10   impadronirsi              2        0.514489               0.083953
11  restaurazione              3        0.517184               0.235784
12      dispotica              1        0.546061               0

           Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0       dimorare              5        0.604302               0.441327
1      germanico              3        0.591660               0.590014
2      scostante              5        0.591950               0.345000
3     irrigidito              2        0.594204               0.235089
4       vassallo              3        0.566769               0.613948
5     amatissimo              4        0.562524               0.072522
6         aquila              5        0.598509               1.000000
7         france              1        0.697734               0.561715
8       malfermo              5        0.588783               0.430132
9       smeraldo              1        0.692666               0.430163
10         arduo              3        0.539211               0.572226
11      margutte              1        0.584068               0.549826
12      sanluigi              1        0.579767               0.530344
13    

          Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0    imperatore              5        0.516638               0.117752
1        coorti              3        0.512362               0.936080
2         nerbo              2        0.552943               1.000000
3    disciplina              4        0.510626               0.298848
4          coll              1        0.597138               0.201446
5   nobilissimo              1        0.594653               0.179913
6    restituita              1        0.594082               0.487549
7       poniamo              1        0.587055               0.527889
8        chiari              1        0.586564               0.477061
9      creatore              3        0.519035               0.110496
10    ritornati              2        0.489974               0.205866
11      ritenea              3        0.489349               0.190671
12        nerva              2        0.474859               0.033556
13    magnanimi     

In [175]:
for autore in lista_autori_cade:
    try:
        print("###" + autore + "###")
        df_autore = similar_words_per_topos("nazione", 5, 10, autore)
        print(df_autore[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + autore)

###CADE_Alessandro Manzoni_cade###
             Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0   conquistatrice              5        0.615822               0.197047
1       longobarda              3        0.520584               0.368741
2    politicamente              3        0.526606               0.016870
3     conservarono              5        0.520362               0.000000
4            razze              1        0.600958               1.000000
5   appartenessero              5        0.522830               0.351990
6          nazioni              1        0.596403               0.261826
7        monarchia              1        0.593482               0.087933
8           gallie              3        0.514872               0.314719
9       repubblica              1        0.587368               0.353495
10      costituita              4        0.507080               0.848351
11     appartenere              3        0.497537               0.868178
12   presentando

              Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0            nazion              5        0.588948               0.395711
1           plebeio              2        0.648645               0.367538
2   bassacondizione              5        0.564939               0.080932
3             poesì              2        0.616605               0.911440
4       famosissimo              1        0.681075               0.429135
5            smirne              2        0.587348               0.947512
6       eccellenzia              1        0.671437               1.000000
7          ateniese              5        0.570112               0.214077
8          depressa              5        0.576250               0.247482
9    dantealighieri              1        0.664813               0.465475
10        sublimità              3        0.553230               0.498286
11           musica              1        0.582923               0.000000
12           feltro              4    

                  Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0              tradotti              1        0.750352               0.331729
1               assunti              3        0.637821               0.210832
2               storici              3        0.642638               0.345054
3          linguacomune              2        0.692545               0.489037
4                popoli              1        0.731821               0.411297
5          risorgimento              1        0.729575               0.249585
6              musicali              1        0.729399               0.336329
7   letteraturaitaliana              2        0.665374               0.181069
8           naturalisti              2        0.626060               0.614148
9          altrenazioni              4        0.606111               0.737520
10           vitacivile              4        0.584904               0.037065
11           interpreti              3        0.604189          

              Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0          ammirare              1        0.892615               0.438740
1             fango              1        0.890298               1.000000
2         uccidersi              2        0.837384               0.951651
3             ampie              1        0.882994               0.447210
4             cieli              1        0.878522               0.110659
5           immersa              1        0.877408               0.267379
6           notizie              1        0.874653               0.467457
7      solennemente              1        0.873753               0.411095
8           pentire              1        0.873523               0.929180
9              godo              5        0.793250               0.526381
10          immensi              1        0.816032               0.523033
11         sapiente              1        0.805585               0.410352
12       scusandosi              1    

In [176]:
for autore in lista_autori_cade:
    try:
        print("###" + autore + "###")
        df_autore = similar_words_per_topos("bandiera", 5, 10, autore)
        print(df_autore[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + autore)

###CADE_Alessandro Manzoni_cade###
                  Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0               ingrata              1        0.816891               0.000000
1               credean              1        0.813521               0.405956
2               ottenni              1        0.813301               0.074291
3              giurasti              3        0.688328               0.224052
4              vittrice              5        0.715704               0.407764
5             germoglia              1        0.806826               0.190182
6               presagi              1        0.806403               0.984807
7                elissa              1        0.806072               0.229286
8                 trito              1        0.805022               0.188065
9                 tradì              3        0.710730               0.951230
10              partorì              4        0.636900               0.393071
11            lignaggio      

                Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0           rivestito              2        0.834957               0.150054
1       generalissimo              2        0.837027               0.316020
2          affermarsi              1        0.857742               1.000000
3        insuperabile              1        0.856823               0.149729
4             giurare              1        0.856056               0.776512
5          cavarfuori              1        0.855873               0.589757
6            coerenza              1        0.855612               0.140194
7        ingenuamente              1        0.855178               0.420575
8              fraude              1        0.855059               0.490559
9               annoi              2        0.818656               0.495283
10           richiamo              3        0.732918               0.989313
11  poverodisgraziato              1        0.799832               0.987822
12         a

             Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0           spense              3        0.602588               0.325405
1          navarra              5        0.593654               0.044092
2           svezia              1        0.683842               0.302600
3       nuovamente              1        0.681941               0.515971
4              xlv              2        0.632211               0.935146
5        stendardo              3        0.605364               0.239346
6          lamagna              3        0.615922               0.217989
7         presidio              2        0.631375               0.395171
8            vanta              4        0.592712               0.161106
9         conducea              1        0.671075               0.311620
10        cercarla              4        0.546558               0.120623
11         cercata              1        0.588560               0.654968
12       detroiani              2        0.564781  

La chiave non esiste nel modelloCADE_Ugo Foscolo_cade
###CADE_Umberto Eco_cade###
              Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0        conoscerle              1        0.894378               0.222872
1           contado              1        0.892562               0.000000
2     scelleratezze              1        0.891878               0.196303
3              viti              1        0.891692               0.369813
4          dueparti              1        0.889196               0.944015
5            sapute              4        0.824388               0.025244
6       catapecchie              1        0.887075               0.160459
7           vendute              2        0.858379               1.000000
8           emanato              1        0.884917               0.454867
9           faville              1        0.884855               0.986075
10       sopportava              1        0.833896               0.162380
11          imberbi           

### TOPOS: GUERRA

In [177]:
for autore in lista_autori_cade:
    try:
        print("###" + autore + "###")
        df_autore = similar_words_per_topos("guerra", 5, 10, autore)
        print(df_autore[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + autore)

###CADE_Alessandro Manzoni_cade###
           Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0        bolliva              5        0.447894               0.218900
1       conclusa              1        0.480124               0.278123
2    racconciare              5        0.437921               0.715509
3          buchi              5        0.429275               0.551171
4    incresciosa              4        0.403615               0.323391
5    cartaginese              5        0.403470               1.000000
6      pochimesi              5        0.397050               0.000000
7       promossa              1        0.432384               0.324673
8    stratagemmi              5        0.412301               0.199132
9       attirava              2        0.398341               0.243991
10  meravigliosa              4        0.390499               0.208905
11         troia              1        0.377899               0.266722
12      credeste              1        0.3

           Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0     forestiera              4        0.447257               0.725939
1          turno              4        0.435247               0.246343
2      detroiani              1        0.532562               0.539979
3      cittadina              2        0.466842               1.000000
4        triegua              5        0.468278               0.159640
5       liberata              1        0.503618               0.000000
6        nimistà              1        0.498962               0.402887
7         mastra              4        0.444565               0.129167
8       manfredi              1        0.493644               0.208538
9        antioco              1        0.493409               0.117504
10  valorosouomo              2        0.430435               0.797395
11     avvenendo              4        0.424892               0.727585
12  persecuzione              3        0.433290               0.384045
13    

           Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0          lucro              5        0.551155               0.410603
1        europea              5        0.548448               0.583411
2      frammento              3        0.444270               0.222064
3      battaglia              1        0.479663               0.009818
4         africa              2        0.450007               0.087435
5   precedettero              2        0.441289               0.063231
6          milan              1        0.463843               0.000000
7      strategia              1        0.460791               0.343977
8      orientale              1        0.449599               0.274473
9         turchi              1        0.443246               0.984224
10       sassoni              4        0.449121               0.377173
11  doppiotaglio              4        0.438573               0.119162
12        dovrai              1        0.426645               1.000000
13    

           Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0   puntoestremo              5        0.486554               0.245102
1       fraterna              2        0.486591               0.337555
2       mormorìo              1        0.544749               0.573130
3           aura              2        0.485637               0.008650
4        sfogata              4        0.454265               0.631969
5      confusion              5        0.451313               0.418270
6        darpace              4        0.472492               0.851394
7     parlamento              1        0.521732               0.550132
8         darete              1        0.520880               0.137405
9       menforti              1        0.519299               0.268838
10        arnese              4        0.476186               0.637912
11     discutono              4        0.427311               0.093028
12       apporta              3        0.438349               0.251982
13    

### TOPOS: FIGURA FEMMINILE

In [178]:
for autore in lista_autori_cade:
    try:
        print("###" + autore + "###")
        df_autore = similar_words_per_topos("donna", 5, 10, autore)
        print(df_autore[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + autore)

###CADE_Alessandro Manzoni_cade###
              Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0           ersilia              5        0.442811               0.079187
1          beatrice              2        0.387514               0.046343
2           tendina              3        0.395653               0.132222
3   donnamargherita              5        0.385485               0.316582
4            impose              1        0.406975               0.183654
5           ragazza              1        0.403316               0.404631
6     occhisbarrati              1        0.391706               0.382784
7           duemule              4        0.374787               0.267603
8          sposarlo              1        0.387913               1.000000
9           arrossò              1        0.379336               0.151624
10          assentì              2        0.366990               0.299938
11       accosciata              1        0.357287               0.180905
12 

           Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0     innamorata              4        0.398015               0.187610
1          livia              5        0.452495               0.034425
2      vociaccia              1        0.447046               0.355181
3      supponete              1        0.445174               0.232688
4          parsa              4        0.399507               0.110910
5      femminile              1        0.436851               0.463552
6       sentirai              5        0.367579               0.019417
7       maschile              1        0.428365               0.197703
8        maschio              3        0.381415               0.864659
9   personaamata              1        0.420011               0.364132
10    duegiovani              1        0.390488               0.528672
11     digiunare              3        0.363802               1.000000
12     inesperta              1        0.378996               0.188307
13    

              Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0          supporlo              4        0.349048               0.284146
1         posseduto              1        0.374093               0.204292
2         dimentica              1        0.372815               0.218337
3            nobile              1        0.369518               0.519064
4           comandò              1        0.367711               0.081617
5         splendida              2        0.350366               0.000000
6             iroso              1        0.364447               0.904381
7        fotografia              4        0.339089               0.805210
8          compagna              1        0.361092               0.182522
9   sentendoparlare              5        0.339181               0.980851
10       giovanetta              4        0.335189               0.136782
11           gabbia              1        0.343256               0.450958
12     ardentemente              3    

          Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0        tirava              1        0.650583               0.145406
1    afflizione              1        0.642749               0.965207
2   consapevole              1        0.640357               0.400668
3   pacatamente              1        0.636691               0.171807
4         salva              1        0.633638               0.000000
5    presentava              2        0.581740               0.346675
6    letterario              1        0.626372               0.886746
7      stupende              1        0.625869               0.194892
8         colta              1        0.625082               0.954583
9    sostituito              1        0.624896               0.140005
10      dicendo              4        0.495468               0.311095
11    frenetica              4        0.483614               0.258448
12      capirlo              2        0.503479               0.892474
13    soggiunse     

              Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0            figlia              4        0.356727               0.013446
1           aprissi              1        0.387854               0.292154
2         strappata              1        0.386792               0.000000
3             moria              2        0.362604               1.000000
4      scenaseconda              1        0.383044               0.312360
5            moglie              3        0.346081               0.218361
6           perfida              1        0.375802               0.008103
7             poich              1        0.375085               0.325897
8       sconosciuta              1        0.372258               0.597973
9         impudente              1        0.369525               0.763275
10  signoracontessa              4        0.351359               0.571386
11            luisa              4        0.354668               0.236760
12          medesma              2    

In [179]:
for autore in lista_autori_cade:
    try:
        print("###" + autore + "###")
        df_autore = similar_words_per_topos("madre", 5, 10, autore)
        print(df_autore[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + autore)

###CADE_Alessandro Manzoni_cade###
            Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0          fidate              5        0.406118               0.309178
1        allogata              4        0.383135               0.129203
2       figliuola              1        0.409062               0.560422
3       collocata              1        0.401356               0.139012
4      fattoressa              1        0.399541               0.300751
5        liberata              1        0.398417               0.354644
6      incomodata              3        0.370802               0.017842
7   promessosposo              2        0.374636               0.869350
8         fattora              1        0.389989               0.229286
9       queivolti              1        0.389201               0.048829
10      angiolina              3        0.358281               0.064984
11        guarita              1        0.366168               0.676618
12        baciava            

            Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0          figlia              5        0.454842               0.986426
1         sorella              5        0.456580               0.152074
2          figlie              2        0.502736               0.578129
3   linguesorelle              5        0.443617               0.465823
4         sorelle              2        0.483324               0.078441
5       ereditato              5        0.439955               0.592488
6        spagnola              5        0.432733               1.000000
7     fratellanza              3        0.449387               0.546074
8   comuneorigine              2        0.453154               0.357774
9     allontanata              1        0.501141               0.496980
10        polacca              2        0.405946               0.107321
11     incomodare              1        0.427256               0.108057
12     ricordando              1        0.423775               0

           Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0       beatrice              1        0.591437               0.271518
1          lucia              5        0.448306               0.247398
2        leonora              4        0.446590               0.201442
3      magnifica              5        0.454264               1.000000
4       sofronia              5        0.466585               0.104826
5       contessa              1        0.556768               0.838999
6       isabella              1        0.542285               0.113454
7        strozzi              1        0.535661               0.771737
8        suocero              1        0.530547               0.327328
9        strozza              1        0.524339               0.335296
10           pia              4        0.440559               0.362967
11   avvedersene              4        0.419483               0.088471
12  accorgendosi              1        0.434573               0.218225
13    

            Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0     maledizione              5        0.506490               0.045107
1   superstizione              5        0.452027               0.250832
2         scenaii              1        0.519897               0.352790
3         placati              1        0.518770               0.223574
4        scenaiii              1        0.516312               0.109555
5      conoscesti              2        0.467261               0.596582
6           volli              1        0.513173               0.236393
7       maledetti              2        0.448647               0.216722
8              od              1        0.511177               0.144813
9          offese              2        0.462952               0.563088
10     lagrimando              4        0.462891               0.453918
11     pregandola              4        0.455998               0.897249
12     affettuosa              1        0.435452               0

In [180]:
for autore in lista_autori_cade:
    try:
        print("###" + autore + "###")
        df_autore = similar_words_per_topos("femmina", 5, 10, autore)
        print(df_autore[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + autore)

###CADE_Alessandro Manzoni_cade###
                Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0            salvarmi              1        0.868316               0.936668
1          passavanti              1        0.868276               0.257346
2              schifa              4        0.763616               0.296722
3              zucche              1        0.858437               0.254731
4           sfrontata              1        0.857481               0.333301
5          commuovere              1        0.856980               0.307049
6   vecchiagovernante              2        0.791609               0.565230
7          aggrondato              1        0.855257               0.945027
8          offendersi              1        0.853230               0.175978
9         serenamente              1        0.852325               0.006671
10             legava              1        0.781618               0.512424
11        carrettieri              1        0.778665 

            Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0            ente              4        0.745047               0.085139
1        chieggio              3        0.739935               0.510417
2        misfatto              1        0.821855               0.044229
3         ragazzi              1        0.811453               0.026592
4      unicoamico              5        0.723397               0.295061
5     farmenzione              1        0.808693               0.250826
6         proponi              1        0.808578               0.231718
7     trattamento              1        0.805081               0.898676
8       disacerba              1        0.804901               0.275519
9         fidarmi              1        0.804897               0.015403
10         ispero              2        0.737971               0.540964
11          sallo              2        0.722351               0.921339
12  potevasperare              1        0.746438               0

           Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0     maschietti              5        0.754831               0.673179
1       infelici              5        0.666686               0.069923
2          ehgià              2        0.667489               0.153095
3      trentasei              5        0.624024               0.053187
4         costei              4        0.599296               0.248654
5        maschio              4        0.584633               0.299555
6          fante              1        0.684373               0.118253
7      affettato              1        0.677759               0.340460
8      signorino              2        0.650374               0.199259
9        camilla              2        0.589650               0.629628
10   ascoltatore              3        0.577646               0.701225
11   spogliarono              1        0.589963               0.000000
12   quattordici              3        0.553380               0.626226
13  al

In [181]:
for autore in lista_autori_cade:
    try:
        print("###" + autore + "###")
        df_autore = similar_words_per_topos("sposa", 5, 10, autore)
        print(df_autore[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + autore)

###CADE_Alessandro Manzoni_cade###
           Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0          betta              5        0.509741               0.972662
1      conviensi              5        0.472673               0.581651
2        custode              1        0.552792               0.926237
3       primiero              2        0.516778               0.705221
4     acconciata              1        0.548799               0.098457
5     damminuove              1        0.546921               0.424242
6         magion              5        0.477452               0.451405
7       riverire              1        0.543118               1.000000
8       liberata              1        0.542976               0.959805
9       ansberga              1        0.542019               0.000000
10     testimone              4        0.435865               0.184780
11       adorata              4        0.491694               0.071213
12         vinci              1        0.4

                 Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0            vittorina              5        0.575358               1.000000
1               angelo              3        0.566451               0.411621
2                dille              2        0.587483               0.361474
3          abbracciami              1        0.668949               0.000000
4                 sant              5        0.570368               0.532353
5      salutacaramente              1        0.664433               0.416220
6           ricordando              2        0.585655               0.958123
7              leonora              1        0.661654               0.375415
8           pregandoti              2        0.584780               0.516838
9          ringraziano              5        0.571522               0.077970
10             rifarsi              4        0.605782               0.278005
11            canonica              2        0.557716               0.347308

                  Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0               rimango              5        0.590982               0.905393
1            confortati              1        0.697536               0.853442
2           contentasse              3        0.604202               0.305281
3               amatore              1        0.674983               0.639631
4             domandavo              4        0.559738               0.182575
5              legitima              5        0.592942               1.000000
6                 torrò              1        0.667716               0.391058
7             comperata              2        0.611628               0.608482
8               ancilla              1        0.662598               0.116138
9               sposare              1        0.661852               0.132161
10              matilde              4        0.541185               0.293769
11              maritar              2        0.525214          

            Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0           elisa              2        0.613179               0.044924
1           reina              1        0.687169               0.359489
2           casta              3        0.544810               0.799969
3           amata              5        0.545257               0.357473
4             dêi              2        0.564569               0.579507
5          compra              2        0.594004               0.292422
6      scenasesta              4        0.538260               0.129585
7           nuora              2        0.569672               0.446654
8         ancilla              1        0.642850               0.666051
9      proserpina              1        0.640289               0.163364
10   secondenozze              3        0.515317               0.122858
11        creduta              4        0.530397               0.099317
12    scenaquinta              2        0.518233               0

### TOPOS: NOTTE/SERA

In [182]:
for autore in lista_autori_cade:
    try:
        print("###" + autore + "###")
        df_autore = similar_words_per_topos("notte", 5, 10, autore)
        print(df_autore[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + autore)

###CADE_Alessandro Manzoni_cade###
           Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0      vegliando              5        0.414424               0.264668
1     angosciose              5        0.364619               0.052553
2          dormì              3        0.372833               0.228062
3         veglia              1        0.402356               0.568751
4           menò              1        0.387132               0.088307
5     persuasero              1        0.386371               0.030921
6     giornodopo              1        0.385488               0.080552
7        cessata              1        0.385215               0.385936
8     sotterfugi              1        0.384204               0.367795
9        orrendi              1        0.383641               0.572785
10   raccontarne              1        0.354532               0.597044
11      divisare              1        0.352149               0.066943
12  pochiistanti              1        0.3

            Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0      tardanotte              4        0.471404               0.182487
1          aurora              3        0.488004               0.606007
2         pioggia              1        0.545387               0.311043
3          serena              1        0.537485               0.176855
4        notturno              2        0.490585               0.151483
5         festivo              1        0.524005               0.000000
6         squilla              1        0.522312               0.133091
7           lampa              1        0.521735               0.348880
8           queta              1        0.520303               0.371640
9         azzurro              5        0.445045               0.853192
10       tramonto              4        0.434470               0.091260
11          lepri              1        0.465512               0.837603
12     vegliavano              4        0.438488               0

          Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0        giorno              3        0.352122               0.793198
1      sospirar              4        0.341227               0.127889
2         serri              1        0.377352               0.069012
3          luni              2        0.350631               0.279174
4     tenebrosa              5        0.340613               0.266379
5        dormir              2        0.340044               0.797588
6        dimane              1        0.364361               0.128391
7     alloggiar              1        0.364079               0.418724
8        mutata              1        0.362615               0.047254
9          sera              1        0.362245               0.184731
10      sgombra              4        0.336807               0.606903
11     chiudere              3        0.331088               0.006200
12     seguente              4        0.336216               0.233258
13    oscurarsi     

            Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0        profonda              5        0.444494               1.000000
1            cupa              4        0.425587               0.607485
2      nolasciami              4        0.433986               0.899954
3      crocifisso              4        0.434141               0.035083
4      addormentò              1        0.497424               0.404817
5       infernale              1        0.495100               0.337253
6           negre              3        0.425926               0.474459
7      lentamente              2        0.455644               0.403424
8   apparecchiato              1        0.485377               0.980699
9           ansio              2        0.450159               0.093746
10      coricarsi              1        0.425755               0.224908
11        seguìta              1        0.421140               0.653032
12     crocefisso              1        0.417619               0

In [183]:
for autore in lista_autori_cade:
    try:
        print("###" + autore + "###")
        df_autore = similar_words_per_topos("sera", 5, 10, autore)
        print(df_autore[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + autore)

###CADE_Alessandro Manzoni_cade###
           Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0          comte              1        0.447558               0.439986
1        bientôt              5        0.419243               0.284202
2         partir              1        0.443724               0.079677
3        sabbato              1        0.443011               0.682645
4           dame              1        0.435197               0.519385
5    passeggiata              1        0.433411               0.498888
6        finisse              1        0.429495               0.000000
7          fanny              1        0.429042               1.000000
8         averti              1        0.428861               0.790194
9     dopopranzo              1        0.428800               0.681607
10     heureuxde              4        0.408418               0.365400
11          jour              1        0.396400               0.542500
12       espérer              2        0.3

         Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0      mattina              5        0.467193               0.120929
1   mezzanotte              5        0.464970               0.519421
2      arrivai              3        0.458791               0.225569
3       lunedì              2        0.489904               0.128780
4       natale              1        0.506056               0.000000
5         hora              2        0.463088               0.025854
6     pranzare              2        0.460135               0.442061
7    vegliando              2        0.464995               0.065812
8   dopopranzo              3        0.451183               0.103280
9     ierisera              1        0.498669               0.144133
10      trovan              4        0.443291               0.563113
11    avemaria              3        0.420372               0.924885
12      rividi              3        0.433172               0.835764
13    malferma              1     

             Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0           matina              5        0.452405               0.678524
1             luni              5        0.443832               0.000000
2      frequentata              5        0.456030               0.922279
3        alloggiar              2        0.451527               0.265476
4          vespero              2        0.445270               1.000000
5         calabria              1        0.485501               0.227858
6         partirsi              1        0.480999               0.149978
7         tristano              1        0.480550               0.721137
8           habito              1        0.480428               0.006734
9        aspettato              1        0.477287               0.952004
10     ondeggiando              4        0.412556               0.026414
11          matino              4        0.406520               0.020445
12       damigelle              3        0.395670  

           Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0         luglio              5        0.568171               1.000000
1   collieuganei              3        0.540418               0.019079
2          seppi              5        0.563745               0.277129
3     passopasso              2        0.602807               0.458277
4          tornò              3        0.563341               0.178351
5         dueore              5        0.541580               0.268532
6     dìseguente              3        0.542055               0.406223
7          scese              5        0.535414               0.465194
8           andò              1        0.631411               0.468022
9       scendeva              2        0.584846               0.623501
10       dilegua              1        0.531675               0.062322
11        arrivo              2        0.509991               0.004599
12     coricarsi              2        0.508547               0.011343
13   c

### Altre parole correlate:

In [184]:
for autore in lista_autori_cade:
    try:
        print("###" + autore + "###")
        df_autore = similar_words_per_topos("tenebre", 5, 10, autore)
        print(df_autore[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + autore)

###CADE_Alessandro Manzoni_cade###
               Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0         zittizitti              5        0.559871               0.933347
1           chiarore              1        0.643262               0.871683
2         stanzaccia              2        0.570396               1.000000
3            abbaino              1        0.629700               0.111375
4              larve              1        0.622730               0.284185
5           solitari              4        0.533355               0.190785
6            insonni              5        0.533992               0.301730
7              nembo              2        0.543311               0.148336
8           ascoltai              1        0.617154               0.091535
9            recinti              5        0.546358               0.462963
10          giacenti              4        0.501186               0.899089
11           usciron              4        0.485346              

           Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0        deserte              5        0.694691               0.245492
1   circondavano              5        0.703493               0.229745
2          dense              5        0.695079               0.858088
3           mute              5        0.664836               0.815337
4         scende              3        0.642008               0.813365
5          imago              1        0.731422               0.926706
6        ridenti              1        0.723260               0.000000
7         sorgea              1        0.720101               0.178794
8         erbosi              1        0.716997               1.000000
9           polo              1        0.715623               0.661666
10         astro              2        0.582930               0.280311
11        ohciel              4        0.589783               0.265459
12       scolora              2        0.599113               0.420611
13    

            Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0         chiaror              5        0.624139               0.675856
1          immota              1        0.738583               0.000000
2       tenebroso              5        0.619452               0.400643
3         calante              1        0.731901               0.252299
4     inghiottito              4        0.625200               0.345408
5         sprazzo              1        0.725112               0.400169
6     qualchefilo              2        0.638550               0.966888
7       allargava              2        0.673167               0.432921
8   balconeaperto              4        0.606478               0.009552
9        luminose              1        0.720861               1.000000
10       vegliano              1        0.649903               0.438178
11      brulichío              2        0.617530               0.912183
12          masse              1        0.635826               0

In [185]:
for autore in lista_autori_cade:
    try:
        print("###" + autore + "###")
        df_autore = similar_words_per_topos("ombra", 5, 10, autore)
        print(df_autore[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + autore)

###CADE_Alessandro Manzoni_cade###
              Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0           vagante              5        0.539568               0.122170
1       personaviva              5        0.518167               0.303011
2         avvedesse              2        0.551702               0.771623
3          scostare              1        0.595387               0.483993
4           scenata              2        0.518089               0.140578
5             pesta              1        0.593231               0.169508
6        languivano              2        0.548979               0.009956
7           elconde              5        0.508934               0.918860
8            crollo              1        0.582497               0.932611
9        consonanza              1        0.579866               0.285767
10    illuminazione              1        0.508224               0.548046
11  moltaattenzione              1        0.506645               0.544333
12 

          Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0        nebbia              4        0.502360               0.992798
1         landa              5        0.513215               0.184107
2       piaggia              2        0.564117               0.134431
3         lampa              1        0.623324               0.445038
4       azzurro              1        0.621902               0.094025
5         spene              1        0.620911               0.040831
6        serena              1        0.619438               0.067068
7         imago              1        0.618434               0.963027
8        doglia              1        0.616025               0.398531
9         bruna              3        0.513762               0.975230
10      inferme              1        0.506304               0.000000
11  notteoscura              2        0.476903               0.407261
12       dubbia              1        0.504581               1.000000
13       scuoti     

           Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0      parolette              2        0.653746               0.985062
1        fiorite              3        0.665230               0.509524
2       fioretti              3        0.651021               0.343706
3         ruvida              1        0.748776               0.294869
4         membro              2        0.668283               0.477103
5          anelo              1        0.745356               0.000000
6        diserto              1        0.743055               0.476751
7   intempestiva              1        0.740416               0.293195
8          trite              1        0.740140               0.098305
9       crescono              3        0.628978               0.975012
10          atro              2        0.598517               0.313104
11     lucertola              1        0.640520               0.573027
12        argute              1        0.636482               0.635088
13    

           Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0          colle              5        0.698992               0.244384
1          fosca              4        0.695572               0.000000
2      travedere              5        0.678305               1.000000
3    ondeggianti              5        0.686274               0.250280
4           cala              1        0.766530               0.658037
5        guatava              1        0.766487               0.402710
6           cupi              4        0.649012               0.404970
7          densa              3        0.679971               0.561725
8         soglie              1        0.764407               0.271259
9        teschio              1        0.763607               0.640717
10       manderà              3        0.649161               0.157718
11   cappelletta              3        0.618461               0.999786
12    silenziosa              1        0.652054               0.113452
13    

### TOPOS: FORTUNA

In [186]:
for autore in lista_autori_cade:
    try:
        print("###" + autore + "###")
        df_autore = similar_words_per_topos("fortuna", 5, 10, autore)
        print(df_autore[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + autore)

###CADE_Alessandro Manzoni_cade###
             Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0           cercai              1        0.476217               0.000000
1   brevesoggiorno              1        0.476195               0.299841
2          stimola              2        0.437031               0.961028
3          goderne              5        0.402085               0.280271
4       approfitto              1        0.470955               0.021082
5           auguro              1        0.467486               0.103444
6         figliola              1        0.464355               0.935329
7          copioso              1        0.463059               0.300209
8      compiacermi              1        0.462792               0.999838
9        invidiare              1        0.461734               1.000000
10          osiamo              4        0.367533               0.900553
11    approfittato              4        0.381697               0.332349
12     dimostrar

            Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0        ricevuti              5        0.391977               0.876019
1       riponendo              3        0.376821               0.920984
2    inseparabile              5        0.375909               1.000000
3         attacco              1        0.440298               0.889841
4            papi              1        0.434319               0.196226
5            nolo              1        0.433530               0.351184
6     arditissimo              1        0.430454               0.175655
7      comandando              1        0.426574               0.339118
8     altaimpresa              1        0.424852               0.199440
9       intrepido              1        0.424228               0.417836
10        coteste              4        0.359468               0.158742
11         spargi              4        0.368930               0.483151
12     ringraziar              4        0.370239               0

               Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0   irreparabilmente              5        0.451940               0.236689
1          clientela              3        0.457812               0.100564
2        inaspettata              4        0.433274               0.473500
3       conquistarsi              1        0.515156               0.882340
4         sciagurato              2        0.439343               0.613704
5             merito              2        0.469182               1.000000
6          distrarsi              4        0.421542               0.369369
7            indizii              1        0.502614               0.158386
8              sorte              1        0.502166               0.067455
9           bastante              1        0.497690               0.356581
10             nelli              4        0.399482               0.162298
11           avvezza              2        0.437000               0.448404
12       maltrattata     

             Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0      altafortuna              1        0.365999               0.039430
1       ingiuriosa              3        0.332196               1.000000
2       reafortuna              1        0.361686               0.252166
3         contenda              3        0.340291               0.214482
4            sorte              2        0.333561               0.431986
5         flagella              1        0.345313               0.516998
6        favorisca              5        0.348781               0.381312
7          incolpa              1        0.339816               0.676518
8          destina              1        0.333069               0.611359
9            armar              5        0.326195               0.508082
10         seconda              4        0.351297               0.135445
11          arride              1        0.324190               0.364907
12  riconoscimento              3        0.329180  

### TOPOS: NOIA

In [187]:
for autore in lista_autori_cade:
    try:
        print("###" + autore + "###")
        df_autore = similar_words_per_topos("noia", 5, 10, autore)
        print(df_autore[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + autore)

###CADE_Alessandro Manzoni_cade###
            Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0       rischioso              1        0.566074               0.358954
1    costipazione              1        0.559220               0.280682
2       inoltrato              5        0.468380               0.048629
3       farglielo              2        0.501448               0.101837
4       perdonata              5        0.472785               0.959057
5     vergognarmi              1        0.550764               0.124940
6          godevo              1        0.547837               0.149261
7        sentirti              1        0.544545               0.613989
8    lungalettera              1        0.544304               0.891070
9       importuna              1        0.542805               0.861012
10  salvatichezza              4        0.486360               0.165188
11         celare              4        0.458750               0.416469
12         recava            

            Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0       monotonia              5        0.440249               0.500731
1       alleviare              4        0.445650               0.574566
2    scontentezza              5        0.441224               0.988172
3      malinconia              1        0.495587               0.165720
4           tedio              2        0.467039               0.073434
5        disgusto              1        0.494199               0.412847
6   scoraggimento              5        0.442159               0.376868
7     accoramento              3        0.436983               0.884674
8       scontento              1        0.483484               1.000000
9   infelicissima              1        0.482050               0.161775
10       tormento              4        0.437095               0.528559
11          sozze              4        0.462080               0.248250
12        scoppio              2        0.436662               0

           Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0      soggiorni              3        0.549269               0.008603
1     spiacevole              1        0.612724               0.089468
2         cresca              2        0.559641               0.948844
3      disacerba              1        0.609880               0.706499
4        potermi              2        0.551274               0.205235
5          devea              2        0.557485               0.694575
6       conforto              1        0.603472               0.984277
7           esta              5        0.524082               0.509889
8         udirne              1        0.599563               0.527199
9      ramarichi              1        0.598018               0.188729
10     ringrazii              4        0.482674               0.169469
11          fele              4        0.527213               0.105842
12       depoeti              2        0.468983               0.324880
13    

La chiave non esiste nel modelloCADE_Ugo Foscolo_cade
###CADE_Umberto Eco_cade###
                Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0             scapito              5        0.733313               0.969159
1             guatare              5        0.738013               0.970385
2            calmarsi              1        0.838354               1.000000
3           sollecitò              1        0.835710               0.340666
4               lonza              1        0.835264               0.392693
5             comperi              3        0.733187               0.505160
6             basilea              1        0.832060               0.530801
7         affievolito              1        0.831799               0.449191
8       dovutopassare              1        0.831485               0.111253
9              cugini              5        0.721292               0.076987
10          collerico              4        0.709285               0.207545
11    

### TOPOS: TEMPORALE/PIOGGIA

In [188]:
for autore in lista_autori_cade:
    try:
        print("###" + autore + "###")
        df_autore = similar_words_per_topos("temporale", 5, 10, autore)
        print(df_autore[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + autore)

###CADE_Alessandro Manzoni_cade###
           Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0        mondana              5        0.606327               0.402922
1          monco              4        0.512986               0.264455
2     improvvisa              2        0.546218               0.318351
3         guscio              2        0.553050               0.397320
4           soda              1        0.617274               0.490287
5       illumina              5        0.544449               0.982124
6       rumorosa              1        0.615943               0.000000
7   prostrazione              1        0.614672               0.208625
8     fortissima              1        0.613941               0.655500
9     ritrovarli              1        0.613041               0.609362
10       immensa              1        0.524577               0.178844
11      bretagna              2        0.480149               0.502768
12   eccitazione              1        0.5

                   Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0             innaturale              1        0.678199               0.023149
1            decadimento              4        0.582614               0.103184
2          indebolimento              1        0.672238               0.404177
3              ubbidisce              3        0.569988               0.107813
4           distruggersi              1        0.662158               0.027486
5                  germi              3        0.555518               0.440630
6                eccidio              2        0.613215               0.108602
7               primario              1        0.655348               0.000000
8         trasformazione              1        0.654315               0.320481
9          felicitàumana              1        0.648220               0.428973
10             dissipata              1        0.580586               0.507477
11           ammissibile              1        0.569

             Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0            segue              5        0.748957               0.448298
1    irrefrenabile              4        0.734018               0.253434
2          viscere              1        0.851169               0.188880
3    eventualmente              1        0.845346               0.000000
4        estenuato              1        0.841306               0.294750
5          tremare              1        0.841167               0.950940
6         scroscio              2        0.790009               0.971033
7       passassero              1        0.837773               0.047446
8       sterminati              1        0.836534               0.282340
9          tizzone              1        0.835850               0.315502
10         orrendo              2        0.724519               0.417270
11      esasperato              3        0.709386               0.370024
12        repressa              4        0.707623  

La chiave non esiste nel modelloCADE_Torquato Tasso_cade
###CADE_Ugo Foscolo_cade###
La chiave non esiste nel modelloCADE_Ugo Foscolo_cade
###CADE_Umberto Eco_cade###
            Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0         dominio              4        0.678673               0.511248
1   giurisdizione              2        0.724914               0.184054
2       assumesse              5        0.666288               0.078276
3        prosapia              3        0.647204               0.296924
4         mondano              1        0.747489               0.929272
5         governo              3        0.666526               0.067473
6        signoria              4        0.635482               0.585790
7     coseterrene              1        0.735738               0.389367
8       giuridico              1        0.734863               0.326293
9       ricchezza              1        0.726252               0.924003
10    consegnando              3        0

In [189]:
for autore in lista_autori_cade:
    try:
        print("###" + autore + "###")
        df_autore = similar_words_per_topos("pioggia", 5, 10, autore)
        print(df_autore[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + autore)

###CADE_Alessandro Manzoni_cade###
           Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0         zefiro              5        0.591217               0.416247
1         rotaie              5        0.591748               1.000000
2           menò              5        0.571010               0.135536
3        incolta              2        0.608689               0.725646
4      rigagnoli              5        0.577560               0.201581
5     brevissimo              1        0.625452               0.939625
6          arida              4        0.531279               0.479371
7        solcata              5        0.556169               0.896096
8   tresettimane              1        0.617696               0.000000
9         dorata              1        0.615712               0.662532
10       diluvio              4        0.581192               0.703133
11       sassosa              3        0.519530               0.791081
12       verzura              2        0.5

           Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0         macera              5        0.690940               0.356625
1       grandine              2        0.685438               0.445560
2          rompo              4        0.622262               0.486087
3       arsiccia              5        0.630984               0.182705
4         supini              1        0.704362               0.238541
5         piovea              4        0.627807               0.951634
6         fiacca              1        0.698026               0.955628
7         fetido              1        0.697456               0.071203
8         tafani              1        0.696355               0.934652
9       fracasso              1        0.695031               0.867463
10       schermo              1        0.643809               0.161526
11  abbiamveduto              2        0.612499               0.906002
12        bufera              4        0.595639               0.494926
13    

           Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0       scirocco              2        0.667392               0.292747
1        cascate              5        0.641569               0.998046
2        arietta              2        0.669271               0.325533
3        tiepida              2        0.669528               0.869420
4          calde              2        0.652380               0.787098
5     minacciava              5        0.632896               0.226814
6     luccicante              4        0.604009               0.546747
7         laguna              5        0.596546               0.224270
8          colme              5        0.610005               0.000000
9       torrenti              2        0.610186               0.444257
10       rasente              1        0.609258               0.050611
11  certimomenti              3        0.567990               0.501087
12      annerite              3        0.576649               0.721055
13    

### TOPOS: GIOVINEZZA

In [190]:
for autore in lista_autori_cade:
    try:
        print("###" + autore + "###")
        df_autore = similar_words_per_topos("giovinezza", 5, 10, autore)
        print(df_autore[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + autore)

###CADE_Alessandro Manzoni_cade###
             Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0        trascorsa              5        0.673990               0.167680
1        offuscata              5        0.579962               0.245607
2           velata              3        0.598041               0.249710
3           senile              2        0.619464               0.000000
4       struggersi              1        0.674510               0.310803
5       vecchiezza              2        0.573246               0.126209
6           focosa              3        0.586853               0.414827
7         virilità              1        0.653916               0.564763
8           matura              2        0.587386               0.312871
9         sepolcro              1        0.649622               0.353351
10         pubertà              4        0.564871               0.400211
11        granpena              2        0.544274               0.567411
12    frontesere

             Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0       rimarranno              2        0.672437               0.559316
1            rompi              1        0.734148               0.100827
2           canute              1        0.723716               0.955333
3             sudo              1        0.722640               0.216462
4     sperimentata              4        0.615613               0.115748
5             altr              3        0.631224               0.929812
6          dettava              1        0.717755               0.082378
7        seguiterà              1        0.715909               0.342818
8         lanugine              5        0.614551               0.080774
9            provo              3        0.585575               0.487927
10          filati              4        0.580660               0.000000
11       tribolati              1        0.614109               0.119096
12         viluppi              1        0.612445  

             Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0      spensierata              5        0.569422               0.160909
1         sfiorita              5        0.609077               0.454273
2         gioventù              1        0.625358               0.155111
3       momentanei              1        0.621531               0.075202
4           illusa              5        0.574793               0.000000
5       soavissima              1        0.612914               0.093801
6        intessuto              2        0.576255               0.922219
7          gettava              1        0.612629               1.000000
8       ultimianni              2        0.548210               0.033801
9          scaccia              1        0.611864               0.005910
10      suolessere              2        0.519667               0.691021
11     compiaciuta              1        0.536048               0.086805
12        rivelata              2        0.514863  

           Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0        segnare              5        0.780598               0.559310
1      passarono              5        0.767043               0.542512
2       giungono              5        0.772205               0.994852
3          lenti              5        0.744829               0.052900
4        normale              2        0.739973               0.988328
5     stracciato              1        0.830447               0.201594
6          pieni              1        0.830295               0.621550
7      affettata              1        0.829050               0.785496
8        vigilie              1        0.828362               0.524190
9   dileguandosi              1        0.827278               0.684672
10    forteanimo              1        0.727690               0.530274
11  abbandonarla              1        0.710791               0.666785
12  accompagnata              1        0.706230               0.766484
13    

In [191]:
for autore in lista_autori_cade:
    try:
        print("###" + autore + "###")
        df_autore = similar_words_per_topos("giovane", 5, 10, autore)
        print(df_autore[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + autore)

###CADE_Alessandro Manzoni_cade###
                   Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0                giovine              5        0.774794               0.114906
1                 forese              2        0.456937               0.061678
2               sposarlo              4        0.430824               0.138467
3            confratello              5        0.427111               0.204908
4               timorato              5        0.417311               0.212373
5           bravogiovine              5        0.417603               0.071686
6                sposare              4        0.416835               1.000000
7                educato              1        0.453924               0.041835
8                ragazza              1        0.452277               0.178008
9               pacifico              3        0.417778               0.115339
10             invaghito              4        0.443068               0.083953
11         povera

                Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0                lisa              1        0.410370               0.632908
1           gagliarda              5        0.356766               0.245792
2   bellissimagiovane              5        0.379477               0.631639
3            beltramo              2        0.374273               0.569596
4              marita              1        0.383729               0.204369
5           attempato              1        0.379583               0.631776
6           cavaliere              1        0.379488               0.391055
7            donzella              3        0.351656               0.052689
8        bellagiovane              4        0.347117               0.299908
9            scudiere              1        0.374197               0.057555
10        somiglianza              4        0.370485               0.097744
11         primavista              1        0.350658               0.360846
12          

           Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0         valido              3        0.415567               0.219732
1   giovanissimo              4        0.408321               0.785014
2          motta              1        0.480442               0.144576
3    vivacissima              1        0.471526               0.146950
4     governante              2        0.407039               0.806882
5   diciottoanni              1        0.467791               0.129348
6         teresa              2        0.410179               0.910126
7     coraggiosa              1        0.453258               0.036231
8        anziano              1        0.450180               0.109890
9          liceo              1        0.447959               0.094546
10       giovine              4        0.387123               0.487632
11      ingegner              1        0.380793               0.337035
12        taddei              1        0.374120               0.478526
13    

           Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0     cortigiano              5        0.483775               0.520747
1    benedettino              2        0.547168               0.474826
2        otranto              4        0.508300               0.428251
3       alludeva              3        0.482872               0.179774
4       affamato              2        0.497980               0.821891
5       vigoroso              1        0.576260               0.987989
6       commosso              1        0.574298               0.100572
7          mangi              5        0.488804               0.433779
8        dolente              1        0.569822               0.240713
9     lussurioso              3        0.509665               0.545605
10     dilettava              1        0.502040               0.960585
11    inconsueto              1        0.500933               0.037046
12    fingendosi              1        0.490827               0.185778
13    

### TOPOS: BACIO

In [192]:
for autore in lista_autori_cade:
    try:
        print("###" + autore + "###")
        df_autore = similar_words_per_topos("bacio", 5, 10, autore)
        print(df_autore[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + autore)

###CADE_Alessandro Manzoni_cade###
               Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0           giorgino              5        0.638675               0.990442
1     strettostretto              5        0.605253               0.743084
2            stringo              5        0.608740               0.141576
3        abbracciami              4        0.631869               0.213194
4           salutami              5        0.597930               0.333994
5             zietta              1        0.667737               0.032052
6       strettissimo              1        0.666928               0.669993
7          abbraccia              1        0.666402               0.791833
8         secretario              1        0.665581               0.197078
9      cordialissimo              2        0.621665               0.000000
10        trebambini              3        0.582705               0.019987
11       amantissimo              4        0.574758              

           Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0      diffidare              5        0.847758               0.101400
1         impone              1        0.899068               0.197766
2          punse              1        0.890206               0.539545
3        schiude              1        0.886541               0.937866
4      aspettata              1        0.885368               0.340621
5       casoraro              1        0.884227               0.932689
6     ricondotto              1        0.883937               0.541767
7       metafora              1        0.882287               0.045546
8     constatare              1        0.880978               0.917955
9         stoico              1        0.879774               0.767292
10       lusinga              4        0.803032               0.571902
11    esercitato              1        0.804675               0.237789
12      avvilito              3        0.753679               1.000000
13    

           Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0        dormite              5        0.685561               0.259899
1   lasciandogli              3        0.699693               0.435947
2   polpastrelli              1        0.768172               0.252181
3     dondolando              3        0.693524               0.511385
4         grattò              1        0.765721               0.301723
5       sognando              4        0.668461               0.267964
6      mozzicone              1        0.764263               0.044355
7        strappo              1        0.760812               0.947319
8        guercio              2        0.692156               0.220483
9    chiacchiera              1        0.758275               0.000000
10    santommaso              1        0.685389               0.602661
11     ammazzata              2        0.662204               0.560272
12   spingendolo              3        0.651815               0.330023
13  st

            Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0        riponeva              5        0.729063               0.088774
1           botta              1        0.829540               0.305309
2           colse              1        0.825283               0.540260
3            noce              2        0.783530               0.192442
4       accettava              2        0.747237               0.955490
5         rimessa              1        0.822726               0.025363
6     raddoppiato              1        0.822600               0.008370
7           turno              1        0.822193               0.952452
8         allungò              1        0.821571               0.069252
9          baleno              1        0.821028               1.000000
10         volate              3        0.692765               0.306283
11       marciare              1        0.740173               0.976221
12       tastiera              1        0.738970               0

### TOPOS: LUNA

In [193]:
for autore in lista_autori_cade:
    try:
        print("###" + autore + "###")
        df_autore = similar_words_per_topos("luna", 5, 10, autore)
        print(df_autore[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + autore)

###CADE_Alessandro Manzoni_cade###
          Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0       pallida              5        0.611673               0.929983
1    specchiava              5        0.656998               0.359852
2        giamai              5        0.640654               0.094094
3      illuminò              5        0.616396               0.337190
4        raggio              3        0.613273               0.960234
5    illuminava              5        0.620881               0.981515
6        dorata              1        0.655055               0.844512
7        dirupo              1        0.652818               0.656408
8         bruna              1        0.649638               0.613748
9   rischiarato              5        0.619399               0.568815
10      diafano              3        0.587325               0.584033
11      calante              4        0.589707               0.642308
12    tremolava              2        0.581207         

         Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0    ritondità              5        0.555890               0.938805
1      eclissi              5        0.558112               0.000000
2        lucea              4        0.513777               0.104167
3      cornuta              5        0.499418               0.180880
4       oscurò              3        0.513287               0.315250
5     salivano              1        0.569594               0.465000
6    emisperio              1        0.567188               0.117044
7       ariete              1        0.561567               0.912460
8      pianeta              1        0.556932               0.981652
9      oriente              1        0.556405               0.153386
10  cilestrina              4        0.479775               0.061857
11   chiudersi              4        0.462150               0.574467
12      lunari              3        0.462835               0.186100
13  certipunti              3     

           Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0       squarcio              5        0.580455               0.974540
1        umidità              3        0.608905               0.313401
2       spargeva              5        0.600892               0.000000
3         nuvola              5        0.596904               0.519884
4         indaco              2        0.628343               0.182456
5   distinguendo              5        0.582790               0.470251
6         incisa              4        0.590104               1.000000
7         fiamma              1        0.682867               0.508967
8    cristallina              5        0.592166               0.711381
9      accecante              1        0.678057               0.544965
10     splendeva              4        0.554558               0.008260
11      caligine              3        0.553159               0.265382
12      tramonto              1        0.565389               0.566070
13  so

### TOPOS: SILENZIO

In [194]:
for autore in lista_autori_cade:
    try:
        print("###" + autore + "###")
        df_autore = similar_words_per_topos("silenzio", 5, 10, autore)
        print(df_autore[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + autore)

###CADE_Alessandro Manzoni_cade###
            Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0          trotto              5        0.389760               0.008583
1           ruppe              3        0.407393               0.398654
2         mezzani              5        0.404901               0.967826
3      esacerbato              5        0.368943               0.869263
4     camminarono              5        0.405219               0.430732
5      dispettoso              1        0.398562               0.963117
6         mistero              1        0.398164               0.863374
7          taceva              3        0.379207               0.651140
8        tacevano              1        0.391966               0.216848
9         novizii              1        0.383830               0.258503
10         opposi              1        0.357310               0.444486
11       numerare              1        0.354496               0.317035
12        serbava            

            Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0   lungosilenzio              3        0.473366               0.884532
1        tardanza              3        0.447736               0.067563
2       lamentava              4        0.416129               0.296534
3         scusate              4        0.424832               0.000000
4     primigiorni              1        0.492823               0.085130
5       viaggetto              1        0.487775               0.146350
6   sinistramente              5        0.406603               0.112225
7        accresca              1        0.478890               0.123068
8      ognilimite              1        0.477845               0.364405
9           scusa              1        0.475142               0.838754
10    sconoscenza              1        0.429665               0.875873
11          rompi              4        0.419735               1.000000
12         sinché              2        0.389461               0

             Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0      allontanato              1        0.607700               1.000000
1          regnare              2        0.551094               0.939655
2       domandollo              1        0.601127               0.434531
3       passolento              1        0.597586               0.020338
4             arli              1        0.595888               0.021796
5             molo              1        0.591821               0.006237
6       discorreva              3        0.493058               0.006245
7             lido              1        0.589032               0.147130
8            fermò              1        0.588313               0.414319
9        incontrar              5        0.484773               0.236241
10       prendesse              2        0.466685               0.266481
11         errante              1        0.515094               0.226905
12        inciampo              2        0.468121  

              Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0              citò              4        0.525636               0.382574
1             colmo              1        0.601758               0.641060
2             iddii              1        0.599544               0.981950
3            rompea              2        0.559608               0.556862
4       capannuccia              1        0.598619               0.562227
5              apro              2        0.539344               1.000000
6             lasci              1        0.597814               0.214270
7           seguita              5        0.507665               0.552450
8             duolo              1        0.595162               0.325568
9               rio              3        0.505553               0.962065
10          affanno              4        0.494398               0.254092
11            mesto              4        0.488689               0.987266
12           chiudo              1    

### TOPOS: AMICIZIA

In [195]:
for autore in lista_autori_cade:
    try:
        print("###" + autore + "###")
        df_autore = similar_words_per_topos("amicizia", 5, 10, autore)
        print(df_autore[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + autore)

###CADE_Alessandro Manzoni_cade###
                  Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0          inalterabile              5        0.504741               0.335353
1              conservo              5        0.491196               0.618307
2         osoaggiungere              1        0.595918               0.199735
3                 onora              4        0.480440               0.028668
4          instancabile              1        0.576046               0.089937
5             altastima              2        0.525982               0.296769
6              gradisci              2        0.489531               0.428453
7      preziosaamicizia              3        0.491773               0.096813
8       affettuosissima              4        0.474138               0.056407
9                    ri              1        0.564312               0.081602
10             pregiato              1        0.481005               0.419365
11         riconoscente      

              Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0       conservarmi              5        0.489781               1.000000
1        concedermi              5        0.539029               0.906344
2      riconoscenza              2        0.487615               0.888680
3         affezione              1        0.561276               0.850842
4      obbligazione              3        0.485938               0.022878
5          professo              5        0.463895               0.520651
6   vivagratitudine              3        0.494181               0.299725
7       benevolenza              1        0.547307               0.172136
8        comandarmi              1        0.544673               0.440123
9       schiettezza              1        0.543452               0.208715
10         cordiale              2        0.456830               0.494881
11     potetevedere              4        0.444790               0.141722
12         proteste              2    

                  Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0              puòesser              3        0.614099               0.045318
1            incurabile              5        0.575620               0.190858
2              chiamami              1        0.711675               0.000000
3               provedi              2        0.625838               1.000000
4             concedere              1        0.703405               0.965633
5                  fulc              1        0.702959               0.159229
6              dehvieni              1        0.700472               0.376093
7               ripudio              1        0.695693               0.953444
8              ignobile              1        0.695172               0.228187
9                toleri              2        0.644826               0.233090
10              veldirò              1        0.612190               0.313296
11              pensaci              1        0.595825          

            Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0        chiamare              5        0.591467               0.142665
1       compiacer              1        0.701535               0.320970
2           giovi              3        0.603258               0.971215
3     lungoandare              1        0.700242               0.113780
4        imputare              1        0.698971               0.465527
5          vivere              1        0.698842               0.974948
6      falsissima              1        0.697125               0.525449
7    cittadinanza              1        0.696376               1.000000
8   attribuiscono              1        0.695607               0.051687
9        servirla              1        0.695189               0.451536
10       servirvi              4        0.558759               0.145763
11         comodo              1        0.603807               0.340812
12      affezione              2        0.561698               0

In [196]:
for autore in lista_autori_cade:
    try:
        print("###" + autore + "###")
        df_autore = similar_words_per_topos("amico", 5, 10, autore)
        print(df_autore[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + autore)

###CADE_Alessandro Manzoni_cade###
              Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0          coetaneo              5        0.428964               0.000000
1        intrinseco              1        0.440196               0.155108
2          professa              2        0.407966               0.179824
3      raccomanderò              2        0.411047               0.350297
4              masi              5        0.421902               0.841943
5   giacomobeccaria              5        0.410008               0.860576
6          giragira              4        0.405715               0.763468
7             cioni              1        0.427463               0.129749
8            pregia              1        0.422393               0.390731
9           cognato              1        0.421142               0.201917
10     dilettissimo              4        0.391116               0.004311
11        seccatore              2        0.383917               0.625261
12 

                   Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0             unicoamico              5        0.485778               0.324060
1         signoravvocato              5        0.476251               0.000000
2            signorconte              2        0.465245               0.141720
3           stimatissimo              1        0.497429               0.157554
4                sincero              2        0.448814               0.471211
5         addiocarissimo              5        0.436192               0.422826
6             credendomi              2        0.449523               0.069597
7   veneratissimosignore              5        0.466993               0.087409
8             rispettoso              1        0.482860               0.099707
9        giacomoleopardi              2        0.445140               0.839187
10               seguirò              4        0.422416               0.171999
11            affettuoso              3        0.406

             Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0         benivolo              5        0.519789               0.248053
1       guadagnare              1        0.590922               0.398118
2       desideroso              4        0.477675               0.310449
3          capital              4        0.475787               0.000000
4         ignobile              1        0.583084               0.514486
5            avido              2        0.498391               0.626761
6          scolaro              3        0.500429               0.395879
7          ricordi              1        0.570478               0.215703
8          tradito              1        0.566960               0.161515
9           tenevo              1        0.563809               0.405784
10         parente              1        0.479371               0.230585
11             ama              1        0.476214               0.166742
12         amatore              1        0.459506  

            Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0   infelicissimo              5        0.563640               0.213282
1    dimenticarsi              5        0.541509               0.357755
2       piangente              1        0.661814               0.495702
3          misero              5        0.538836               0.365689
4          fedele              5        0.555014               0.386776
5         aspetta              3        0.562879               0.009207
6          invoca              3        0.545617               0.455615
7    ringraziarti              3        0.545511               0.499582
8          labbro              1        0.638354               0.407715
9             ami              5        0.535816               0.880417
10       rispondi              1        0.543184               0.373150
11         deluso              1        0.537372               0.218019
12        accorse              3        0.507473               1

### TOPOS: SOLITUDINE

In [197]:
for autore in lista_autori_cade:
    try:
        print("###" + autore + "###")
        df_autore = similar_words_per_topos("solitudine", 5, 10, autore)
        print(df_autore[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + autore)

###CADE_Alessandro Manzoni_cade###
              Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0           vagante              5        0.494285               0.066246
1     frequentatori              5        0.530678               0.111671
2       tristissima              5        0.480343               0.316066
3          febbrile              1        0.579032               0.987438
4          mestizia              5        0.497387               1.000000
5          desiderò              1        0.576989               0.702647
6        stanchezza              1        0.570284               0.000000
7       imbalordito              5        0.489835               0.076062
8         patimento              1        0.561448               0.451476
9       trascorrere              1        0.560943               0.237943
10         restarne              1        0.489758               0.497918
11      incontrando              4        0.455111               0.095343
12 

             Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0           merope              5        0.874139               0.991094
1   rappresentarsi              5        0.866983               0.802593
2          effetti              5        0.869529               0.687619
3          amabile              5        0.852155               0.456645
4           attori              5        0.830696               0.895679
5           platea              5        0.797129               0.489103
6          sincera              1        0.889000               0.015357
7         addunque              1        0.887338               0.972482
8      riflessioni              1        0.887074               0.920379
9       fortemente              1        0.883864               0.252984
10      eccellenti              4        0.787586               0.000000
11          esiodo              1        0.793644               0.022023
12        proviamo              3        0.749262  

             Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0      manifestava              5        0.578181               0.362940
1         restasse              5        0.569713               0.199747
2      significata              4        0.586319               0.208661
3         stupendo              1        0.687243               0.009271
4        infernale              1        0.668209               0.899817
5       innaturale              2        0.605920               0.225230
6       vecchiezza              1        0.664451               0.571972
7     potentemente              1        0.663068               0.854189
8     rinchiudersi              3        0.592683               0.053657
9   innocentemente              1        0.659540               0.017467
10     senzalimiti              2        0.594091               0.425973
11      pentimenti              3        0.554147               0.075850
12     precipitava              3        0.568699  

              Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0      dispiacevole              2        0.754108               0.028689
1            rumore              5        0.710771               0.524092
2         cagionava              3        0.686242               0.985612
3          digerire              5        0.692831               0.519725
4        pocostante              1        0.768336               0.931237
5     contravveleno              4        0.685489               0.562289
6           capello              1        0.765854               0.917515
7         selvatico              1        0.764201               0.715875
8         crescendo              1        0.756475               0.388726
9      dissipazione              2        0.719325               0.377824
10  potutoresistere              4        0.673217               0.069753
11         tensione              1        0.694165               0.501884
12       rimettermi              2    

In [198]:
for autore in lista_autori_cade:
    try:
        print("###" + autore + "###")
        df_autore = similar_words_per_topos("solitario", 5, 10, autore)
        print(df_autore[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + autore)

###CADE_Alessandro Manzoni_cade###
          Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0   scenaottava              5        0.623816               0.000000
1   incresciosa              1        0.705934               0.993021
2      amplesso              1        0.704656               0.350387
3     coperchio              5        0.604964               0.928847
4      schifoso              1        0.693476               0.167445
5         mesce              1        0.693057               0.449006
6        aspira              1        0.692895               0.060071
7        impera              1        0.689825               0.906687
8      immemore              1        0.688835               0.912091
9         velen              1        0.688534               0.371217
10      arbusto              4        0.586892               1.000000
11      insulta              1        0.592217               0.379447
12        opaco              1        0.591056         

            Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0          stuoia              2        0.681336               0.463974
1          rimoto              5        0.664937               0.205482
2       cavalcato              5        0.610049               0.131800
3     altecolonne              3        0.625785               0.047005
4         solingo              1        0.730881               0.957228
5          candia              1        0.722495               0.000000
6         oracoli              1        0.721863               0.413533
7       sollevato              3        0.607852               0.464743
8         inviati              4        0.614165               0.383719
9            varo              2        0.670062               0.448000
10       cimitero              1        0.628624               0.064296
11       laghetto              4        0.586791               0.478455
12       castagni              1        0.625935               0

              Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0        granellino              3        0.699117               0.991388
1         asciugava              1        0.804036               0.931934
2              pepe              1        0.802954               1.000000
3           affitto              1        0.801660               0.331301
4            chiodo              5        0.642470               0.502612
5          scavalcò              1        0.788658               0.414439
6          compagne              4        0.669634               0.512890
7           chiazza              3        0.666798               0.032162
8             aglio              1        0.785255               0.083785
9             vispo              1        0.783335               0.403675
10          sparare              1        0.661456               0.619746
11          pendeva              4        0.600236               0.326475
12      giardiniere              2    

### TOPOS: INFINITO

In [199]:
for autore in lista_autori_cade:
    try:
        print("###" + autore + "###")
        df_autore = similar_words_per_topos("infinito", 5, 10, autore)
        print(df_autore[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + autore)

###CADE_Alessandro Manzoni_cade###
             Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0          fisiche              1        0.784009               0.048134
1      distruggono              3        0.672062               0.971081
2       annientare              2        0.723089               0.714988
3          volerli              4        0.679321               0.215547
4           aliena              1        0.777828               0.021854
5         lodavano              1        0.776850               0.454348
6         forzando              3        0.686683               0.250896
7         nequizie              1        0.771384               0.512004
8       parlandone              1        0.770927               0.000000
9         derivino              3        0.681887               0.331088
10     compositori              1        0.679702               0.139245
11       scacciati              1        0.677429               0.522226
12        parzia

                Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0             presuma              4        0.451942               0.228018
1   desiderioinfinito              5        0.457691               0.000000
2          illimitato              5        0.463870               0.207719
3               cessa              1        0.522901               0.218508
4       nessunpiacere              1        0.511116               0.487721
5         senzalimiti              2        0.471801               0.027728
6         puòesistere              1        0.504861               1.000000
7     indefinitamente              3        0.443752               0.580688
8              amarsi              2        0.443233               0.261848
9          risultasse              5        0.423984               0.620423
10        possessione              3        0.421509               0.491059
11             amarlo              3        0.401366               0.122393
12          

              Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0          duravano              4        0.657162               0.946384
1         rivedersi              5        0.651261               0.109180
2   indimenticabili              1        0.793489               0.499593
3       lunghissimi              4        0.656724               0.009925
4             minor              1        0.786576               0.330970
5          vegliata              1        0.781851               0.005672
6   qualunquegenere              1        0.781271               0.459053
7         mantenute              1        0.780324               0.104767
8        affermarlo              1        0.779977               1.000000
9           pedanti              1        0.777212               0.247299
10       conosciuti              4        0.624883               0.457315
11      resistevano              4        0.605495               0.947761
12           pronti              4    

La chiave non esiste nel modelloCADE_Primo Levi_cade
###CADE_Torquato Tasso_cade###
                Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0           progresso              5        0.641801               0.504641
1           diminuire              5        0.560463               0.392892
2              andare              5        0.561669               0.033904
3            derivati              1        0.651709               0.417347
4         dicoadunque              3        0.553234               1.000000
5   qualsivogliaaltra              1        0.645137               0.458236
6         moltiluoghi              2        0.568796               0.184940
7              pelago              4        0.545585               0.498006
8             vaganti              1        0.635902               0.459855
9              gioire              1        0.634848               0.000000
10          dividersi              1        0.553529               0.907238
11  

# TOPOS COMPLESSI

In [41]:
lista_periodi_letterari = ['1_duecento_poetica_e_prosa Medievo', '2_dolce_stil_novo', '3_petrarchismo', 
                           '4_boccaccio_e_umanesimo', '5_manierismo_e_barocco', '6_classicismo_arcadia', 
                           '7_illuminismo_neoclassicismo', '8_romanticismo', '9_verismo', '10_decadentismo', 
                           '11_avanguardie_primo_novecento', '12_neorealismo']

lista_autori_w2v = ['Alessandro Manzoni', 'Dante Alighieri', 'Dino Buzzati', 'Francesco Petrarca', 'Gabriele D\'Annunzio', 
                    'Giacomo Leopardi', 'Giovanni Boccaccio', 'Giuseppe Parini', 'Italo Calvino', 'Italo Svevo', 
                    'Ludovico Ariosto', 'Luigi Pirandello', 'Pier Paolo Pasolini', 'Primo Levi', 'Torquato Tasso', 
                    'Ugo Foscolo', 'Umberto Eco', 'Vittorio Alfieri']

lista_periodi_letterari_cade = ['CADE_1_duecento_poetica_e_prosa Medievo_cade', 'CADE_2_dolce_stil_novo_cade', 
                                'CADE_3_petrarchismo_cade', 'CADE_4_boccaccio_e_umanesimo_cade', 
                                'CADE_5_manierismo_e_barocco_cade', 'CADE_6_classicismo_arcadia_cade', 
                                'CADE_7_illuminismo_neoclassicismo_cade', 'CADE_8_romanticismo_cade', 'CADE_9_verismo_cade',
                                'CADE_10_decadentismo_cade', 'CADE_11_avanguardie_primo_novecento_cade', 
                                'CADE_12_neorealismo_cade']

lista_autori_cade = ['CADE_Alessandro Manzoni_cade', 'CADE_Dante Alighieri_cade', 
                     'CADE_Dino Buzzati_cade', 'CADE_Francesco Petrarca_cade', 
                     'CADE_Gabriele D\'Annunzio_cade', 'CADE_Giacomo Leopardi_cade', 
                     'CADE_Giovanni Boccaccio_cade', 'CADE_Giuseppe Parini_cade', 
                     'CADE_Italo Calvino_cade', 'CADE_Italo Svevo_cade', 
                     'CADE_Ludovico Ariosto_cade', 'CADE_Luigi Pirandello_cade', 
                     'CADE_Pier Paolo Pasolini_cade', 'CADE_Primo Levi_cade', 
                     'CADE_Torquato Tasso_cade', 'CADE_Ugo Foscolo_cade', 
                     'CADE_Umberto Eco_cade', 'CADE_Vittorio Alfieri_cade']

## BIVIO

#### PERIODO LETTERARIO - W2V

In [12]:
os.chdir(path_letterario_w2v)

In [13]:
for periodo in lista_periodi_letterari:
    try:
        print("###" + periodo + "###")
        df_periodo = similar_words_per_topos("bivio", 5, 10, periodo)
        print(df_periodo[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + periodo)

###1_duecento_poetica_e_prosa Medievo###
La chiave non esiste nel modello1_duecento_poetica_e_prosa Medievo
###2_dolce_stil_novo###
La chiave non esiste nel modello2_dolce_stil_novo
###3_petrarchismo###
La chiave non esiste nel modello3_petrarchismo
###4_boccaccio_e_umanesimo###
La chiave non esiste nel modello4_boccaccio_e_umanesimo
###5_manierismo_e_barocco###
La chiave non esiste nel modello5_manierismo_e_barocco
###6_classicismo_arcadia###
              Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0               leo              1        0.988064               0.416301
1           tremesi              4        0.985377               0.504368
2           soprano              4        0.984708               0.041371
3       felicissimo              2        0.986045               0.483611
4         königsegg              1        0.985589               0.437416
5            dueore              1        0.984653               0.364397
6            iscena              1

La chiave non esiste nel modello11_avanguardie_primo_novecento
###12_neorealismo###
            Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0          treiso              5        0.887339               0.746234
1        lunapark              5        0.888143               0.673349
2       scendendo              4        0.886508               0.786077
3   duecentometri              4        0.879463               0.870689
4       affluente              5        0.882739               0.404852
5   attraversando              5        0.883587               0.111870
6       fiumicino              2        0.878587               0.393648
7        ferrovia              3        0.878659               0.592425
8        piazzale              5        0.876592               0.554693
9     divinoamore              2        0.875229               0.551294
10           auto              1        0.885389               1.000000
11      telegrafo              2        0.881528    

Nessun riscontro

## PESSIMISMO

#### PERIODO LETTERARIO - W2V

In [14]:
os.chdir(path_letterario_w2v)

In [18]:
for periodo in lista_periodi_letterari:
    try:
        print("###" + periodo + "###")
        df_periodo = similar_words_per_topos("pessimismo", 5, 10, periodo)
        print(df_periodo[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + periodo)

###1_duecento_poetica_e_prosa Medievo###
La chiave non esiste nel modello1_duecento_poetica_e_prosa Medievo
###2_dolce_stil_novo###
La chiave non esiste nel modello2_dolce_stil_novo
###3_petrarchismo###
La chiave non esiste nel modello3_petrarchismo
###4_boccaccio_e_umanesimo###
La chiave non esiste nel modello4_boccaccio_e_umanesimo
###5_manierismo_e_barocco###
La chiave non esiste nel modello5_manierismo_e_barocco
###6_classicismo_arcadia###
La chiave non esiste nel modello6_classicismo_arcadia
###7_illuminismo_neoclassicismo###
La chiave non esiste nel modello7_illuminismo_neoclassicismo
###8_romanticismo###
La chiave non esiste nel modello8_romanticismo
###9_verismo###
             Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0    pervertimento              4        0.911008               0.484002
1         parziale              5        0.915179               0.445487
2          natural              1        0.906761               0.257784
3           pruova        

In [17]:
for periodo in lista_periodi_letterari:
    try:
        print("###" + periodo + "###")
        df_periodo = similar_words_per_topos("suicidio", 5, 10, periodo)
        print(df_periodo[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + periodo)

###1_duecento_poetica_e_prosa Medievo###
La chiave non esiste nel modello1_duecento_poetica_e_prosa Medievo
###2_dolce_stil_novo###
La chiave non esiste nel modello2_dolce_stil_novo
###3_petrarchismo###
La chiave non esiste nel modello3_petrarchismo
###4_boccaccio_e_umanesimo###
La chiave non esiste nel modello4_boccaccio_e_umanesimo
###5_manierismo_e_barocco###
La chiave non esiste nel modello5_manierismo_e_barocco
###6_classicismo_arcadia###
La chiave non esiste nel modello6_classicismo_arcadia
###7_illuminismo_neoclassicismo###
La chiave non esiste nel modello7_illuminismo_neoclassicismo
###8_romanticismo###
               Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0          meritoria              4        0.821060               0.229936
1      insensibilità              4        0.823078               0.514497
2           ingenito              2        0.820810               0.165159
3              oblio              1        0.826445               0.660933
4     

              Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0      supposizione              5        0.906926               0.577637
1           fallito              3        0.894457               0.432974
2       preferibile              4        0.883819               0.346322
3         pestaggio              5        0.889984               0.318757
4        rinunciato              1        0.889592               0.609781
5        rinunziato              2        0.887223               0.619382
6        pienamente              1        0.880033               0.091555
7         proponevo              1        0.879554               0.174349
8          supporre              1        0.878565               0.360579
9          ritenuto              4        0.887889               0.137903
10     privilegiato              1        0.883954               0.000000
11            neill              2        0.885979               0.482841
12        giudicato              1    

Nessun riscontro

## LOCUS AMOENUS

#### PERIODI LETTERARI - W2V

In [19]:
os.chdir(path_letterario_w2v)

In [20]:
for periodo in lista_periodi_letterari:
    try:
        print("###" + periodo + "###")
        df_periodo = similar_words_per_topos("eden", 5, 10, periodo)
        print(df_periodo[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + periodo)

###1_duecento_poetica_e_prosa Medievo###
La chiave non esiste nel modello1_duecento_poetica_e_prosa Medievo
###2_dolce_stil_novo###
La chiave non esiste nel modello2_dolce_stil_novo
###3_petrarchismo###
La chiave non esiste nel modello3_petrarchismo
###4_boccaccio_e_umanesimo###
La chiave non esiste nel modello4_boccaccio_e_umanesimo
###5_manierismo_e_barocco###
La chiave non esiste nel modello5_manierismo_e_barocco
###6_classicismo_arcadia###
La chiave non esiste nel modello6_classicismo_arcadia
###7_illuminismo_neoclassicismo###
La chiave non esiste nel modello7_illuminismo_neoclassicismo
###8_romanticismo###
La chiave non esiste nel modello8_romanticismo
###9_verismo###
La chiave non esiste nel modello9_verismo
###10_decadentismo###
La chiave non esiste nel modello10_decadentismo
###11_avanguardie_primo_novecento###
La chiave non esiste nel modello11_avanguardie_primo_novecento
###12_neorealismo###
             Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0      costr

In [23]:
for periodo in lista_periodi_letterari:
    try:
        print("###" + periodo + "###")
        df_periodo = similar_words_per_topos("paradisoterrestre", 5, 10, periodo)
        print(df_periodo[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + periodo)

###1_duecento_poetica_e_prosa Medievo###
La chiave non esiste nel modello1_duecento_poetica_e_prosa Medievo
###2_dolce_stil_novo###
La chiave non esiste nel modello2_dolce_stil_novo
###3_petrarchismo###
La chiave non esiste nel modello3_petrarchismo
###4_boccaccio_e_umanesimo###
               Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0   chomedimostrammo              5        0.919364               1.000000
1     medesimoluogho              2        0.912974               0.000000
2      imitavirgilio              5        0.914997               0.732048
3       horatornando              3        0.917347               0.504607
4   convenientechosa              3        0.913746               0.481725
5         tracteremo              4        0.906924               0.346987
6        intenderemo              4        0.913398               0.909906
7     habbiamoveduto              3        0.905232               0.533176
8         dimostramo              4        0.

La chiave non esiste nel modello11_avanguardie_primo_novecento
###12_neorealismo###
           Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0     pndapetzim              5        0.858758               0.552748
1     diecitribù              5        0.869840               0.084694
2        lucania              5        0.840236               0.412875
3        resterà              1        0.852129               0.125664
4         ipazie              3        0.839406               0.309080
5   mediooriente              1        0.836627               0.319836
6      palestina              3        0.832175               0.000000
7       risalita              1        0.831893               0.318167
8      queipaesi              2        0.831875               0.364740
9        avvento              2        0.820230               1.000000
10      bisanzio              4        0.838018               0.438494
11       ventura              2        0.835346               0.

In [25]:
for periodo in lista_periodi_letterari:
    try:
        print("###" + periodo + "###")
        df_periodo = similar_words_per_topos("giardino", 5, 10, periodo)
        print(df_periodo[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + periodo)

###1_duecento_poetica_e_prosa Medievo###
       Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0    diversi              3        0.996990               0.483008
1      panno              1        0.995701               0.349442
2   talvolta              1        0.994592               0.517600
3      manda              1        0.993952               0.619293
4     albero              3        0.993525               0.290102
5        vai              2        0.992212               0.501257
6    làentro              1        0.992775               0.373981
7    credere              4        0.993047               0.411680
8       olio              5        0.994208               0.433036
9        ivi              2        0.992481               0.346810
10      neve              2        0.995149               1.000000
11    andava              1        0.993757               0.124488
12     petto              1        0.991845               0.327207
13    colore         

                      Words  Abs.frequency  Med.similarity  \
0              arciduchesse              5        0.979968   
1                  favorita              5        0.973353   
2                   palazzo              5        0.978372   
3                    camera              4        0.970784   
4              altezzereali              5        0.978283   
5      augustissimiregnanti              5        0.971690   
6                    sparsa              4        0.969141   
7                schönbrunn              5        0.976743   
8                  galleria              1        0.970200   
9              appartamenti              1        0.970140   
10                 marianna              2        0.973912   
11                  seguito              1        0.971637   
12                    bonno              2        0.970273   
13  serenissimearciduchesse              2        0.965719   
14             arciduchessa              1        0.971107   
15      

          Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0      ondariva              5        0.752712               0.446815
1      terrazza              5        0.743732               0.164376
2         vigna              4        0.727718               0.273382
3         parco              5        0.737039               0.700216
4       piscina              3        0.732605               0.228810
5     palazzina              4        0.726827               0.000000
6       tendine              1        0.722573               1.000000
7      terrazzo              3        0.720227               0.156821
8        chalet              1        0.716530               0.480173
9       vetrata              1        0.716048               0.685253
10        pozzo              4        0.731514               0.098274
11        prato              4        0.722360               0.596199
12    boschetto              1        0.725166               0.574282
13      fienile     

#### PERIODI LETTERARI - CADE

In [28]:
os.chdir(path_letterario_cade)

In [29]:
for periodo in lista_periodi_letterari_cade:
    try:
        print("###" + periodo + "###")
        df_periodo = similar_words_per_topos("paradisoterrestre", 5, 10, periodo)
        print(df_periodo[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + periodo)

###CADE_1_duecento_poetica_e_prosa Medievo_cade###
La chiave non esiste nel modelloCADE_1_duecento_poetica_e_prosa Medievo_cade
###CADE_2_dolce_stil_novo_cade###
           Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0        sommità              5        0.835372               0.263007
1        entraro              3        0.800809               0.709957
2          ronca              1        0.849293               0.000000
3           noli              1        0.848699               0.458164
4          colco              1        0.847373               0.427140
5   leggeramente              1        0.846563               0.406609
6       degnasti              3        0.782188               0.088119
7        bifolco              1        0.842982               0.950125
8       tremolar              1        0.842115               0.414819
9      malaspina              1        0.841942               0.984826
10      metterlo              1        0.815207          

La chiave non esiste nel modelloCADE_6_classicismo_arcadia_cade
###CADE_7_illuminismo_neoclassicismo_cade###
La chiave non esiste nel modelloCADE_7_illuminismo_neoclassicismo_cade
###CADE_8_romanticismo_cade###
           Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0          abele              5        0.671133               0.081106
1          caino              5        0.598289               1.000000
2     incontrerà              4        0.584951               0.203858
3    emigrazione              1        0.659811               0.493257
4         adonai              5        0.584169               0.134279
5       eruzione              1        0.654168               0.435050
6        sultani              2        0.614351               0.438893
7    simboleggia              1        0.643877               0.106003
8           rubi              1        0.640375               0.575536
9        esperia              1        0.639287               0.397886
10      

                Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0               gange              5        0.565825               0.565050
1        quattrofiumi              5        0.594162               0.236799
2          nestoriani              2        0.589680               0.280827
3                 noè              2        0.583806               0.459061
4           sambatyon              1        0.598310               0.237257
5         progenitori              1        0.593923               0.247637
6            bisanzio              4        0.557271               0.655711
7      isolefortunate              2        0.560114               0.595182
8              nomadi              1        0.588530               0.214309
9         promessogli              5        0.558979               0.000000
10         diecitribù              4        0.547270               0.014106
11           sacerdos              3        0.550831               0.908536
12       nuo

Ho visto che sopra la parola 'pndapetzim' è associata al paradiso terrestre nel decadentismo, provo a vedere le parole più simili ad essa negli altri periodi letterari

In [35]:
lista_periodi_letterari_cade.remove('CADE_12_neorealismo_cade')

In [36]:
for periodo in lista_periodi_letterari_cade:
        print("###" + periodo + "###")        
        df = compare_word_btw_embeddings("pndapetzim", 5, 'CADE_12_neorealismo_cade', periodo)
        print(df)

###CADE_1_duecento_poetica_e_prosa Medievo_cade###
            Words  Med.similarity
5        avessono        0.515534
22       potevano        0.488960
3      andrebbono        0.487919
2      altreterre        0.487740
1   altrecontrade        0.481129
12     difendiamo        0.477077
20           oggi        0.458024
4     anticamente        0.449020
21     perciocché        0.447647
30    volleandare        0.435928
###CADE_2_dolce_stil_novo_cade###
          Words  Med.similarity
13      godesse        0.483834
14      lascerò        0.474140
3     ascoltato        0.471644
27     sepolcri        0.469657
6   cogitazioni        0.469172
10      esperti        0.450522
32   tornassero        0.440294
18     opposita        0.429865
31      teniamo        0.426937
9      dogliosa        0.424840
###CADE_3_petrarchismo_cade###
          Words  Med.similarity
23    prendervi        0.490233
32       vicini        0.480274
16   fuggiranno        0.469361
0     accordati        0.46684

#### AUTORI: W2V

In [37]:
os.chdir(path_autori_w2v)

In [39]:
for autore in lista_autori_w2v:
    try:
        print("###" + autore + "###")
        df_autore = similar_words_per_topos("paradisoterrestre", 5, 10, autore)
        print(df_autore[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + autore)

###Alessandro Manzoni###
La chiave non esiste nel modelloAlessandro Manzoni
###Dante Alighieri###
La chiave non esiste nel modelloDante Alighieri
###Dino Buzzati###
La chiave non esiste nel modelloDino Buzzati
###Francesco Petrarca###
La chiave non esiste nel modelloFrancesco Petrarca
###Gabriele D'Annunzio###
La chiave non esiste nel modelloGabriele D'Annunzio
###Giacomo Leopardi###
La chiave non esiste nel modelloGiacomo Leopardi
###Giovanni Boccaccio###
La chiave non esiste nel modelloGiovanni Boccaccio
###Giuseppe Parini###
La chiave non esiste nel modelloGiuseppe Parini
###Italo Calvino###
La chiave non esiste nel modelloItalo Calvino
###Italo Svevo###
La chiave non esiste nel modelloItalo Svevo
###Ludovico Ariosto###
La chiave non esiste nel modelloLudovico Ariosto
###Luigi Pirandello###
La chiave non esiste nel modelloLuigi Pirandello
###Pier Paolo Pasolini###
La chiave non esiste nel modelloPier Paolo Pasolini
###Primo Levi###
La chiave non esiste nel modelloPrimo Levi
###Torqu

## ATTIMO FUGGENTE

#### PERIODI STORICI: W2V

In [42]:
os.chdir(path_letterario_w2v)

In [43]:
for periodo in lista_periodi_letterari:
    try:
        print("###" + periodo + "###")
        df_periodo = similar_words_per_topos("attimo", 5, 10, periodo)
        print(df_periodo[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + periodo)

###1_duecento_poetica_e_prosa Medievo###
La chiave non esiste nel modello1_duecento_poetica_e_prosa Medievo
###2_dolce_stil_novo###
La chiave non esiste nel modello2_dolce_stil_novo
###3_petrarchismo###
La chiave non esiste nel modello3_petrarchismo
###4_boccaccio_e_umanesimo###
La chiave non esiste nel modello4_boccaccio_e_umanesimo
###5_manierismo_e_barocco###
La chiave non esiste nel modello5_manierismo_e_barocco
###6_classicismo_arcadia###
La chiave non esiste nel modello6_classicismo_arcadia
###7_illuminismo_neoclassicismo###
La chiave non esiste nel modello7_illuminismo_neoclassicismo
###8_romanticismo###
              Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0         incontrar              4        0.889409               0.000000
1           ristava              4        0.878300               0.416660
2      raggiungerla              5        0.882127               0.402273
3         frapposto              2        0.878183               0.625355
4      poch

In [44]:
for periodo in lista_periodi_letterari:
    try:
        print("###" + periodo + "###")
        df_periodo = similar_words_per_topos("carpediem", 5, 10, periodo)
        print(df_periodo[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + periodo)

###1_duecento_poetica_e_prosa Medievo###
La chiave non esiste nel modello1_duecento_poetica_e_prosa Medievo
###2_dolce_stil_novo###
La chiave non esiste nel modello2_dolce_stil_novo
###3_petrarchismo###
La chiave non esiste nel modello3_petrarchismo
###4_boccaccio_e_umanesimo###
La chiave non esiste nel modello4_boccaccio_e_umanesimo
###5_manierismo_e_barocco###
La chiave non esiste nel modello5_manierismo_e_barocco
###6_classicismo_arcadia###
La chiave non esiste nel modello6_classicismo_arcadia
###7_illuminismo_neoclassicismo###
La chiave non esiste nel modello7_illuminismo_neoclassicismo
###8_romanticismo###
La chiave non esiste nel modello8_romanticismo
###9_verismo###
La chiave non esiste nel modello9_verismo
###10_decadentismo###
La chiave non esiste nel modello10_decadentismo
###11_avanguardie_primo_novecento###
La chiave non esiste nel modello11_avanguardie_primo_novecento
###12_neorealismo###
La chiave non esiste nel modello12_neorealismo


In [45]:
for periodo in lista_periodi_letterari:
    try:
        print("###" + periodo + "###")
        df_periodo = similar_words_per_topos("attimofuggente", 5, 10, periodo)
        print(df_periodo[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + periodo)

###1_duecento_poetica_e_prosa Medievo###
La chiave non esiste nel modello1_duecento_poetica_e_prosa Medievo
###2_dolce_stil_novo###
La chiave non esiste nel modello2_dolce_stil_novo
###3_petrarchismo###
La chiave non esiste nel modello3_petrarchismo
###4_boccaccio_e_umanesimo###
La chiave non esiste nel modello4_boccaccio_e_umanesimo
###5_manierismo_e_barocco###
La chiave non esiste nel modello5_manierismo_e_barocco
###6_classicismo_arcadia###
La chiave non esiste nel modello6_classicismo_arcadia
###7_illuminismo_neoclassicismo###
La chiave non esiste nel modello7_illuminismo_neoclassicismo
###8_romanticismo###
La chiave non esiste nel modello8_romanticismo
###9_verismo###
La chiave non esiste nel modello9_verismo
###10_decadentismo###
La chiave non esiste nel modello10_decadentismo
###11_avanguardie_primo_novecento###
La chiave non esiste nel modello11_avanguardie_primo_novecento
###12_neorealismo###
La chiave non esiste nel modello12_neorealismo


## SILENZIO

#### PERIODI STORICI: W2V

In [46]:
for periodo in lista_periodi_letterari:
    try:
        print("###" + periodo + "###")
        df_periodo = similar_words_per_topos("silenzio", 5, 10, periodo)
        print(df_periodo[['Words', 'Abs.frequency', 'Med.similarity', 'Med.similarity(norm.)']])
    except KeyError:
        print("La chiave non esiste nel modello" + periodo)

###1_duecento_poetica_e_prosa Medievo###
La chiave non esiste nel modello1_duecento_poetica_e_prosa Medievo
###2_dolce_stil_novo###
La chiave non esiste nel modello2_dolce_stil_novo
###3_petrarchismo###
La chiave non esiste nel modello3_petrarchismo
###4_boccaccio_e_umanesimo###
             Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0       grandeagio              5        0.826410               0.124988
1       fortarrigo              2        0.835030               0.511547
2        guerriera              2        0.831629               0.736168
3   fortepiangendo              4        0.824121               0.178229
4   lungadimoranza              1        0.830384               0.818670
5        veggendol              1        0.828519               0.562352
6           tofano              3        0.830539               0.370334
7         ciutazza              4        0.828758               0.306792
8          postosi              1        0.825360              

            Words  Abs.frequency  Med.similarity  Med.similarity(norm.)
0      dispettoso              5        0.621654               0.848928
1           sordo              4        0.616405               0.697358
2   dolorosamente              2        0.615846               0.542733
3    raccapriccio              3        0.609008               0.540679
4      sbalordito              2        0.607233               0.211645
5        inquieto              2        0.609842               1.000000
6         tremore              1        0.605503               0.430252
7          taceva              5        0.614821               0.313095
8      turbamento              3        0.610033               0.518938
9      interrotto              1        0.597233               0.804571
10        scoppio              2        0.615018               0.382295
11       mormorio              1        0.627443               0.472601
12       ribrezzo              2        0.619954               0